# Football Parsing Code

In [1]:
## Basic stuff
%load_ext autoreload
%autoreload
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
display(HTML("""<style>div.output_area{max-height:10000px;overflow:scroll;}</style>"""))

## Python Version
import sys
print("Python: {0}".format(sys.version))

import datetime as dt
start = dt.datetime.now()

print("Notebook Last Run Initiated: "+str(start))

Python: 3.6.6 |Anaconda custom (64-bit)| (default, Jun 28 2018, 11:07:29) 
[GCC 4.2.1 Compatible Clang 4.0.1 (tags/RELEASE_401/final)]
Notebook Last Run Initiated: 2019-03-29 20:19:04.983909


In [51]:
from os.path import join
from fsUtils import mkSubDir, setFile, isFile, removeFile, isDir
from ioUtils import getFile, saveFile
from timeUtils import clock, elapsed
from fileUtils import getBaseFilename, getBasename, getDirname
from webUtils import getWebData, getHTML
from timeUtils import printDateTime, getDateTime, addMonths
from searchUtils import findExt
from time import sleep
from random import random
import sys
import re
from datetime import timedelta



class output:
    def __init__(self):
        self.name   = "output"
        self.dirval = "/Volumes/Blue/Football"
        if not isDir(self.dirval):
            self.dirval = "/Users/tgadfort/Documents/football"


        
    def getSaveDir(self):
        return self.dirval

    
class espn:
    def __init__(self):
        self.name = "espn"
        self.baseurl = "http://www.espn.com"
        
    def getBase(self):
        return self.baseurl

In [3]:
############################################################################################################
# Game Class
############################################################################################################
class game:
    def __init__(self, gameID, date, teamA, teamB, teamAResult, teamBResult, teamAScore, teamBScore, location, extra={}):
        self.gameID = gameID
        self.date   = date
        self.teamA  = teamA
        self.teamB  = teamB
        self.teamAScore  = teamAScore
        self.teamBScore  = teamBScore
        self.teamAResult  = teamAResult
        self.teamBResult  = teamBResult
        self.location = location
        
        self.OT   = extra.get('OT')
        self.Bowl = extra.get('Bowl')

    def getWinner(self):
        if self.teamAScore > self.teamBScore:
            return self.teamA
        elif self.teamAScore < self.teamBScore:
            return self.teamB
        else:
            return "T"

        
    def getGame(self):
        retval = {"GameID": self.gameID}

        
        
############################################################################################################
# Team Class
############################################################################################################
class team:
    def __init__(self, year, teamName, teamMascot, teamID):
        self.year       = year
        self.teamName   = teamName
        self.teamMascot = teamMascot
        self.teamID     = teamID
        self.games      = []

        
    def getTeamID(self):
        return self.teamID
    
        
    def addGame(self, game):
        result = game.teamAResult
        self.games.append({"Result": result, "Game": game})

            
    def setStatistics(self):
        wins   = sum([x["Result"] == "W" for x in self.games])
        losses = sum([x["Result"] == "L" for x in self.games])
        ties   = sum([x["Result"] == "T" for x in self.games])
        ngames = len(self.games)
        if ngames != wins+losses+ties:
            raise ValueError("The sum of wins, losses, and ties does not match total number of games!")
        self.wins   = wins
        self.losses = losses
        self.ties   = ties
        self.ngames = ngames

        
    def summary(self):
        print("{0: <6}{1: <50}{2: <5}{3: <5}{4: <5}{5: <5}".format(self.year, self.teamName, 
                                                                   self.wins, self.losses, self.ties, self.ngames))
        
        
    def getGames(self):
        return self.games
        
        
############################################################################################################
# Season Class
############################################################################################################
class season:
    def __init__(self, year):
        self.year  = year
        self.teams = {}
        self.games = {}
        
    def getYear(self):
        return self.year
    
    def addTeam(self, team):
        teamID = team.getTeamID()
        self.teams[teamID] = team

In [4]:
class historical(espn, output):
    def __init__(self):
        self.name = "historical"
        espn.__init__(self)
        output.__init__(self)
        
        ## 2015
        self.noGameData2003 = ['232350023', '232400195', '232400254', '232402006', '232402050', '232412439', '232420021', '232420062', '232420167', '232420235', '232420248', '232420276', '232422005', '232422426', '232422440', '232422751', '232442132', '232470005', '232490068', '232490309', '232490349', '232492638', '232492649', '232492655', '232550276', '232560005', '232560036', '232560070', '232560167', '232560189', '232560202', '232560309', '232562005', '232562084', '232562572', '232562638', '232610023', '232630021', '232630036', '232630097', '232630202', '232630278', '232630349', '232632005', '232632006', '232632084', '232632426', '232632439', '232700036', '232700062', '232700068', '232700149', '232700167', '232700193', '232700235', '232700252', '232700278', '232700349', '232702084', '232702440', '232702638', '232702653', '232730151', '232770021', '232770036', '232770041', '232770058', '232770166', '232770167', '232770193', '232770202', '232770235', '232770242', '232772132', '232772309', '232772348', '232772426', '232772440', '232772567', '232820252', '232840005', '232840023', '232840062', '232840068', '232840070', '232840097', '232840254', '232840276', '232840328', '232842005', '232842006', '232842638', '232842655', '232890036', '232900097', '232910021', '232910202', '232910242', '232910248', '232910249', '232910349', '232912006', '232912084', '232912309', '232912348', '232912439', '232912567', '232912751', '232980021', '232980062', '232980068', '232980151', '232980202', '232980278', '232980328', '232982050', '232982084', '232982132', '232982426', '232982439', '232982440', '232982572', '232982655', '233040252', '233050005', '233050023', '233050166', '233050167', '233050235', '233050242', '233050276', '233052005', '233052426', '233052567', '233052572', '233052638', '233052649', '233052751', '233110167', '233120005', '233120087', '233120151', '233120195', '233120242', '233120248', '233122005', '233122032', '233122132', '233122348', '233122439', '233122440', '233122638', '233190036', '233190087', '233190097', '233190167', '233190202', '233190249', '233190254', '233190278', '233190328', '233190349', '233192006', '233192440', '233192567', '233192572', '233260021', '233260023', '233260058', '233260062', '233260070', '233260097', '233260235', '233260242', '233260252', '233262309', '233262426', '233262439', '233262655', '233262751', '233290166', '233320276', '233322132', '233330151', '233330154', '233330235', '233330248', '233332348', '233332638', '233332751', '233402426']
        self.noGameData2003 += ['232352306']
        self.noGameData2004 = ['242480068', '242480195', '242480242', '242480252', '242480276', '242482751', '242550058', '242550189', '242550235', '242550349', '242552005', '242552006', '242552426', '242552628', '242620023', '242620166', '242620202', '242620242', '242620248', '242622439', '242622440', '242690005', '242690021', '242690036', '242690166', '242690195', '242692567', '242692655', '242730276', '242742005', '242760023', '242760036', '242760058', '242760062', '242760235', '242760249', '242760349', '242762084', '242762132', '242762439', '242762649', '242812572', '242820252', '242830062', '242830195', '242830242', '242830278', '242830328', '242830349', '242832005', '242832006', '242832116', '242890005', '242900058', '242900189', '242900235', '242900252', '242902032', '242902116', '242902426', '242902439', '242902440', '242902567', '242902649', '242960036', '242970062', '242970195', '242970249', '242970276', '242972005', '242972006', '242972132', '242972393', '242972426', '242972440', '242972572', '242972628', '242972649', '242972655', '243040023', '243040036', '243040189', '243040202', '243040248', '243040276', '243040278', '243042132', '243042393', '243042426', '243042751', '243102006', '243110062', '243110070', '243110189', '243110242', '243110252', '243110349', '243112116', '243112439', '243112440', '243112655', '243142459', '243162032', '243170278', '243180005', '243180036', '243180058', '243180189', '243180195', '243180249', '243180252', '243182005', '243182050', '243182084', '243182567', '243182655', '243232032', '243250021', '243250062', '243250151', '243250167', '243250202', '243250276', '243250278', '243250349', '243252005', '243252132', '243252628', '243282116', '243282649', '243320023', '243322572', '243322628', '243340242', '243392426']
        self.noGameData2005 = ['252460008', '252460023', '252460066', '252460204', '252460258', '252462032', '252462567', '252530008', '252530084', '252530096', '252530239', '252600024', '252600025', '252600154', '252600264', '252600265', '252602005', '252670070', '252670238', '252672306', '252672567', '252740023', '252740062', '252740070', '252740204', '252770249', '252810008', '252810166', '252810328', '252812348', '252812440', '252880062', '252880068', '252880278', '252882440', '252950023', '252950154', '252952306', '253020068', '253020096', '253020204', '253020252', '253022306', '253022348', '253090068', '253090328', '253092440', '253160062', '253160070', '253160166', '253160238', '253160349', '253162032', '253230008', '253230023', '253230068', '253230152', '253230328', '253230349', '253232306', '253232426', '253232439', '253300023', '253300166', '253300249', '253302348']
        self.noGameData2006 = ['262440278', '262450084', '262450152', '262450264', '262452306', '262452509', '262520008', '262520059', '262520096', '262520239', '262520252', '262520258', '262522306', '262590070', '262590166', '262590258', '262590264', '262590265', '262590333', '262592348', '262660024', '262660145', '262660238', '262660239', '262660252', '262730096', '262730204', '262730238', '262730239', '262730328', '262800070', '262800328', '262870024', '262870265', '262870278', '262942032', '262942348', '262942440', '263010023', '263012306', '263012440', '263080070', '263080166', '263080204', '263080249', '263080265', '263080328', '263082393', '263082653', '263150062', '263150096', '263150264', '263150278', '263150309', '263152032', '263152226', '263152229', '263152440', '263220062', '263220096', '263220249', '263220276', '263220278', '263222348', '263222653', '263282348', '263290070', '263290145', '263290309', '263290328', '263292393', '263292433', '263360023', '263360166', '263360309', '263362229']
        self.noGameData2007 = ['272440009', '272440058', '272440150', '272440153', '272440195', '272440238', '272440242', '272440245', '272442226', '272442579', '272510012', '272510070', '272510167', '272510197', '272510218', '272510265', '272512567', '272580202', '272580204', '272580235', '272582032', '272650009', '272650021', '272650070', '272650195', '272650248', '272650249', '272652084', '272652638', '272702032', '272720008', '272720195', '272720197', '272720202', '272720248', '272790150', '272790218', '272792084', '272792309', '272792638', '272860005', '272860024', '272860036', '272860193', '272862032', '272862084', '272930005', '272930197', '272930218', '272930242', '273002084', '273002638', '273070005', '273070070', '273070145', '273070150', '273070193', '273070236', '273070242', '273072032', '273072633', '273140005', '273140167', '273140202', '273140276', '273142459', '273142567', '273210036', '273210098', '273210218', '273210242', '273210248', '273210333', '273212084', '273212348', '273212567', '273212638', '273280021', '273280070', '273280167', '273280242', '273280248', '273280276', '273282229', '273282459', '273352653']
        self.noGameData2008 = ['282430005', '282430012', '282430084', '282500012', '282500036', '282500070', '282500183', '282502032', '282570248', '282572032', '282642655', '282710218', '282712649', '282780166', '282782649', '282850021', '282990070', '282990249', '282992649', '283060258', '283062638', '283132393', '283250059', '283262649', '283270218', '283330218', '283412229']
        self.noGameData2009 = ['292460218', '292480193', '292480238', '292550249', '292622348', '292760021', '292762084', '292830218', '292830235', '292830265', '292832084', '292900195', '292970193', '293042638', '293180235', '293250023', '293312006', '293392348']        
        self.noGameData2010 = ['302452309', '302470103', '302472199', '302540077', '302540142', '302612638', 
                               '302680077', '302680183', '302820195', '302820249', '302890098', '302890249',
                               '302960070', '302962032', '303030062', '303032226', '303100249', '303172116', 
                               '303310278', '303312229', '303312653']            
        self.noGameData2011 = ['312462633', '312532006', '312600235', '312602439', 
                               '312670235', '312672653', '313160202', '313160235', '313302348']        
        self.noGameData2012 = ['322430328', '322450154', '322450167', '322520036', '322592572',
                               '322592638', '322662655', '322730113', '322732459', '322732655',
                               '322870195', '322872655', '323152006', '323220113']
        self.noGameData2013 = ['333580204']
        self.noGameData2014 = ['400548012', '400548062', '400548068', '400548080', '400548081',
                               '400548095', '400548125', '400548227', '400548409', '400547715',
                               '400547809', '400547919', '400548223', '400548269', '400548416']
        self.noGameData2015 = ['400787481', '400763646', '400763654', '400787345',
                               '400787363', '400787107', '400787357']
        self.noGameData2016 = ['400868914', '400868922', '400868930', '400868960', '400869143',
                               '400869274', '400869306', '400869182', '400869229', '400869241',
                               '400869370', '400869569', '400869156', '400869353', '400869383',
                               '400869390', '400869539', '400869819', '400869828', '400869842']
        self.noGameData2017 = ['400941794', '400944828', '400935239', '400944873', '400944860']
        self.noGameData2018 = []
        
        self.noGameData  = self.noGameData2003 + self.noGameData2004 + self.noGameData2005 + self.noGameData2006 + self.noGameData2007 + self.noGameData2008 + self.noGameData2009 
        self.noGameData += self.noGameData2010 + self.noGameData2011 + self.noGameData2012 + self.noGameData2013 + self.noGameData2014 + self.noGameData2015 + self.noGameData2016 
        self.noGameData += self.noGameData2017 + self.noGameData2018
                
        
        subdir    = "season"
        outputdir = mkSubDir(self.getSaveDir(), subdir)
        self.seasonDir = outputdir
        
        subdir    = "results"
        outputdir = mkSubDir(self.getSaveDir(), subdir)
        self.resultsDir = outputdir
        
        subdir    = "games"
        outputdir = mkSubDir(self.getSaveDir(), subdir)
        self.gamesDir = outputdir
        
        
        subdir    = "season"
        outputdir = mkSubDir(self.getResultsDir(), subdir)
        self.seasonResultsDir = outputdir
        
        subdir    = "games"
        outputdir = mkSubDir(self.getResultsDir(), subdir)
        self.gamesResultsDir = outputdir
        
    def getSeasonDir(self):
        return self.seasonDir
        
    def getGamesDir(self):
        return self.gamesDir
        
    def getResultsDir(self):
        return self.resultsDir
        
    def getSeasonResultsDir(self):
        return self.seasonResultsDir
        
    def getGamesResultsDir(self):
        return self.gamesResultsDir
        
        
    def getYearlySeasonDir(self, year):
        outputdir = mkSubDir(self.getSeasonDir(), str(year))
        return outputdir
        
        
    def getYearlyGamesDir(self, year):
        outputdir = mkSubDir(self.getGamesDir(), str(year))
        return outputdir
        
        
    def downloadTeamStandingsByYear(self, year, debug=False):
        baseurl  = self.getBase()
        suburl   = "college-football/standings/_/season"
        url      = join(baseurl, suburl, str(year))
        
        savename  = setFile(self.getSeasonDir(), str(year)+".p")
        if isFile(savename):
            return
        
        if debug:
            print("Downloading {0}".format(url))        
        getWebData(base=url, savename=savename, useSafari=False)
        sleep(10+2*random())


    def downloadTeamStandings(self, startYear=2003, endYear=2018, debug=False):
        for year in range(startYear, endYear+1):
            self.downloadTeamStandingsByYear(year, debug)
        
        
    def downloadTeamDataByYear(self, idval, name, year, debug=False):
        baseurl  = self.getBase()
        suburl   = "college-football/team/schedule/_/id/{0}/season".format(idval)
        url      = join(baseurl, suburl, str(year))
        
        outputdir = self.getYearlySeasonDir(year)
        savename  = setFile(outputdir, "{0}-{1}.p".format(name, year))
        if isFile(savename):
            return
        
        if debug:
            print("Downloading {0} to {1}".format(url, savename))
        getWebData(base=url, savename=savename, useSafari=False)
        sleep(15+2*random())
            
            
    def parseAndDownloadTeamYearlyStandings(self):
        files = findExt(self.getSeasonDir(), ext=".p", debug=False)
        for ifile in files:
            year     = getBaseFilename(ifile)
            htmldata = getFile(ifile)
            bsdata   = getHTML(htmldata)
            
            idVals = {}
            links  = bsdata.findAll("a")
            for link in links:
                attrs = link.attrs
                if attrs.get("data-clubhouse-uid") is not None:
                    href  = attrs['href']
                    name  = getBasename(href)
                    idval = getBasename(getDirname(href))
                    
                    if idVals.get(idval) is not None:
                        if idVals[idval] != name:
                            raise ValueError("Error in ID for this year!")
                    idVals[idval] = name

            for idVal,name in idVals.items():
                self.downloadTeamDataByYear(idVal, name, season=str(year), debug=True)
    #http://www.espn.com/college-football/team/schedule/_/id/201/season/2005"
            
            
    def parseTeamYearlyStandings(self, startYear=2003, endYear=2018, debug=False, verydebug=False):
        for year in range(startYear, endYear+1):
            seasonDir = self.getYearlySeasonDir(year)
            files = findExt(seasonDir, ext=".p", debug=False)
            
            seasonData = season(year)
            
            for ifile in files:
                nameyear = getBaseFilename(ifile)
                htmldata = getFile(ifile)
                bsdata   = getHTML(htmldata)
                teamName = nameyear.replace("-{0}".format(year), "")
                
                
                metadata = bsdata.find("meta", {"property": "og:url"})
                if metadata is None:
                    raise ValueError("Could not find basic team meta data for this file! {0}".format(ifile))
                    
                try:
                    content = metadata.attrs['content']
                    year    = getBasename(content)
                    teamID  = getBasename(getDirname(getDirname(content)))
                except:
                    raise ValueError("Could not get team year and ID from meta data: {0}".format(metadata))
                    
                if verydebug:
                    print(year,'\t',teamID,'\t',ifile)
                
                
                ## Create Team Object
                teamData = team(year=year, teamName=teamName, teamMascot=None, teamID=teamID)
                
                tables = bsdata.findAll("table", {"class": "Table2__table"})
                if verydebug:
                    print("\tFound {0} game tables".format(len(tables)))
                for it,table in enumerate(tables):
                    trs = table.findAll("tr")
                    
                    headers = trs[1]
                    headers = [x.text for x in headers.findAll("td") if x is not None]
                    
                    gameRows = trs[2:]
                    totalGames = len(gameRows)
                    
                    if verydebug:
                        print("\tFound {0} potential games".format(totalGames))
                    
                    for ig,tr in enumerate(gameRows):
                        tds = tr.findAll("td")
                        gameData = dict(zip(headers, tds))
                        extra    = {"OT": False, "Bowl": False}
                        
                        
                        ## Get the Date
                        try:
                            date = gameData["Date"]
                        except:
                            print(ifile)
                            raise ValueError("No date for this game! {0}".format(gameData))                            
                        date = date.text
                        
                        ## Only Keep Games With Regular Dates
                        try:
                            dateval = "{0} {1}".format(date.split(", ")[-1], year)
                            date    = getDateTime(dateval)
                        except:
                            date    = None
                        
                        if date is None:
                            continue
                        
                        ## Check for January Games (in the following year)
                        if date.month == 1:
                            date = addMonths(date, 12)
                            
                        
                        ## Get the Opponent
                        try:
                            opponent = gameData["Opponent"]
                        except:
                            raise ValueError("No opponent for this game! {0}".format(game))   
                            
                        try:
                            oppolink = opponent.find("a")
                            oppohref = oppolink.attrs['href']
                            opponame = getBasename(oppohref)
                            oppoID   = getBasename(getDirname(oppohref))
                        except:
                            opponame = opponent.text
                            oppoID   = 0
                            #raise ValueError("Could not find href in link! {0}".format(opponent))


                        
                        try:
                            gamespan = opponent.find("span", {"class": "pr2"})
                            gametype = gamespan.text
                        except:
                            raise ValueError("Could not find game type from {0}".format(opponent))
                        
                        if gametype == "vs":
                            location = teamID
                        elif gametype == "@":
                            location = oppoID
                        else:
                            raise ValueError("Location --> {0}".format(gametype))
                            
                            
                        if verydebug:
                            print("\t{0}/{1}\t{2}\t{3: <4}{4: <50}".format(ig, totalGames, printDateTime(date), gametype, opponame), end="\t")


                        
                        ## Get the Result
                        try:
                            result = gameData["Result"]
                        except:
                            raise ValueError("No result for this game! {0}".format(game))
                            
                        spans = result.findAll("span")
                        if len(spans) == 0:
                            continue
                        if len(spans) != 2:
                            raise ValueError("There are {0} spans in this row!: {1}".format(len(spans), result))
                        outcome = spans[0].text.strip()
                        score   = spans[1].text.strip()
                        
                        if score.endswith("OT"):
                            extra = {"OT": True}
                            score = score[:-3].strip()
                            
                        try:
                            scores  = [int(x) for x in score.split('-')]
                        except:
                            raise ValueError("Could not create integer scores from {0}".format(spans))

                        if outcome == 'W':                            
                            teamScore  = scores[0]
                            oppoScore  = scores[1]
                            teamResult = "W"
                            oppoResult = "L"
                        elif outcome == "L":
                            teamScore = scores[1]
                            oppoScore = scores[0]
                            teamResult = "L"
                            oppoResult = "W"
                        elif outcome == "T":
                            teamScore = scores[0]
                            oppoScore = scores[1]
                            teamResult = "T"
                            oppoResult = "T"
                        else:
                            raise ValueError("Did not recognize game outcome {0}".format(outcome))


                        ## Get the Game
                        try:
                            gamelink = result.find("a")
                            gamehref = gamelink.attrs['href']
                        except:
                            raise ValueError("Could not find href in link! {0}".format(result))

                            
                        if verydebug:
                            print("{0}  {1}".format(teamResult, "-".join(str(x) for x in [teamScore,oppoScore])))
                            
                            
                        ## Create game object
                        gameData = game(gameID=gameID, date=date, teamA=teamID, teamB=oppoID,
                                        teamAResult=teamResult, teamBResult=oppoResult,
                                        teamAScore=teamScore, teamBScore=oppoScore, location=location)
                        
                        
                        ## Append game to team data
                        teamData.addGame(gameData)
                        

                ## Show Summary
                teamData.setStatistics()
                if debug:
                    teamData.summary()
                    if teamData.ngames == 0:
                        removeFile(ifile, debug=True)
                        
                seasonData.addTeam(teamData)
                
            #http://www.espn.com/college-football/team/schedule/_/id/201/season/2005"

            savename = setFile(self.getSeasonResultsDir(), "{0}.p".format(year))            
            saveFile(idata=seasonData, ifile=savename, debug=True)
            
            
    def downloadGameDataByID(self, gameID, year, test=False, debug=False):        
        gamesDir   = self.getYearlyGamesDir(year)
        url="http://www.espn.com/college-football/playbyplay?gameId={0}".format(gameID)
        savename = setFile(gamesDir, "{0}.p".format(gameID))

        if isFile(savename):
            from os.path import getsize                    
            size = round(getsize(savename)/1e3)
            if size < 1:
                removeFile(savename, debug=True)

        if test:
            print("Downloading {0} to {1}".format(url,savename))
            return
        getWebData(base=url, savename=savename, dtime=6, useSafari=True, debug=True)
        sleep(6)
            
    def downloadGameData(self, debug=False, verydebug=False):
        resultsDir = self.getSeasonResultsDir()
        files = findExt(resultsDir, ext=".p", debug=False)

        gameType = "playbyplay"
        print("Sleeping for 5 seconds...")
        sleep(5)

        
        for ifile in files:
            seasonData = getFile(ifile)
            year       = seasonData.getYear()
            if year not in [2013,2014,2015]:
                continue
            gamesDir   = self.getYearlyGamesDir(year)
            
            teams = seasonData.teams
            for teamID,teamData in teams.items():
                teamGames = teamData.games
                for gameData in teamGames:
                    gameResult = gameData["Result"]
                    gameObject = gameData["Game"]
                    gameID     = gameObject.gameID
                    
                    if False:
                        prevLocation = "/Volumes/Seagate/Football/Games/Plays/{0}.html".format(gameID)
                        if isFile(prevLocation):
                            savename = setFile(gamesDir, "{0}.p".format(gameID))
                            if not isFile(savename) or True:
                                data = open(prevLocation, "rb").read()
                                saveFile(idata=data, ifile=savename, debug=True)
                                continue
                        continue

                    self.downloadGameDataByID(gameID, year, debug)
                        
                        
            
            
    def parseGameData(self, startYear=2003, endYear=2018, debug=False, verydebug=False):
        noData = {}
        for year in range(startYear, endYear+1):
            
            yearData = {}
            
            gamesDir = self.getYearlyGamesDir(year)        
            files    = findExt(gamesDir, ext=".p", debug=False)
            
            
            noData[year] = []
            for i,ifile in enumerate(files):
                gameID   = getBaseFilename(ifile)
                
                if gameID in self.noGameData:
                    continue
                
                htmldata = getFile(ifile)
                bsdata   = getHTML(htmldata)
                #print(bsdata)
                
                
                #verydebug=True
                #if gameID not in ['400603866']:
                #    continue
                
                teamData  = bsdata.findAll("div", {"class": "team-container"})
                
                longNames = [x.find("span", {"class": "long-name"}) for x in teamData]
                longNames = [x.text for x in longNames if x is not None]
                
                shortNames = [x.find("span", {"class": "short-name"}) for x in teamData]
                shortNames = [x.text for x in shortNames if x is not None]
                
                teamAbbrevs = [x.find("span", {"class": "abbrev"}) for x in teamData]
                teamNames   = [x.attrs for x in teamAbbrevs if x is not None]
                teamNames   = [x['title'] for x in teamNames]
                teamAbbrevs = [x.text for x in teamAbbrevs]
                
                teamIDs = [x.find("img", {"class": "team-logo"}) for x in teamData]
                teamIDs = [x.attrs for x in teamIDs if x is not None]
                teamIDs = [x['src'] for x in teamIDs]
                teamIDs = [re.search(r"(\d+).png", x) for x in teamIDs]
                teamIDs = [x.groups()[0] for x in teamIDs]

                awayTeam = {"Name": longNames[0], "Mascot": shortNames[0], "Abbrev": teamAbbrevs[0], "ID": teamIDs[0]}
                homeTeam = {"Name": longNames[1], "Mascot": shortNames[1], "Abbrev": teamAbbrevs[1], "ID": teamIDs[1]}
                
                    
                
                metadata = bsdata.find("meta", {"property": "og:title"})
                title    = None
                if metadata is not None:
                    title = metadata.attrs['content']
                    if verydebug:
                        print("==> {0}".format(title))
                
                ## Possesions
                posData = bsdata.find("ul", {"class": "css-accordion"})
                if posData is None:
                    posData = bsdata.find("article", {"class": "play-by-play"})
                if posData is None:
                    noData[year].append(gameID)
                    if verydebug:
                        print("Could not find possession data! {0}".format(gameID))
                    continue
                    #print(bsdata)
                    #1/0
                    #removeFile(ifile, debug)
                    #continue
                
                
                gameData = {"Teams": {"Away": awayTeam, "Home": homeTeam}, "Plays": []}

                if i % 10 == 0:
                    print("{0}/{1} with {2} no data games".format(i,len(files),len(noData[year])))
                
                    
                ###################
                ## Get Full Drive Data
                ###################

                drives = posData.findAll("li", {"class": "accordion-item"})
                if verydebug:
                    print("Drives {0}".format(len(drives)))

                for idr,drive in enumerate(drives):                                            

                    ## Get Drive Summary
                    headlines = [x.text.strip() for x in drive.findAll("span", {"class": "headline"})]
                    if verydebug:
                        print("Headlines {0}".format(len(headlines)))


                    ## Get Drive Details
                    details = [x.text.strip() for x in drive.findAll("span", {"class": "drive-details"})]
                    if verydebug:
                        print("Details {0}".format(len(details)))


                    ## Get Home Score
                    homescores = drive.findAll("span", {"class": "home"})
                    homescores = [x.find("span", {"class": "team-score"}) for x in homescores]
                    homescores = [x.text for x in homescores if x is not None]
                    if verydebug:
                        print("Home Scores {0}".format(len(homescores)))


                    ## Get Away Score
                    awayscores = drive.findAll("span", {"class": "away"})
                    awayscores = [x.find("span", {"class": "team-score"}) for x in awayscores]
                    awayscores = [x.text for x in awayscores if x is not None]
                    if verydebug:
                        print("Away Scores {0}".format(len(awayscores)))


                    ## Get Possession
                    possessions = drive.findAll("span", {"class": "home-logo"})
                    possessions = [x.find("img", {"class": "team-logo"}) for x in possessions]
                    possessions = [x.attrs['src'] for x in possessions if x is not None]
                    possessions = [x.split('&')[0] for x in possessions]
                    possessions = [getBaseFilename(x) for x in possessions]
                    if verydebug:
                        print("Possessions {0}".format(len(possessions)))


                    ## Check for valid headline (parsed correctly?)
                    if len(headlines) == 0:
                        continue
                        
                    validFGs    = ["Missed FG", "Field Goal", "FIELD GOAL", "MISSED FG", "Made FG",
                                   "Field Goal Good", "Field Goal Missed", "Blocked FG"]
                    validTDs    = ["Touchdown", "TOUCHDOWN", "END OF HALF Touchdown", "Downs Touchdown",                                  
                                   "Missed FG Touchdown", "End of Half Touchdown", "End of Game Touchdown", 
                                   "PUNT Touchdown", "FUMBLE Touchdown", "INTERCEPTION Touchdown",
                                   "FIELD GOAL Touchdown", "MISSED FG Touchdown", "Rushing Touchdown", "Passing Touchdown",
                                  "Kickoff Return Touchdown", "Interception Return Touch", "Turnover on Downs Touchdown",
                                  "Field Goal Missed Touchdown", "Field Goal Touchdown", "Rushing Touchdown Touchdown",
                                  "Field Goal Good Touchdown", "Passing Touchdown Touchdown",
                                   "Fumble Return Touchdown Touchdown", "Rushing TD", "Passing TD",
                                   "Blocked Punt TD", "Punt Return TD", "Fumble Ret. TD",
                                   "Interception TD", "Fumble TD", "Rushing TD Touchdown",
                                   "Blocked Punt TD Touchdown", "Blocked FG (TD)",
                                   "Punt Return TD Touchdown", "Kick Return TD",
                                   "Kickoff Return Touchdown Touchdown",
                                   "Missed FG (TD) Touchdown", "Blocked FG (TD) Touchdown",
                                   "Punt Return Touchdown Touchdown", "Interception Return Touch Touchdown"]
                    validEnds   = ["End of Half", "End of Game", "END OF HALF", "END OF GAME", "End of 4th Quarter"]
                    validTOs    = ["Fumble", "Interception", "FUMBLE", "INTERCEPTION", "Kickoff", "KICKOFF",
                                  "Blocked Punt"]
                    validTOPnts = ["Interception Touchdown", "Safety", "Punt Touchdown", "Fumble Touchdown",
                                   "Punt Return Touchdown", "Fumble Return Touchdown", "SAFETY"]
                    validDowns  = ["Punt", "Downs", "PUNT", "Possession (For OT Drives)", "DOWNS",
                                   "Possession (For OT Drives) Touchdown", "Turnover on Downs",
                                  "Poss. on downs", "Penalty"]
                    validPlay   = ["Rush", "Pass", "Sack", "Timeout", "Incomplete", "Pass Complete"]
                    valid2PT    = ["2PT Pass failed", "Missed PAT Return"]
                    validOdds   = ["on-side kick"]
                    validHeadlines  = validFGs + validTDs + validEnds + validTOs + validTOPnts + validDowns + validPlay + valid2PT
                    isValidHeadline = sum([x in validHeadlines for x in headlines])
                    if headlines[0] == '':
                        continue
                    if isValidHeadline == 0 and idr < len(drives) - 1:
                        print(idr,'/',len(drives))
                        print(title)
                        print(ifile)
                        #print(bsdata)
                        raise ValueError("No valid headline in {0}".format(headlines))
                        print("No valid headline in {0}".format(headlines))
                        continue


                    ## Analyze Play-by-Play
                    try:
                        driveList = drive.find("ul", {"class": "drive-list"})                        
                        plays = driveList.findAll("li")
                    except:
                        raise ValueError("Could not find drive list in drive {0}".format(drive))

                    driveData = []
                    for ip,play in enumerate(plays):

                        ## Check for Starting Position
                        startPos = play.find("h3")
                        if startPos is None:
                            raise ValueError("Could not find Starting Position in Play! {0}".format(play))
                        startData = startPos.text.strip()


                        ## Check for Play Text
                        span = play.find("span", {"class": "post-play"})
                        if span is None:
                            raise ValueError("Could not find post play data! {0}".format(play))
                        playData = span.text.strip()


                        driveData.append({"Play": ip, "Start": startData, "Data": playData})

                        #print(idr,'\t',ip,'\t',startData,'\t',playData)


                    ## Save Drive Data
                    gameData["Plays"].append({"Drive": len(gameData), "Headline": headlines, "Detail": details, 
                                              "HomeScore": homescores, "AwayScore": awayscores,
                                              "Possession": possessions, "Data": driveData})



                    if verydebug:
                        print(idr,'\t',headlines)
                        print(idr,'\t',details)
                        print(idr,'\t',homescores)
                        print(idr,'\t',awayscores)
                        print(idr,'\t',possessions)
                        print("")

                if verydebug:
                    print("Found {0} drives for gameID {1}".format(len(gameData), gameID))
                yearData[gameID] = gameData
                
            print("Parsed {0}/{1} games in {2}".format(len(yearData), len(files), year))
            savename = setFile(self.getGamesResultsDir(), "{0}-games.p".format(year))
            saveFile(idata=yearData, ifile=savename, debug=True)
            
        return noData

        
        # No Data in noData

# Order To Download ESPN Data

In [5]:
hist = historical()
#hist.downloadTeamStandings()
#hist.parseAndDownloadTeamYearlyStandings()
#hist.parseTeamYearlyStandings()
#hist.downloadGameData()
#hist.parseGameData()

# Extract Game Data

In [252]:
############################################################################################################
## Play Text Yardage Play
############################################################################################################
class playyards:
    def __init__(self, text=None, playtype=None, test=False):
        self.text     = text
        self.playtype = playtype
        self.test     = test
        
        self.playyards    = None
        self.kickingyards = None
        self.runbackyards = None
        self.penaltyyards = None
        
        self.yards = None
        
    def setPlay(self, text):
        self.text = text
        
    def setPlayType(self, playtype):
        self.playtype = playtype
        
    def makeYards(self, yards, debug=False):
        if self.test:
            return yards
        
        if yards == "NET" or yards == "IGN":
            return yards
        
        if yards == None:
            return None
        
        try:
            result = int(yards)
        except:
            raise ValueError("Could not extract yards from [{0}] play with [{1}] text".format(yards, self.text))
            
        return result
        
        
    def show(self, yards, caller, debug=False):            
        if debug:
            print("\t\t===> {0} Yards -> [{1}]".format(caller, yards))
            
    
    ############################################################################################################
    ## Find Play Yardage
    ############################################################################################################
    def findYards(self, debug=False):
        sign   = 1
        result = None
        
        self.findPenaltyYards(debug)
        self.findKickingYards(debug)
        self.findReturnYards(debug)
        self.findPlayYards(debug)
        
        yards = [self.playyards, self.kickingyards, self.runbackyards, self.penaltyyards]
        if not len([x for x in yards if x is not None]):
            if self.test is True:
                if debug:
                    print("Could not find yards in this play")
                self.yards = None
            else:
                raise ValueError("Could not find any yards for this play: [{0}]".format(self.text))
        else:
            if any([isinstance(x, int) for x in yards]):
                self.yards = sum([x for x in yards if (x is not None) and (isinstance(x, int))])
            elif any([isinstance(x, str) for x in yards]):
                self.yards = ", ".join([x for x in yards if (x is not None) and (isinstance(x, str))])
            else:
                self.yards = None
            


    
    ############################################################################################################
    ## Find Play Yardage
    ############################################################################################################
    def findPlayYards(self, debug=False):
        sign   = 1
        result = None
        start  = self.text

        prep = ("(or|for)")
        num  = "([+-?]\d+|\d+)"        
        dist = ("(yards|yard|Yds|yds|Yd|yd)")
                    
        
        
        #################################################################
        ### Check for yards
        #################################################################
        if result is None:
            if sum([x in self.text for x in ["no gain", "no loss", "DECLINED"]]) > 0:
                result = [0]
                if debug:
                    print("\t\t===> {0}".format(result))      

        if result is None:
            if sum([x in self.text for x in ["loss of zero", "gain of zero"]]) > 0:
                result = [0]
                if debug:
                    print("\t\t===> {0}".format(result))                

        if result is None:
            m = re.search(r"{0}\s{1}\s{2}".format(prep, num, dist), self.text)
            if m is not None:
                result = m.groups(0)
                result = result[1:]
                if debug:
                    print("\t\t===> {0}".format(result))        
        
        if result is None:
            m = re.search(r"\w+\s(-\d+)\s\w+", self.text)
            if m is not None:
                result = m.groups(0)                
                if debug:
                    print("\t\t===> {0}".format(result))

        if result is None:
            m = re.search(r"for\sa\s(\w+)\sof\s(\d+)\s{0}".format(dist), self.text)
            if m is not None:
                results = m.groups()
                sign    = results[0]
                result  = results[1:]
                if sign == "loss":
                    sign = -1
                if debug:
                    print("\t\t===> {0} ({1})".format(result, sign))
        
        if result is None:
            pattern = r"{0}\s{1}\spenalty".format(num, dist)
            m = re.search(pattern, self.text)
            if m is not None:
                sign   = -1
                result = m.groups()
                if debug:
                    print("\t\t===> {0}".format(result))
        
        if result is None:
            if sum([x in self.text for x in ["incomplete", "Incomplete"]]) > 0:
                result = [0]
                if debug:
                    print("\t\t===> {0}".format(result))
        
        if result is None:
            if sum([x in self.text for x in [" no gain", " No Gain", "failed"]]) > 0:
                result = [0]
                if debug:
                    print("\t\t===> {0}".format(result))
        
        if result is None:
            m = re.search(r"{0}\s{1}".format(num, dist), self.text)
            if m is not None:
                result = m.groups()
                if debug:
                    print("\t\t===> {0}".format(result))

        if result is None:
            result = [None]
        self.playyards = self.makeYards(result[0])
        self.show(self.runbackyards, "Drive", debug=debug)

        
        

    ############################################################################################################
    ## Find Penalty Yardage
    ############################################################################################################
    def findPenaltyYards(self, debug=False):
        kick = ("(punt|kickoff)")
        prep = ("(or|for)")
        num  = "([+-?]\d+|\d+)"  
        dist = ("(yards|yard|Yds|yds|Yd|yd)")
        
        yards = None
        
        ## False Start
        if sum([x in self.text for x in ["False Start"]]) > 0:
            yards = -5
            
        ## Offensive Pass Interference
        if sum([x in self.text for x in ["Offensive Pass Interference"]]) > 0:
            yards = "NET"
            
        ## Offensive Pass Interference
        if sum([x in self.text for x in ["Illegal Block"]]) > 0:
            yards = "NET"


        if yards is None:
            yards = "IGN"
        
            

        self.penaltyyards = self.makeYards(yards)
        self.show(self.runbackyards, "Penalty", debug=debug)


        
    ############################################################################################################
    ## Find Kicking Yardage
    ############################################################################################################
    def findKickingYards(self, debug=False):
        kick = ("(punt|kickoff)")
        prep = ("(or|for)")
        num  = "([+-?]\d+|\d+)"  
        dist = ("(yards|yard|Yds|yds|Yd|yd)")
        
        yards = None
        
        if yards is None:
            m = re.search(r"{0}\s{1}\s{2}\s{3}".format(kick, prep, num, dist), self.text)
            if m is not None:
                result = m.groups(0)
                yards  = result[2]

        self.kickingyards = self.makeYards(yards)
        self.show(self.kickingyards, "Kicking", debug=debug)


        
    

    ############################################################################################################
    ## Find Return Yardage
    ############################################################################################################
    def findReturnYards(self, debug=False):
        runback  = "(return|runback|returns)"
        norun    = "(downed|down)"
        prep     = "(or|for|at)"
        article  = "(the|a)"
        num      = "([+-?]\d+|\d+)"
        word     = "(\w+)"
        dist     = "(yards|yard|Yds|yds|Yd|yd)"
        
        yards = None
            
        if yards is None:
            m = re.search(r"{0}\s{1}\s{2}\s{3}".format(runback, prep, num, dist), self.text)
            if m is not None:
                result = m.groups(0)
                yards  = result[2]
        
        if yards is None:
            m = re.search(r"{0}\s{1}\s{2}\s{3}\s{4}".format(norun, prep, article, word, num), self.text)
            if m is not None:
                result = m.groups(0)
                yards  = 0
                    
        if yards is None:
            if sum([x in self.text for x in ["fair catch", "Fair Catch"]]) > 0:
                yards = 0

        self.runbackyards = self.makeYards(yards)
        self.show(self.runbackyards, "Return", debug=debug)
                        
            
_ = clock("Last Run")

Current Time is Mon Apr 01, 2019 07:53:22 for Last Run


In [254]:
yds = playyards(test=False)
yds.setPlay("Alex Starzyk punt for 43 yds, downed at the Vandy 21")
yds.setPlay("VANDERBILT Penalty, Offensive Pass Interference (Ralph Webb) to the Vandy 15")
yds.setPlay("P.J. Walker pass incomplete to Brandon Shippen")
yds.setPlay("kickoff for 58 yds")
print(yds.text)
yds.findYards(debug=True)
print("Yards: {0}".format(yds.yards))

kickoff for 58 yds
		===> Penalty Yards -> [None]
		===> Kicking Yards -> [58]
		===> Return Yards -> [None]
		===> ('58', 'yds')
		===> Drive Yards -> [None]
Yards: 116


In [300]:
############################################################################################################
### ## Football Play Data
############################################################################################################
class footballplay:
    def __init__(self, playtype, text, debug=False):
        self.playtype = playtype.title()
        self.text     = text
        
        self.__dict__[playtype] = True
        
        self.startY  = None
        self.endY    = None
        self.startT  = None
        self.endT    = None
        
        self.down    = None
        self.togo    = None
        self.quarter = None
        
        self.result   = None
        self.gain     = None
        self.turnover = None
        self.newdowns = None
        
        self.possession = None

        self.printType(debug)
        
    def setType(self, playtype):
        self.type = playtype
        
    def printType(self, debug=False):
        if debug:
            print("===> {0} Play".format(self.playtype))
        
        
     
        
        
class playanalysis:
    def __init__(self, text, playtype):
        self.text  = text
        self.yards = None
        
        self.__dict__[playtype] = True
        self.playtype = playtype
        
        
        py = playyards(text=text, playtype=playtype)
        self.findYards = py.findYards
        
        self.called = {}
    
    
    def setPlayText(self, text):
        self.text = text
    
    
    def getKey(self, key):
        if self.__dict__.get(key) is not None:
            return self.__dict__[key]
        return None
        
    
    def isScore(self, points=True):
        if self.getKey("touchdown") is True:
            if points:
                return 6
            return True
        elif self.getKey("fieldgoal") is True:
            if points:
                return 3
            return True
        elif self.getKey("safetypts") is True:
            if points:
                return 2
            return True
        elif self.getKey("pat") is True:
            if self.getKey("oneptpat") is True:
                if points:
                    return 1
                return True
            elif self.getKey("twoptpat") is True:
                if points:
                    return 2
                return True
            elif self.getKey("defpat") is True:
                if points:
                    return 2
                return True
            else:
                if points:
                    return 0
                return False
        else:
            if points:
                return 0
            return False
            
        
    ##################################################
    ## Passing Play
    ##################################################
    def findInterceptedPass(self, debug): 
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.interception = False
        if sum([x in self.text for x in ["interception", "Interception", "intercepted", "Intercepted"]]) > 0:
            self.interception = True

            if self.touchdown is False:
                if sum([x in self.text for x in [" Kick)", " KICK)"]]) > 0:
                    self.touchdown = True

        
    def findInterceptedPAT(self, debug):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        try:
            patsubplay = self.play[self.text.rfind("("):self.text.rfind(")")]
            self.interception = False
            if sum([x in patsubplay for x in ["interception", "Interception", "intercepted", "Intercepted"]]) > 0:
                self.interception = True
        except:
            if self.getKey("interception") is None:
                self.interception = False
            return
        
        

    def findPassing(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay(debug)
        
        self.complete = False
        self.interception = False
        
        if sum([x in self.text for x in ["complete", "Complete"]]) > 0:
            self.complete = True
                        
        if self.complete is False:
            self.findInterceptedPass(debug)
                    
        
    ##################################################
    ## Rushing Play
    ##################################################
    def findRushing(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay(debug)
                    
        
    ##################################################
    ## Interception Play
    ##################################################
    def findInterception(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay(debug)
        self.findPassing(debug)
        
        ## Check for implied touchdown
        if self.interceptionreturn is True:
            if self.touchdown is False:
                if sum([x in self.text for x in [" Kick)", " KICK)"]]) > 0:
                    self.touchdown = True
                    
        
    ##################################################
    ## Fumble Play
    ##################################################
    def findFumble(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay(debug)
        
        ## Check for implied touchdown
        if self.fumble is True:
            if self.touchdown is False:
                if sum([x in self.text for x in [" Kick)", " KICK)"]]) > 0:
                    self.touchdown = True
            
    
            
    ##################################################
    ## Basic Play
    ##################################################
    def addPAT(self, debug=False):
        self.addpat = False
        if self.touchdown is True:
            if sum([x in self.text for x in [" Kick)", " KICK)", " kick)", "2 point", " 2 Point", "Two-point", "two-point", "Two-Point"]]) > 0:
                self.addpat = True
                                

    ##################################################
    ## Basic Play
    ##################################################
    def findBasicPlay(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True


        self.fumble    = False
        self.touchdown = False
        self.safety    = False
        self.penalty   = False
        self.runback   = False
        self.noplay    = False


        if sum([x in self.text for x in ["touchdown", "Touchdown", "TOUCHDOWN", " TD", "TD,", "TD "]]) > 0:
            ## Noted Exceptions
            if self.text.find("TD Moton") != -1:
                self.touchdown = False
            else:
                self.touchdown = True
            
        if sum([x in self.text for x in [" fumble", " Fumble", " fumbled", " Fumbled"]]) > 0:
            self.fumble = True
            
        if sum([x in self.text for x in ["penalty", "PENALTY", "Penalty"]]) > 0:
            self.penalty = True
        
        if sum([x in self.text for x in ["return", "Return"]]) > 0:
            self.runback = True
        
        if sum([x in self.text for x in ["NO PLAY", "No Play"]]) > 0:
            self.noplay = True
        
        if sum([x in self.text for x in ["SAFETY", "Safety"]]) > 0:
            self.safety = True
        
            
    ##################################################
    ## Basic Kicking
    ##################################################
    def findBasicKicking(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay()
        self.blocked   = False
        self.missed    = False
        self.runback   = False
        self.touchback = False
        
        
        if sum([x in self.text for x in ["return", "Return"]]) > 0:
            self.runback = True
        
        if sum([x in self.text for x in ["no return", "No Return"]]) > 0:
            self.runback = False

        if sum([x in self.text for x in [" block", " blocked", "Blocked", "Block", "BLOCKED"]]) > 0:
            if sum([x in self.text.upper() for x in ["ILLEGAL BLOCK"]]) == 0:
                self.blocked = True

        if sum([x in self.text for x in ["touchback", "Touchback"]]) > 0:
            self.touchback = True
            
        if sum([x in self.text for x in [" miss ", " missed", " Missed", "MISSED", "no good", "no good", "No Good", "No good", "NO GOOD", "Failed", "FAILED", "failed"]]) > 0:
            self.missed = True
                    
        
    ##################################################
    ## Punt Play
    ##################################################
    def findPunt(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay(debug)
        
        ## Check for implied touchdown
        if self.punt is True:
            if self.touchdown is False:
                if sum([x in self.text for x in [" Kick)", " KICK)"]]) > 0:
                    self.touchdown = True
            
        
    def findFieldGoal(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicKicking(debug)

        if self.blocked is True or self.missed is True:
            self.fieldgoaltry = True
            self.fieldgoal    = False
        else:
            self.fieldgoaltry = False
            self.fieldgoal    = True
        
        
    def findPAT(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicKicking(debug)
        self.findInterceptedPAT(debug)
        
        
        ## Check for incorrect blocked assignment
        if self.blocked is True:
            if sum([x in self.text for x in ["punt", " PUNT", "Punt"]]) > 0:
                self.blocked = False
            if sum([x in self.text for x in ["Field Goal", "FIELD GOAL", "FG"]]) > 0:
                self.blocked = False
                
            
        ## Extra Point
        if self.missed is True or self.blocked is True:
            self.oneptpattry = True
            self.oneptpat    = False
        else:
            self.oneptpattry = False
            self.oneptpat    = True

        
        ## Defensive PAT
        self.defpat = False
        if sum([x in self.text for x in ["defensive PAT", "Defensive PAT"]]) > 0:
            self.defpat      = True
            self.oneptpat    = False
            self.oneptpattry = True

        
        ## 2-Point
        self.twoptpattry = False
        self.twoptpat    = False
        if sum([x in self.text for x in ["2 point", " 2 Point", "Two-point", "two-point", "Two-Point"]]) > 0:
            self.twoptpattry = True
            self.oneptpattry = False
            self.oneptpat    = False
            
            if self.missed is True or self.interception is True:
                self.twoptpat = False
            else:
                self.twoptpat = True
                
        
        ## Interception (from two point)
        if self.interception is True:
            self.twoptpattry = True
            self.twoptpat    = False
            self.oneptpattry = False
            self.oneptpat    = False
            

        ## Sanity check
        self.pat = False
        if sum([self.oneptpat, self.oneptpattry, self.twoptpat, self.twoptpattry, self.defpat]) > 0:
            self.pat = True

            
        
    def findKickoff(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicKicking(debug)
        
        self.touchback = False
        self.onside    = False
        self.recovery  = False
        
        if sum([x in self.text for x in ["onside ", "Onside ", "on-side"]]) > 0:
            self.onside = True

        if sum([x in self.text for x in ["recovered"]]) > 0:
            self.recovery = True

        

    ############################################################################################################
    ## Return Play
    ############################################################################################################
    def findReturn(self, debug=False):
        fname = sys._getframe().f_code.co_name
        if self.called.get(fname) is not None:
            return
        self.called[fname] = True

        self.findBasicPlay()
        
        self.puntreturn         = False
        self.fieldgoalreturn    = False
        self.kickoffreturn      = False
        self.onsidereturn       = False
        self.fumblereturn       = False
        self.interceptionreturn = False

        if self.__dict__.get("punt") is not None:
            if self.punt is True:
                self.puntreturn = True
                self.findPunt()
                
        if self.__dict__.get("kickoff") is not None:
            if self.kickoff is True:
                self.kickoffreturn = True
                
        if self.__dict__.get("onside") is not None:
            if self.onside is True:
                self.onsidereturn = True
                
        if self.__dict__.get("fieldgoal") is not None:
            if self.fieldgoal is True:
                self.fieldgoalreturn = True
                
        if self.__dict__.get("fumble") is not None:
            if self.fumble is True:
                self.fumblereturn = True
                self.findFumble()
                
        if self.__dict__.get("interception") is not None:
            if self.interception is True:
                self.interceptionreturn = True
                self.findInterception()
                

                
        
            
            

    ############################################################################################################
    ## Result of Play
    ############################################################################################################
    def findResult(self, debug=False):
        return self.playtype
        
        self.result = None
        if self.__dict__.get("penalty"):
            if self.penalty is True:
                self.result = "Penalty"
        elif self.__dict__.get("timeout"):
            if self.timeout is True:
                self.result = "Timeout"
        elif self.__dict__.get("end"):
            if self.end is True:
                self.result = "End"
        elif self.__dict__.get("touchdown"):
            if self.touchdown is True:
                self.result = "Touchdown"
        elif self.__dict__.get("madefieldgoal"):
            if self.madefieldgoal is True:
                self.result = "FieldGoal"
        elif self.__dict__.get("madefieldpat"):
            if self.madefieldpat is True:
                self.result = "PAT"
        elif self.__dict__.get("interception"):
            if self.interception is True:
                self.result = "Interception"
        elif self.__dict__.get("punt"):
            if self.punt is True:
                self.result = "Punt"
        else:
            self.result = "Continue"


_, _ = clock("Last Run")

Current Time is Mon Apr 01, 2019 08:42:00 for Last Run


In [320]:
############################################################################################################
## Penalty Play
############################################################################################################
class penaltyplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "penalty"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa  = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Penalty Specific
        self.penaltytype  = None
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = self.yds.penaltyyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is penaltyyards=={1}".format(self.name, self.result))
            
            
        
############################################################################################################
## Punt Play
############################################################################################################
class puntplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "punt"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa  = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.kicker = None
                
    def analyze(self, debug=False):
        self.pa.findPunt()
        self.yds.findYards()
        self.result = self.yds.kickingyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for kickyards=={2} and runbackyards=={3}".format(self.name, self.result, self.yds.kickyards, self.yds.runbackyards))
            print("\tResult of {0} play is touchback=={1}, blocked=={2}, touchdown=={3}".format(self.name, self.pa.touchback, self.pa.blocked, self.pa.touchdown))                    

        
        
############################################################################################################
## Kickoff Play
############################################################################################################
class kickoffplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "kickoff"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa  = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.kicker = None
                
    def analyze(self, debug=False):
        self.pa.findKickoff()
        self.yds.findYards()
        self.result = self.yds.kickingyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for kickyards=={2} and runbackyards=={3}".format(self.name, self.result, self.yds.kickyards, self.yds.runbackyards))
            print("\tResult of {0} play is touchback=={1}, blocked=={2}, touchdown=={3}".format(self.name, self.pa.touchback, self.pa.blocked, self.pa.touchdown))            
        

        
############################################################################################################
## Field Goal Play
############################################################################################################
class fieldgoalplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "fieldgoal"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.kicker = None
                
    def analyze(self, debug=False):
        self.pa.findFieldGoal()
        self.yds.findYards()
        self.result = self.yds.kickingyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
            print("\tResult of {0} play is blocked=={1}, return=={2}".format(self.name, self.blocked, self.runback))
        

        
############################################################################################################
## PAT Play
############################################################################################################
class patplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "pat"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.kicker = None
                
    def analyze(self, debug=False):
        self.pa.findPAT()
        self.yds.findYards()
        self.result = self.yds.kickingyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
            print("\tResult of {0} play is blocked=={1}, return=={2}".format(self.name, self.blocked, self.runback))

            

############################################################################################################
## Return Play
############################################################################################################
class returnplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "return"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa  = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.returner = None
                
    def analyze(self, debug=False):
        print(self.pa.__dict__)
        self.pa.findBasicKicking()
        self.pa.findBasicPlay()
        self.pa.findPassing()
        self.pa.findRushing()
        self.pa.findReturn()
        self.yds.findYards()
        self.result = self.yds.runbackyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for runbackyards=={2}".format(self.name, self.result, self.yds.runbackyards))
            print("\tResult of {0} play is touchback=={1}, blocked=={2}, touchdown=={3}".format(self.name, self.pa.touchback, self.pa.blocked, self.pa.touchdown))   
        

        
############################################################################################################
## Downs Play
############################################################################################################
class downsplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "downs"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = 0
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## No Play
############################################################################################################
class noplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "no"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = 0
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## Safety Play
############################################################################################################
class safetyplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "safety"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)

        ## Safety Specific
        self.rushing = None
        self.passing = None
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = self.yds.yards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## Timeout Play
############################################################################################################
class timeoutplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "timeout"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = 0
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## End Play
############################################################################################################
class endplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "end"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = 0
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## Begin Play
############################################################################################################
class beginplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "begin"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = 0
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## Sack Play
############################################################################################################
class sackplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "sack"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.quarterback = None
                
    def analyze(self, debug=False):
        self.pa.findBasicPlay()
        self.yds.findYards()
        self.result = self.yds.playyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))
        
        


############################################################################################################
## Run Play
############################################################################################################
class rushingplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "rushing"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Running Back
        self.runningback = None
                
    def analyze(self, debug=False):
        self.pa.findRushing()
        self.yds.findYards()
        self.result = self.yds.playyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for yards=={2}".format(self.name, self.result))          

            

        
############################################################################################################
## Pass Play
############################################################################################################
class passingplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "passing"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
        
        ## Players
        self.quarterback = None
        self.receiver    = None
                
    def analyze(self, debug=False):
        self.pa.findPassing()
        self.yds.findYards()
        self.result = self.yds.playyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for passingyards=={2}".format(self.name, self.result))
        

        
############################################################################################################
## Fumble Play
############################################################################################################
class fumbleplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "fumble"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)

        ## Fumble Specific
        self.rushing = None
        self.passing = None
        
        ## Player Specific
        self.fumbler   = None
        self.recoverer = None
        self.turnover  = None
                
    def analyze(self, debug=False):
        self.pa.findReturn()
        self.yds.findYards()
        self.result = self.yds.playyards
        self.show(debug)

    def show(self, debug=False):
        if debug:
            print("\tResult of {0} play is result=={1} for returnyards=={2}".format(self.name, self.result))
        
        


############################################################################################################
## Touchdown Play
############################################################################################################
class touchdownplay(footballplay):
    def __init__(self, text, debug=False):
        self.name = "touchdown"
        self.text = text
        footballplay.__init__(self, self.name, text, debug)
        self.pa = playanalysis(text=text, playtype=self.name)
        self.yds = playyards(text=text, playtype=self)
                
    def analyze(self, debug=False):
        self.pa.findReturn()
        self.yds.findYards()
        self.result = self.yds.playyards
        self.show(debug)
        
            
_ = clock("Last Run")

Current Time is Mon Apr 01, 2019 09:12:09 for Last Run


In [321]:
class playstartclass:
    def __init__(self, down=None, togo=None, startY=None, side=None, extra=None):
        self.down   = down
        self.togo   = togo
        self.startY = startY
        self.side   = side
        self.extra  = extra
        self.quarter   = None
        self.gameclock = None
        self.distToEndZone = None
        
    def setStartY(self, startY):
        self.startY = startY
        
    def setDistToEndZone(self, dist):
        self.distToEndZone = dist
        
    def setQuarter(self, quarter):
        self.quarter = quarter
        
    def setGameClock(self, gameclock):
        self.gameclock = gameclock
        
        
class drivedetailclass:
    def __init__(self, plays, yards, gametime):
        self.plays = plays
        self.yards = yards
        self.gametime = gametime
        
        
class playclass:
    def __init__(self, possession, start, play):
        self.possession = possession
        self.start = start
        self.play  = play
        

class driveclass:
    def __init__(self, headline, detail, possession, postdrivehomescore, postdriveawayscore, plays=None):
        self.headline = headline
        self.detail   = detail
        self.possession = possession
        self.postdrivehomescore = postdrivehomescore
        self.postdriveawayscore = postdriveawayscore
        self.plays = plays
        
    def setPlays(self, plays):
        self.plays = plays
        
        
class playtype:
    def __init__(self, playText, debug=False):
        play = None
        self.playtext = playText
        self.unknownPlays = []
        
        playSubText = playText
        pos = playText.rfind("(")
        if pos != -1 and pos > 5:
            playSubText = playText[:pos].strip()
        
        if sum([x in playSubText for x in ["field goal", "Field Goal", "Field goal", "FIELD GOAL", " fg ", " FG ", "MISSED FG", "Missed FG"]]) > 0:
            play = fieldgoalplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["timeout", "Timeout"]]) > 0:
            play = timeoutplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["kickoff", "Kickoff", "kick off", "Kick Off", "Onside Kick", "Onside kick", "onside kick", "on-side kick"]]) > 0:
            play = kickoffplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["punt ", "PUNT", "Punt", " punted", " Punted", " punt,", " punter ", "punts "]]) > 0:
            play = puntplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["end of the ", "End Of The ", "End of the ", "end of ", "End of ", "END OF "]]) > 0:
            play = endplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["start of the ", "Start Of The ", "Start of the ", "Begin Drive", "start of ", "Start of ", "START OF "]]) > 0:
            play = beginplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["SAFETY", "safety", "Safety"]]) > 0:
            play = safetyplay(playText, debug=debug)
        elif sum([x in playSubText for x in [" sack ", " sacked ", " Sack ", " Sacked ", "sacked,"]]) > 0:
            play = sackplay(playText, debug=debug)
        elif sum([x in playSubText for x in [" pass ", " passed ", " Pass ", " Passed ", " spikes ", " spiked ",
                                          "Interception Return", "Interception", "INTERCEPTION"]]) > 0:
            play = passingplay(playText, debug=debug)
        elif sum([x in playSubText for x in [" rush ", " rushed ", " Rush ", " Rushed ", " scramble", " rush,", " run ", " Run"]]) > 0:
            play = rushingplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["penalty", "PENALTY", "Penalty"]]) > 0:
            play = penaltyplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["fumble", "Fumble", " fumbled ", " Fumble ", " Fumbled ", "FUMBLE"]]) > 0:
            if sum([x in playSubText for x in ["touchdown", "Touchdown", "TOUCHDOWN"]]) > 0:
                play = touchdownplay(playText, debug=debug)
            else:
                play = fumbleplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["downs", "Downs", "DOWNS"]]) > 0:
            play = downsplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["touchdown", "Touchdown", "TOUCHDOWN"]]) > 0:
            play = touchdownplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["extra point", "Extra Point", "Extra point", "PAT", "2 point", "2 Point", "two-point", "Two-point", "Two-Point"]]) > 0:
            play = patplay(playText, debug=debug)
        elif sum([x in playSubText for x in ["NO PLAY", "No Play"]]) > 0:
            play = noplay(playText, debug=debug)
        elif len(playText) <= 1:
            self.play = None
        else:
            self.unknownPlays.append(playText)
            self.play = None
            
        self.play = play
                
            
    def getPlay(self):
        return self.play
        
    def getPlayText(self):
        return self.playtext
                        
            
_ = clock("Last Run")

Current Time is Mon Apr 01, 2019 09:12:09 for Last Run


In [323]:
playText = "(OT) Terry Wilson pass complete to Lynn Bowden Jr. for 4 yds to the TexAM 21"
ptype = playtype(playText)
play  = ptype.getPlay()
print(play)
playText = "No Play"
ptype = playtype(playText)
play  = ptype.getPlay()
print(play)

In [330]:
class playbyplay(espn, output):
    def __init__(self):
        self.name = "playbyplay"
        espn.__init__(self)
        output.__init__(self)
        
        self.hist = None
        
        
    def setHistorical(self, hist):
        self.hist = hist
    
    
    def parsePlayStart(self, playStartText, playNo, numPlays, playData):
        if len(playStartText) == 0:
            return None
        
        ps = None
        
        down = "(st|nd|rd|th)"
        num  = "(\d+)"
        word = "(\w+)"
        goal = "(GOAL|goal|Goal)"
        prep = "(on|at)"
        amp  = "(&|and)"
        
        ## Look for match of type [1st and 10 at CAL 19]
        m = re.search(r"{0}{1}\s{2}\s{3}\s{4}\s{5}\s{6}".format(num, down, amp, num, prep, word, num), playStartText)
        if m is not None:
            groups = m.groups()
            down   = groups[0]
            togo   = groups[3]
            startY = groups[6]
            side   = groups[5]
            ps     = playstartclass(down=down, togo=togo, startY=startY, side=side)
            

        ## Look for match of type [1st and GOAL at CAL 1]
        m = re.search(r"{0}{1}\s{2}\s{3}\s{4}\s{5}\s{6}".format(num, down, amp, goal, prep, word, num), playStartText)
        if m is not None:
            groups = m.groups()
            down   = groups[0]
            togo   = groups[6] ## replace goal with distance to goal
            startY = groups[6]
            side   = groups[5]
            ps     = playstartclass(down=down, togo=togo, startY=startY, side=side)
            

        ## Look for very near match without side of field [1st and 10 at 50]
        m = re.search(r"{0}{1}\s{2}\s{3}\s{4}\s{5}".format(num, down, amp, goal, prep, num), playStartText)
        if m is not None:
            groups = m.groups()
            down   = groups[0]
            togo   = groups[3] ## replace goal with distance to goal
            startY = groups[5]
            side   = None
            ps     = playstartclass(down=down, togo=togo, startY=startY, side=side)
            

        return ps
        raise ValueError("Could not parse [{0}] and [{1}]".format(playStartText, playData))
        
        
        
    
    def parseClockAndQuarter(self, playData, debug=False):
        gameclock = None
        quarterNo = None
        
        ## Check for end of quarter/half/game
        if sum([x in playData for x in ["End of the ", "End Of The ", "end of the ", "end of ", "End of "]]) > 0:
            gameclock = timedelta(minutes=0, seconds=0) 
            if sum([x in playData for x in ["1st Quarter", "1st quarter"]]) > 0:
                quarterNo = 1
            elif sum([x in playData for x in ["2nd Quarter", "2nd quarter", "1st Half", "1st half", "half", "Half"]]) > 0:
                quarterNo = 2
            elif sum([x in playData for x in ["3rd Quarter", "3rd quarter"]]) > 0:
                quarterNo = 3
            elif sum([x in playData for x in ["4th Quarter", "4th quarter", "2nd Half", "2nd half", " Game", " game"]]) > 0:
                quarterNo = 4
            elif "OT" in playData:
                quarterNo = "OT"
            else:
                quarterNo = "UNKNOWN END QTR"
                #raise ValueError("Could not determine quarter from {0}".format(playData))

                
        if gameclock is None and quarterNo is None:
            ## Check for start of quarter/half/game
            if sum([x in playData for x in ["Start of the ", "Start Of The ", "start of the ", "start of "]]) > 0:
                gameclock = timedelta(minutes=15, seconds=0) 
                if sum([x in playData for x in ["1st Quarter", "1st quarter"]]) > 0:
                    quarterNo = 1
                elif sum([x in playData for x in ["2nd Quarter", "2nd quarter", "1st Half", "1st half"]]) > 0:
                    quarterNo = 2
                elif sum([x in playData for x in ["3rd Quarter", "3rd quarter", "2nd Half", "2nd half"]]) > 0:
                    quarterNo = 3
                elif sum([x in playData for x in ["4th Quarter", "4th quarter", "2nd Half", "2nd half", " Game", " game"]]) > 0:
                    quarterNo = 4
                elif "OT" in playData:
                    quarterNo = "OT"
                else:
                    quarterNo = "UNKNOWN START QTR"
                    #raise ValueError("Could not determine quarter from {0}".format(playData))

        
        if gameclock is None and quarterNo is None:

            ## Check for specific format (HH:MM - 1st)
            m = re.match(r"\((.*?)\)", playData)
            if m is None:
                raise ValueError("Could not determine time and quarter from {0}".format(playData))

            try:
                text = m.group(0)
            except:
                raise ValueError("Could not extract regex result from {0}".format(playData))

               
            ## Check for overtime
            try:
                result = text[1:-1]
                if "OT" in result:
                    gameclock = timedelta(minutes=0, seconds=0) 
                    quarterNo = "OT"
            except:
                pass
            

            if gameclock is None:
                try:
                    result = text[1:-1]
                    result = result.split(" - ")
                    gameclock,quarter = result
                except:
                    raise ValueError("Could not parse time data: {0}".format(text))


                try:
                    minutes,seconds = gameclock.split(":")
                    gameclock = timedelta(minutes=int(minutes), seconds=int(seconds)) 
                except:
                    raise ValueError("Could not create timedelta for {0}".format(gameclock))


                quarterNo = {"1st":1, "2nd": 2, "3rd": 3, "4th": 4}.get(quarter)
                if quarterNo is None:
                    print("Could not find quarter from [{0}] or [{1}]".format(quarter, text))
                    #raise ValueError("Could not find quarter from [{0}] or [{1}]".format(quarter, text))


                try:
                    playData = playData.replace(text, "").strip()
                except:
                    raise ValueError("Could not remove [{0}] from [{1}]".format(text, playData))
                
        
        return gameclock,quarterNo,playData
        
        
    
    def parsePlayData(self, playStart, playData, fieldMap, debug=False):
        ##########################
        ## Find clock and quarter
        ##########################
        gameclock, quarter, playText = self.parseClockAndQuarter(playData)
        
        ##########################
        ## Determine play type
        ##########################
        ptype = playtype(playText)
        play  = ptype.getPlay()
        if play is None:
            raise ValueError("Could not determine play type from {0}".format(playText))
        play.analyze(debug=False)

        
        ##########################
        ## Insert Clock/Quarter
        ##########################
        if playStart is None:
            playStart = playstartclass()
            
        if isinstance(playStart, playstartclass):
            playStart.setQuarter(quarter)
            playStart.setGameClock(gameclock)

            
        return play, playStart

        
    def parsePossession(self, possession, fieldMap, debug=False):
        if not isinstance(possession, list):
            raise ValueError("Possession is not a list: {0}".format(possession))
            
        if len(possession) != 1:
            raise ValueError("Not one element in possession list: {0}".format(possession))
            
        teamID = possession[0]
        
        teamAbbrev = None
        try:
            teamAbbrev = fieldMap[teamID]
        except:
            raise ValueError("Could not find {0} in field map: {1}".format(teamID, fieldMap))
            
        return teamAbbrev
        
        
    def augmentPlayStartWithPossession(self, possession, startVals, debug=False):
        if isinstance(startVals, playstartclass):
            
            ## Check for a team having the ball on their own side of the field (common)
            try:
                startY = int(startVals.startY)
            except:
                raise ValueError("Starting line {0} is not an integer".format(startVals.startY))

            if possession == startVals.side:
                distToEndZone = 100 - startY
            else:
                distToEndZone = startY                
                
            startVals.setStartY(startY)
            startVals.setDistToEndZone(distToEndZone)

        return startVals
    

    def parseHeadline(self, headline):
        pltype = None
        
        if isinstance(headline, list):
            if len(headline) >= 1:
                ptype  = playtype(headline[0])
                pltype = ptype.getPlay()
                
                if pltype is None:
                    raise ValueError("Could not determine headline play type: {0}".format(headline[0]))
            else:
                print("Not one headline entry: {0}".format(headline))
        else:
            raise ValueError("Headline is not a list: {0}".format(headline))
            
        return pltype
    
    
    def parseScore(self, score):
        if not isinstance(score, list):
            raise ValueError("Could not determine score type: {0}".format(score))
            
        if len(score) != 1:
            raise ValueError("Not one detail entry: {0}".format(score))
            
        scoredata = score[0]
        
        try:
            scoredata = int(scoredata)
        except:
            raise ValueError("Could not find an integer score for {0}".format(scoredata))
            
        return scoredata
    
    
    def parseDetail(self, detail):
        if not isinstance(detail, list):
            raise ValueError("Could not determine detail play type: {0}".format(detail))
            
        if len(detail) != 1:
            raise ValueError("Not one detail entry: {0}".format(detail))
            
        detaildata = detail[0]
        
        
        yards = "(yards|yard|Yds|yds|Yd|yd)"
        plays = "(play|plays)"        
        num  = "([+-?]\d+|\d+)"
        
        totalplays = None
        totalyards = None
        totalclock = None

        m = re.search(r"{0}\s{1},\s{2}\s{3},\s{4}:{5}".format(num, plays, num, yards, num, num), detaildata)
        if m is not None:
            groups = m.groups()
            totalplays = int(groups[0])
            totalyards = int(groups[2])
            totalclock = timedelta(minutes=int(groups[4]), seconds=int(groups[5]))

            
        if totalplays is None and totalyards is None and totalclock is None:
            m = re.search(r"{0}\s{1},\s{2}\s{3}".format(num, plays, num, yards), detaildata)
            if m is not None:
                groups = m.groups()
                totalplays = int(groups[0])
                totalyards = int(groups[2])
                totalclock = timedelta(minutes=0, seconds=0)
                
            
        if totalplays is None and totalyards is None and totalclock is None:
            raise ValueError("Could not parse drive detail: {0}".format(detaildata))

        drivedetail = drivedetailclass(plays=totalplays, yards=totalyards, gametime=totalclock)
            
        return drivedetail
        
    
    def parseGames(self, gameID=None, debug=False):
        if hist is None:
            raise ValueError("Must set historical class!")

        self.unknownPlays = []
            
        files    = findExt(hist.getGamesResultsDir(), ext=".p", debug=False)
        for ifile in files:
            print(ifile)
            try:
                year = int(getBaseFilename(ifile).split("-")[0])
            except:
                raise ValueError("Could not get year from {0}".format(ifile))
            
            if year < 2014:
                continue
                
            """
            seasonDataFilename = setFile(hist.getSeasonResultsDir(), "{0}.p".format(year))
            seasonData = getFile(seasonDataFilename)
            teams = seasonData.teams
            for teamID,teamData in teams.items():
                print(teamID,'\t',teamData.teamID,'\t',teamData.teamName)
                for gameData in teamData.games:
                    result = gameData["Result"]
                    game   = gameData["Game"]
                    for k,v in game.__dict__.items():
                        print(k,'\t',v)                    
            """    
            yearData = getFile(ifile)

            if len(self.unknownPlays) > 75:
                break


            
            totalGames = 0
            for gameIdent,gameData in yearData.items():
                if gameID is not None:
                    if gameID != gameIdent:
                        continue
                
                teamsMetaData    = gameData["Teams"]
                homeTeamMetaData = teamsMetaData["Home"]
                awayTeamMetaData = teamsMetaData["Away"]
                driveData        = gameData["Plays"]
                
                print("GAME ID: {0}".format(gameIdent))
                print("  Home Team: {0}".format(homeTeamMetaData))
                print("  Away Team: {0}".format(awayTeamMetaData))

                fieldMap = {}
                fieldMap[homeTeamMetaData["ID"]]     = homeTeamMetaData["Abbrev"]
                fieldMap[homeTeamMetaData["Abbrev"]] = homeTeamMetaData["ID"]
                fieldMap[awayTeamMetaData["ID"]]     = awayTeamMetaData["Abbrev"]
                fieldMap[awayTeamMetaData["Abbrev"]] = awayTeamMetaData["ID"]
                
                fieldMap["Home"] = homeTeamMetaData["Abbrev"]
                fieldMap["Away"] = awayTeamMetaData["Abbrev"]


                if gameID in hist.noGameData:
                    continue
                
                if len(self.unknownPlays) > 75:
                    break
                    
                
                gameResult = []
                totalPlays = 0
                for idr,drive in enumerate(driveData):
                    driveNo    = drive['Drive']
                    headline   = drive['Headline']
                    detail     = drive['Detail']
                    ### For whatever reason home/away scores are reversed on the webpage...
                    homescore  = drive['AwayScore']
                    awayscore  = drive['HomeScore']
                    possession = drive['Posession'] ## note this needs to change later
                    drivedata  = drive['Data']
                    
                    
                    
                    print("{0}\t{1} - {2}".format(idr,homescore, awayscore))
                    
    
                    ## Determine possession as defined in the play start fields later
                    possession = self.parsePossession(possession, fieldMap)
                    headline   = self.parseHeadline(headline)
                    detail     = self.parseDetail(detail)
                    homescore  = self.parseScore(homescore)
                    awayscore  = self.parseScore(awayscore)
            
        
                    fullDriveData = driveclass(headline=headline, detail=detail, possession=possession,
                                              postdrivehomescore=homescore, postdriveawayscore=awayscore)
                    
                    drivePlays = []
            
                    for ipl,play in enumerate(drivedata):
                        playNo        = play['Play']
                        playStartText = play['Start']
                        playData      = play['Data']
                        startVals = self.parsePlayStart(playStartText, playNo, len(drivedata), playData)
                        startVals = self.augmentPlayStartWithPossession(possession, startVals)
                        playVals, startVals = self.parsePlayData(startVals, playData, fieldMap)
                        
                        playResults = playclass(possession=possession, start=startVals, play=playVals)
                        
                        totalPlays += 1
                        drivePlays.append(playResults)
                        
                    fullDriveData.setPlays(drivePlays)
                    fullDriveData = self.insertMissingData(gameIdent, idr, fullDriveData, debug)
                    fullDriveData = self.augmentPlayWithScore(fullDriveData, fieldMap, debug)

                    
                    gameResult.append(fullDriveData)
                
                gameResult  = self.splitChangeOfPossession(gameResult, fieldMap, debug=True)
                scoreResult = self.analyzeGameScore(gameResult, fieldMap, debug=True)
                self.analyzeGameData(gameResult)
                if scoreResult is False:
                    raise ValueError("There was a problem parsing the scores for this game {0}!".format(gameIdent))


                    
                totalGames += 1
                if debug:
                    print("Found {0} plays in this game {1}".format(totalPlays, gameID))
                    
                    
            print("Found {0} total games for {1}".format(totalGames, ifile))

            
    def insertMissingData(self, gameID, driveNo, fullDriveData, debug=False):
        if gameID == "401012350":
            if driveNo == 21:
                tmp = fullDriveData.plays[3]
                fullDriveData.plays[3] = fullDriveData.plays[4]
                fullDriveData.plays[4] = tmp
                
                ptype = playtype(fullDriveData.plays[3].play.text)
                play  = ptype.getPlay()
                play.analyze(debug=False)
                fullDriveData.plays[3].play = play
                ptype = playtype(fullDriveData.plays[4].play.text)
                play  = ptype.getPlay()
                play.analyze(debug=False)
                fullDriveData.plays[4].play = play
        if gameID == "401012348":
            if driveNo == 7:
                lastplay = fullDriveData.plays[-1]
                start    = lastplay.start
                playText = "Ryley Guay 37 yd FG GOOD"                
                ptype = playtype(playText)
                play  = ptype.getPlay()                
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                playStart = playstartclass(down=4, togo=start.togo, startY=start.startY, side=start.side)
                playStart.setQuarter(start.quarter)
                playStart.setGameClock(start.gameclock)
                playResults = playclass(possession=fullDriveData.possession, start=playStart, play=play)
                fullDriveData.plays.append(playResults)
            if driveNo == 8:
                lastplay = fullDriveData.plays[0]
                playText = "No Play"
                ptype = playtype(playText)
                play  = ptype.getPlay()
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                lastplay.play = play                
        if gameID == "401012347":
            if driveNo == 0:
                lastplay = fullDriveData.plays[0]
                playText = lastplay.play.text
                playText = playText.replace("return for 17 yds", "return for 17 yds for a TD")
                ptype = playtype(playText)
                play  = ptype.getPlay()
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                lastplay.play = play
                lastplay.play.pa.touchdown = True
        if gameID == "401012341":
            if driveNo == 21:
                lastplay = fullDriveData.plays[-1]
                playText = lastplay.play.text
                playText = "{0} (Cooper Garcia Kick)".format(playText)                
                ptype = playtype(playText)
                play  = ptype.getPlay()
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                lastplay.play = play
        if gameID == "401012316":
            if driveNo == 14:
                lastplay = fullDriveData.plays[-1]
                lastplay.play.pa.fumble = False
                lastplay.play.pa.touchdown = True
        if gameID == "401012302":
            if driveNo == 15:
                lastplay = fullDriveData.plays[-2]
                lastplay.play.pa.fumble = False
                lastplay.play.pa.touchdown = True
        if gameID == "401012289":
            if driveNo == 20:
                lastplay = fullDriveData.plays[-2]
                playText = lastplay.play.text
                playText = playText.replace(" (", " For a TD (")             
                ptype = playtype(playText)
                play  = ptype.getPlay()
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                lastplay.play = play
                lastplay.play.pa.touchdown = True
        if gameID == "401012263":
            if driveNo == 18:
                lastplay = fullDriveData.plays[-2]
                playText = lastplay.play.text
                playText = "{0} For a TD".format(playText)            
                ptype = playtype(playText)
                play  = ptype.getPlay()
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                lastplay.play = play
        if gameID == "401012282":
            if driveNo == 8:
                lastplay = fullDriveData.plays[-1]
                start    = lastplay.start
                playText = "Tyrel Dodson 78 Yd Return of Blocked Field Goal (Seth Small Kick)"
                
                ptype = playtype(playText)
                play  = ptype.getPlay()                
                if play is None:
                    raise ValueError("Could not determine play type from {0}".format(playText))
                play.analyze(debug=False)
                play.pa.touchdown = True
                playStart = playstartclass(down=4, togo=start.togo, startY=start.startY, side=start.side)
                playStart.setQuarter(start.quarter)
                playStart.setGameClock(start.gameclock)
                playResults = playclass(possession=fullDriveData.possession, start=playStart, play=play)
                fullDriveData.plays.append(playResults)
                
                headline   = self.parseHeadline(["Touchdown"])
                fullDriveData.headline = headline


        return fullDriveData
            
            
    def augmentPlayWithScore(self, fullDriveData, fieldMap, debug=False):
        if not isinstance(fullDriveData, driveclass):
            raise ValueError("Game result is {0}".format(type(fullDriveData)))

        homeTeam = fieldMap["Home"]
        awayTeam = fieldMap["Away"]
        
        plays      = fullDriveData.plays
        headline   = fullDriveData.headline
        possession = fullDriveData.possession

        ## Check For Touchdown
        if isinstance(headline, touchdownplay):
            if sum(play.play.pa.touchdown for play in plays) == 0:
                for i in range(-len(plays), 1, -1):
                    if sum([x in plays[i].play.text for x in [" Kick)", " KICK)"]]) > 0:
                        print("Artificially setting play [{0}] to touchdown since text does not reflect it".format(i))
                        plays[i].play.pa.touchdown = True
                        break
            
            if sum(play.play.pa.touchdown for play in plays) == 0:
                for i in [-1,-2]:
                    try:
                        lastplay = plays[i]
                    except:
                        continue

                    if lastplay.play.pa.getKey("end") is True:
                        continue

                    if lastplay.play.pa.getKey("penalty") is True or lastplay.play.pa.getKey("penaltyplay") is True:
                        continue

                    if lastplay.play.pa.getKey("fumble") is True:
                        lastplay.play.pa.touchdown = True
                        break
                        if possession == homeTeam:
                            lastplay.possession = awayTeam
                        elif possession == awayTeam:
                            lastpata.possession = homeTeam
                            
                    lastplay.play.pa.touchdown = True
                    print("Artificially setting play [{0}] to touchdown since text does not reflect it".format(i))
                    break
                    
                if sum(play.play.pa.touchdown for play in plays) == 0:
                    for j,play in enumerate(plays):
                        print(j,'\t',play.play.text)
                    raise ValueError("Touchdown still not in text!")


        ## Check For Fumble + Touchdown
        if isinstance(headline, fumbleplay):
            if headline.pa.getKey("touchdown"):
                if sum(play.play.pa.touchdown for play in plays) == 0:
                    print("Artificially setting last play to touchdown since text does not reflect it")
                    lastplay = plays[-1]
                    lastplay.play.pa.touchdown = True
                    if sum(play.play.pa.touchdown for play in plays) == 0:
                        raise ValueError("Touchdown still not in text!")
                
        return fullDriveData
        
        
            
            
    def analyzeGameScore(self, gameResult, fieldMap, debug=False):
        if not isinstance(gameResult, list):
            raise ValueError("Game result is {0}".format(type(gameResult)))

        homeTeam = fieldMap["Home"]
        awayTeam = fieldMap["Away"]

        finalHomeScore = None
        runningHomeScore = 0
        finalAwayScore = None
        runningAwayScore = 0
        if debug:
            print("{0: <7}{1: <5}{2: <4}{3: <4}{4: <4}{5: <4}".format("Drive", "POS", "H", "(H)", "A", "(A)"))
            
        for idr in range(len(gameResult)):
            driveData  = gameResult[idr]
            if isinstance(driveData, driveclass) is False:
                raise ValueError("Drive Data is not a DriveClass object!")
                
            homescore  = driveData.postdrivehomescore
            finalHomeScore = homescore
            awayscore  = driveData.postdriveawayscore
            finalAwayScore = awayscore
            
            drivePlays = driveData.plays
            if isinstance(drivePlays, list) is False:
                raise ValueError("Drive Plays is not a list object!")

            scoringplays = []
            for drivePlay in drivePlays:
                play       = drivePlay.play
                possession = drivePlay.possession
                score      = play.pa.isScore()
                if score > 0:
                    scoringplays.append(play.text)
                    if possession == homeTeam:
                        runningHomeScore += score
                    elif possession == awayTeam:
                        runningAwayScore += score
                    else:
                        raise ValueError("Possession {0} is neither home {1} or away {2}".format(possession, homeTeam, awayTeam))
                        
            if debug:
                print("{0: <7}{1: <5}{2: <4}{3: <4}{4: <4}{5: <4}{6}".format(idr, possession, runningHomeScore, homescore, runningAwayScore, awayscore, scoringplays))
            
        if finalAwayScore != runningAwayScore or finalHomeScore != runningHomeScore:
            return False
        return True
            
            
    def splitChangeOfPossession(self, gameResult, fieldMap, debug=False):
        if not isinstance(gameResult, list):
            raise ValueError("Game result is {0}".format(type(gameResult)))

        homeTeam = fieldMap["Home"]
        awayTeam = fieldMap["Away"]
        
        splitDrives = []
        for idr in range(len(gameResult)):
            driveData  = gameResult[idr]
            if isinstance(driveData, driveclass) is False:
                raise ValueError("Drive Data is not a DriveClass object!")
                
            
            drivePlays = driveData.plays
            if isinstance(drivePlays, list) is False:
                raise ValueError("Drive Plays is not a list object!")


            ######################################################
            ## Split play into [kick] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if isinstance(playData.play, kickoffplay) and playData.play.pa.getKey("noplay") is False:
                    if driveData.possession == homeTeam:
                        playData.possession = awayTeam
                    elif driveData.possession == awayTeam:
                        playData.possession = homeTeam
                    newReturnPlay  = returnplay(text=playData.play.text)
                    newReturnPlay.analyze()
                    newReturnPlay.pa.kickoffplay = False
                    newReturnPlay.pa.touchdown = playData.play.pa.touchdown
                    newReturnPlay.pa.fumble    = playData.play.pa.fumble
                    playData.play.pa.touchdown = False
                    playData.play.pa.fumble    = False
                    playData.play.pa.runback   = False
                    newPlayData = playclass(possession=driveData.possession, start=playData.start, play=newReturnPlay)
                    drivePlays.insert(dp+1, newPlayData)
                    break


            ######################################################
            ## Split play into [punt] + [return/safety + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if isinstance(playData.play, puntplay) and playData.play.pa.getKey("noplay") is False:
                    if playData.play.pa.getKey("safety"):
                        newSafetyPlay  = safetyplay(text=playData.play.text)
                        newSafetyPlay.analyze()
                        newPlayData = playclass(possession=playData.possession, start=playData.start, play=newSafetyPlay)
                        drivePlays.insert(dp+1, newPlayData)
                        break
                    else:
                        playData.play.pa.touchdown = False
                        newReturnPlay  = returnplay(text=playData.play.text)
                        newReturnPlay.pa.punt = True
                        newReturnPlay.analyze()
                        newReturnPlay.pa.punt = False
                        newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                        if driveData.possession == homeTeam:
                            newPlayData.possession = awayTeam
                        elif driveData.possession == awayTeam:
                            newPlayData.possession = homeTeam
                        drivePlays.insert(dp+1, newPlayData)
                        break


            ######################################################
            ## Split play into [PAT] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if dp == len(drivePlays) - 1:
                    if isinstance(playData.play, patplay) and playData.play.pa.getKey("noplay") is False:
                        if playData.play.pa.getKey("defpat"):
                            playData.play.pa.defpat  = False
                            playData.play.pa.runback = False
                            newReturnPlay  = returnplay(text=playData.play.text)
                            newReturnPlay.analyze()
                            newReturnPlay.pa.defpat = True
                            newReturnPlay.pa.pat    = True
                            newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                            if driveData.possession == homeTeam:
                                newPlayData.possession = awayTeam
                            elif driveData.possession == awayTeam:
                                newPlayData.possession = homeTeam
                            drivePlays.insert(dp+1, newPlayData)
                            break


            ######################################################
            ## Split play into [interception] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if isinstance(playData.play, passingplay) and playData.play.pa.getKey("noplay") is False:
                    if playData.play.pa.interception is True:
                        if dp == len(drivePlays) - 1:
                            playData.play.pa.touchdown = False
                            playData.play.pa.runback   = False
                            newReturnPlay  = returnplay(text=playData.play.text)
                            newReturnPlay.analyze()
                            newReturnPlay.pa.interception = False
                            newReturnPlay.pa.runback      = True
                            newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                            if playData.possession == homeTeam:
                                newPlayData.possession = awayTeam
                            elif playData.possession == awayTeam:
                                newPlayData.possession = homeTeam
                            drivePlays.insert(dp+1, newPlayData)
                            break


            ######################################################
            ## Split play into [fumble] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if playData.play.pa.getKey("fumble") and playData.play.pa.getKey("runback"):
                    newReturnPlay  = returnplay(text=playData.play.text)
                    newReturnPlay.analyze()
                    newReturnPlay.pa.fumble = False
                    newReturnPlay.pa.touchdown = playData.play.pa.touchdown
                    playData.play.pa.touchdown = False
                    newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                    if playData.possession == homeTeam:
                        newPlayData.possession = awayTeam
                    elif playData.possession == awayTeam:
                        newPlayData.possession = homeTeam
                    drivePlays.insert(dp+1, newPlayData)
                    break


            ######################################################
            ## Split play into [FieldGoal] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if isinstance(playData.play, fieldgoalplay):
                    if playData.play.pa.getKey("blocked"):
                        newReturnPlay  = returnplay(text=playData.play.text)
                        newReturnPlay.pa.fieldgoal = True
                        newReturnPlay.analyze()
                        newReturnPlay.pa.fieldgoal = False
                        newReturnPlay.pa.touchdown = playData.play.pa.touchdown
                        playData.play.pa.touchdown = False
                        newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                        if playData.possession == homeTeam:
                            newPlayData.possession = awayTeam
                        elif playData.possession == awayTeam:
                            newPlayData.possession = homeTeam
                        drivePlays.insert(dp+1, newPlayData)
                        break


            ######################################################
            ## Split play into [fumble] + [return + X] for end of game
            ######################################################
            if idr == len(gameResult) - 1:
                for dp in range(len(drivePlays)):
                    playData  = drivePlays[dp]
                    if playData.play.pa.getKey("fumble") is True and playData.play.pa.getKey("touchdown") is True:
                        playData.play.pa.touchdown = False
                        newReturnPlay  = returnplay(text=playData.play.text)
                        newReturnPlay.analyze()
                        newReturnPlay.pa.fumble = False
                        newReturnPlay.pa.touchdown = True
                        newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                        if playData.possession == homeTeam:
                            newPlayData.possession = awayTeam
                        elif playData.possession == awayTeam:
                            newPlayData.possession = homeTeam
                        drivePlays.insert(dp+1, newPlayData)
                        break



            ######################################################
            ## Split play into [safety] + [return + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if isinstance(playData.play, safetyplay):
                    newReturnPlay  = returnplay(text=playData.play.text)
                    newReturnPlay.analyze()
                    newReturnPlay.pa.safety    = False
                    newReturnPlay.pa.safetypts = True
                    newPlayData = playclass(possession=playData.possession, start=playData.start, play=newReturnPlay)
                    if driveData.possession == homeTeam:
                        newPlayData.possession = awayTeam
                    elif driveData.possession == awayTeam:
                        newPlayData.possession = homeTeam
                    drivePlays.insert(dp+1, newPlayData)
                    break
                    
                    
            ######################################################
            ## Split play into [TD] + [PAT + X]
            ######################################################
            for dp in range(len(drivePlays)):
                playData  = drivePlays[dp]
                if playData.play.pa.touchdown is True:
                    if sum([isinstance(x.play, patplay) for x in drivePlays]) == 0:
                        playData.play.pa.addPAT()
                        if playData.play.pa.getKey("addpat") is True:
                            playData.play.pa.addpat = False
                            newPATPlay  = patplay(text=playData.play.text)
                            newPATPlay.analyze()
                            newPATPlay.pa.touchdown = False
                            newPlayData = playclass(possession=playData.possession, start=playData.start, play=newPATPlay)
                            drivePlays.insert(dp+1, newPlayData)
                            break
                            
                                
        return gameResult
            
    
    
    def analyzeGameData(self, gameResult, debug=False):
        if not isinstance(gameResult, list):
            raise ValueError("Game result is {0}".format(type(gameResult)))
            
        print("Drive\tPlay\tPosess\t{0: <5}{1: <5}{2: <10}{3: <3}{4: <4}{5: <5}{6: <5}{7: <30}{8}".format("Gain", "Dist", "Class", "D", "TG", "Side", "Line", "Keys", "Text"))
        for idr,driveData in enumerate(gameResult):
            drivePlays = driveData.plays
            possession = driveData.possession
            headline   = driveData.headline
            detail     = driveData.detail
            print("\n\n")
            print(headline,'\t\t',detail)
            for ip,playData in enumerate(drivePlays):
                playPossession = playData.possession
                print("  {0}\t{1}\t{2}".format(idr,ip,playPossession), end="\t")
            
                keys = ", ".join([k for k,v in playData.play.pa.__dict__.items() if v is True])
                
                    
                try:
                    playResult   = playData.play.result
                    print("{0: <5}".format(playResult), end="")
                except:
                    print("{0: <5}".format(""), end="")
                
                    
                try:
                    playDist   = playData.start.distToEndZone
                    print("{0: <5}".format(playDist), end="")
                except:
                    print("{0: <5}".format(""), end="")
                    
                    
                try:
                    playName   = playData.play.name
                    print("{0: <10}".format(playName), end="")
                except:
                    print("{0: <10}".format(""), end="")
                    
                    
                try:
                    playDown   = playData.start.down
                    print("{0: <3}".format(playDown), end="")
                except:
                    print("{0: <3}".format(""), end="")
                    
                    
                try:
                    playTogo   = playData.start.togo
                    print("{0: <4}".format(playTogo), end="")
                except:
                    print("{0: <4}".format(""), end="")
                    
                    
                try:
                    playSide   = playData.start.side
                    print("{0: <5}".format(playSide), end="")
                except:
                    print("{0: <5}".format(""), end="")
                    
                    
                try:
                    playStartY   = playData.start.startY
                    print("{0: <5}".format(playStartY), end="")
                except:
                    print("{0: <5}".format(""), end="")

                

                print("{0: <30}".format(keys), end="")


                playText   = playData.play.text
                print("{0}".format(playText))

                
_ = clock("Last Run")

Current Time is Mon Apr 01, 2019 10:42:01 for Last Run


In [331]:
pbp = playbyplay()
pbp.setHistorical(hist)
pbp.parseGames(gameID=None, debug=False)

/Users/tgadfort/Documents/football/results/games/2009-games.p
/Users/tgadfort/Documents/football/results/games/2010-games.p
/Users/tgadfort/Documents/football/results/games/2011-games.p
/Users/tgadfort/Documents/football/results/games/2008-games.p
/Users/tgadfort/Documents/football/results/games/2018-games.p
GAME ID: 401012246
  Home Team: {'Name': 'Alabama', 'Mascot': 'Crimson Tide', 'Abbrev': 'ALA', 'ID': '333'}
  Away Team: {'Name': 'Louisville', 'Mascot': 'Cardinals', 'Abbrev': 'LOU', 'ID': '97'}
0	['7'] - ['0']
1	['7'] - ['0']
2	['7'] - ['0']
3	['7'] - ['0']
4	['14'] - ['0']
5	['14'] - ['0']
6	['21'] - ['0']
7	['21'] - ['0']
8	['21'] - ['0']
9	['21'] - ['0']
10	['21'] - ['0']
11	['21'] - ['0']
12	['28'] - ['0']
13	['28'] - ['0']
14	['28'] - ['0']
15	['34'] - ['0']
16	['34'] - ['7']
17	['34'] - ['7']
18	['41'] - ['7']
19	['44'] - ['7']
20	['44'] - ['7']
21	['44'] - ['7']
22	['51'] - ['7']
23	['51'] - ['7']
24	['51'] - ['7']
25	['51'] - ['14']
26	['51'] - ['14']
{'text': "Evan O'Har

  20	6	LOU	0         end                        end                           End of 3rd Quarter
  20	7	LOU	0    68   passing   2  10  LOU  32   passing, complete             Jawon Pass pass incomplete to Jaylen Smith
  20	8	LOU	0    68   passing   3  10  LOU  32   passing, complete             Jawon Pass pass incomplete to Dez Fitzpatrick
  20	9	LOU	58   68   punt      4  10  LOU  32   punt, penalty, runback        Mason King punt for 58 yds , Jaylen Waddle returns for 21 yds to the ALABAMA 47 ALABAMA Penalty, Illegal Block (Joshua McMillon) to the Alab 21
  20	10	ALA	21   68   return    4  10  LOU  32   return, penalty, runback, puntreturnMason King punt for 58 yds , Jaylen Waddle returns for 21 yds to the ALABAMA 47 ALABAMA Penalty, Illegal Block (Joshua McMillon) to the Alab 21



<__main__.fieldgoalplay object at 0x1a25ae9160> 		 <__main__.drivedetailclass object at 0x1a25ae92e8>
  21	0	ALA	6    79   passing   1  10  ALA  21   passing, complete             Jalen Hurts pass complet

  10	3	ARK	     14   pat       1  10  EIU  14   pat, oneptpat                 La'Michael Pettway 14 Yd pass from Ty Storey (Connor Limpert Kick)



<__main__.puntplay object at 0x1a3243dcf8> 		 <__main__.drivedetailclass object at 0x1a3243deb8>
  11	0	ARK	65        kickoff                    kickoff                       Connor Limpert kickoff for 65 yds for a touchback
  11	1	EIU	          return                     return, touchback             Connor Limpert kickoff for 65 yds for a touchback
  11	2	EIU	3    75   rushing   1  10  EIU  25   rushing                       Johnathan Brantley run for 3 yds to the EIlln 28
  11	3	EIU	4    72   passing   2  7   EIU  28   passing, complete             Johnathan Brantley pass complete to Teriq Phillips for 4 yds to the EIlln 32
  11	4	EIU	3    68   rushing   3  3   EIU  32   rushing                       Robert Columbus run for 3 yds to the EIlln 35 for a 1ST down
  11	5	EIU	0    65   passing   1  10  EIU  35   passing, complete             

  0	4	WASH	0    75   passing   3  10  WASH 25   passing, complete             Jake Browning pass incomplete to Myles Gaskin
  0	5	WASH	43   75   punt      4  10  WASH 25   punt, runback                 Joel Whitford punt for 43 yds , Ryan Davis returns for 32 yds to the Wash 36
  0	6	AUB	32   75   return    4  10  WASH 25   return, runback, puntreturn   Joel Whitford punt for 43 yds , Ryan Davis returns for 32 yds to the Wash 36



<__main__.touchdownplay object at 0x1a35870588> 		 <__main__.drivedetailclass object at 0x1a35870c18>
  1	0	AUB	13   36   passing   1  10  WASH 36   passing, complete             Jarrett Stidham pass complete to Ryan Davis for 13 yds to the Wash 23 for a 1ST down
  1	1	AUB	2    23   rushing   1  10  WASH 23   rushing                       Kam Martin run for 2 yds to the Wash 21
  1	2	AUB	8    21   passing   2  8   WASH 21   passing, complete             Jarrett Stidham pass complete to Kam Martin for 8 yds to the Wash 13 for a 1ST down
  1	3	AUB	0    13   ru

  18	9	WASH	0    72   return    4  22  AUB  28   return, puntreturn            Arryn Siposs punt for 40 yds, fair catch by Aaron Fuller at the Wash 32



<__main__.puntplay object at 0x1a36a50f28> 		 <__main__.drivedetailclass object at 0x1a36a50ac8>
  19	0	WASH	23   68   passing   1  10  WASH 32   passing, penalty, noplay, completeBrowning, Jake pass complete to Jones, Ty for 23 yards to the AUBURN45, PENALTY WASHINGTON pass interference (Jones, Ty) 15 yards to the WASHINGTON17, NO PLAY.
  19	1	WASH	10   83   rushing   1  25  WASH 17   rushing                       Jake Browning run for 10 yds to the Wash 27
  19	2	WASH	3    73   passing   2  15  WASH 27   passing, complete             Jake Browning pass complete to Andre Baccellia for 3 yds to the Wash 30
  19	3	WASH	11   70   passing   3  12  WASH 30   passing, complete             Jake Browning pass complete to Aaron Fuller for 11 yds to the Wash 41
  19	4	WASH	36   59   punt      4  1   WASH 41   punt, runback                 Race

...

  7	0	LOU	63        kickoff                    kickoff                       Blanton Creque kickoff for 63 yds , Lynn Bowden Jr. return for 23 yds to the Kent 25
  7	1	UK	23        return                     return, runback               Blanton Creque kickoff for 63 yds , Lynn Bowden Jr. return for 23 yds to the Kent 25
  7	2	UK	3    75   rushing   1  10  UK   25   rushing                       Terry Wilson run for 3 yds to the Kent 28
  7	3	UK	IGN  72   penalty   2  7   UK   28   penalty                       KENTUCKY Penalty,  (-5 Yards) to the Kent 23
  7	4	UK	0    77   passing   2  12  UK   23   passing, penalty, noplay, completeTerry Wilson deep pass incomplete to Lynn Bowden Jr., PENALTY LOU pass interference (Character, Mar.) 15 yards to the UK38, 1ST DOWN UK, NO PLAY.
  7	5	UK	4    62   rushing   1  10  UK   38   rushing, penalty              Asim Rose run for 4 yds to the Kent 42 KENTUCKY Penalty, unsportsmanlike conduct (Asim Rose) to the Kent 27
  7	6	UK	32   73   passing  

  1	6	MIZ	     71   return    4  1   ARK  29   return, runback, puntreturn   Reid Bauer punt for 41 yds , Johnathon Johnson returns for a loss of 1 yard to the Misso 29



<__main__.puntplay object at 0x1a309a7ef0> 		 <__main__.drivedetailclass object at 0x1a309a7c88>
  2	0	MIZ	1    71   rushing   1  10  MIZ  29   rushing                       Tyler Badie run for a loss of 1 yard to the Misso 28
  2	1	MIZ	8    72   rushing   2  11  MIZ  28   rushing                       Tyler Badie run for 8 yds to the Misso 36
  2	2	MIZ	2    64   rushing   3  3   MIZ  36   rushing                       Tyler Badie run for 2 yds to the Misso 38
  2	3	MIZ	44   62   punt      4  1   MIZ  38   punt                          Corey Fatony punt for 44 yds, downed at the Ark 18
  2	4	ARK	0    62   return    4  1   MIZ  38   return, puntreturn            Corey Fatony punt for 44 yds, downed at the Ark 18



<__main__.puntplay object at 0x1a2547de80> 		 <__main__.drivedetailclass object at 0x1a35f1a7f0>
  3	0	A

15     CLEM 42  42  21  21  ['Tavien Feaster 13 Yd Run (Greg Huegel Kick)', 'Tavien Feaster 13 Yd Run (Greg Huegel Kick)']
16     SC   42  42  21  21  []
17     CLEM 49  49  21  21  ['Adam Choice 15 Yd Run (Greg Huegel Kick)', 'Adam Choice 15 Yd Run (Greg Huegel Kick)']
18     SC   49  49  28  28  ['Deebo Samuel 32 Yd pass from Jake Bentley (Parker White Kick)', 'Deebo Samuel 32 Yd pass from Jake Bentley (Parker White Kick)']
19     SC   49  49  28  28  []
20     CLEM 49  49  28  28  []
21     CLEM 49  49  28  28  []
22     SC   49  49  35  35  ['Jake Bentley pass complete to Shi Smith for 20 yds for a TD, (Parker White KICK)', 'Jake Bentley pass complete to Shi Smith for 20 yds for a TD, (Parker White KICK)']
23     CLEM 56  56  35  35  ['Travis Etienne run for 7 yds for a TD, (Greg Huegel KICK)', 'Travis Etienne run for 7 yds for a TD, (Greg Huegel KICK)']
Drive	Play	Posess	Gain Dist Class     D  TG  Side Line Keys                          Text



<__main__.touchdownplay object at 0x

  17	12	CLEM	     15   pat       2  4   SC   15   pat, oneptpat                 Adam Choice 15 Yd Run (Greg Huegel Kick)



<__main__.touchdownplay object at 0x1a25b8f5f8> 		 <__main__.drivedetailclass object at 0x1a25b8ff60>
  18	0	CLEM	65        kickoff                    kickoff                       B.T. Potter kickoff for 65 yds for a touchback
  18	1	SC	          return                     return, touchback             B.T. Potter kickoff for 65 yds for a touchback
  18	2	SC	5    75   rushing   1  10  SC   25   rushing                       Mon Denson run for 5 yds to the SCaro 30
  18	3	SC	2    70   rushing   2  5   SC   30   rushing                       Mon Denson run for 2 yds to the SCaro 32
  18	4	SC	15   68   passing   3  3   SC   32   passing, complete             Jake Bentley pass complete to Deebo Samuel for 15 yds to the SCaro 47 for a 1ST down
  18	5	SC	3    53   rushing   1  10  SC   47   rushing                       Rico Dowdle run for 3 yds to the 50 yard line
  1

ValueError: Touchdown still not in text!

In [ ]:
x = driveclass(1,2,3, 4,5)

In [ ]:
xd = x.__dict__
xd['headline'] = 'A'

In [ ]:
y = driveclass(**xd)
y.headline

In [ ]:

detaildata = '4 plays, 0 yards'


yards = "(yards|yard|Yds|yds|Yd|yd)"
plays = "(play|plays)"        
num  = "([+-?]\d+|\d+)"

totalplays = None
totalyards = None
totalclock = None

m = re.search(r"{0}\s{1},\s{2}\s{3},\s{4}:{5}".format(num, plays, num, yards, num, num), detaildata)
if m is not None:
    groups = m.groups()
    totalplays = int(groups[0])
    totalyards = int(groups[2])
    totalclock = timedelta(minutes=int(groups[4]), seconds=int(groups[5]))
else:
    raise ValueError("Could not parse drive detail: {0}".format(detaildata))


if totalplays is None and totalyards is None and totalclock is None:
    m = re.search(r"{0}\s{1},\s{2}\s{3}".format(num, plays, num, yards), detaildata)
    if m is not None:
        groups = m.groups()
        totalplays = int(groups[0])
        totalyards = int(groups[2])
        totalclock = timedelta(minutes=0, seconds=0)
    else:
        raise ValueError("Could not parse drive detail: {0}".format(detaildata))

totalplays

In [ ]:
m = re.search(r"{0}{1}\s{2}\s{3}\s{4}\s{5}\s{6}".format(num, down, amp, num, prep, word, num), start)
print(m.groups())

In [ ]:
start = 'Ryan Leadingham (CSUS) pass left side complete to Jason Girley (CSUS) for 4 yards.'

In [ ]:
start = ' sacked for a loss of 8 yards'
        
m = re.search(r"for\sa\s(\w+)\sof\s(\d+)\syard", start)
print(m.groups(0))

In [ ]:
prep = ("(or|for)")
num  = "([+-?]\d+|\d+)"        

plays = ["for 4 yard", "for -6 yard"]
for play in plays:
    print(play)
    m = re.search(r"{0}\s{1}\syard".format(prep, num), play)
    if m is not None:
        result = m.groups()                
        print("\t\t===> {0}".format(result))
    else:
        print("No Result")
    print("")

In [ ]:
start = "test of the hello"
print(re.findall("\sof|and|or\s", start))
start = "test or the hello"
print(re.findall("\s(of|and|or)\s", start))
start = "test and the hello"
print(re.findall("\s(of|and|or)\s", start))
start = "test the hello"
print(re.findall("\s(of|and|or)\s", start))

In [ ]:
list(range(-2,0))

In [ ]:
detaildata='6 plays, 18 yards, 2:53'
        

print(m)
if m is not None:
    groups = m.groups()
    print(groups)

In [ ]:
def fillConv():
    convs={}
    convs["Miami (FL)"] = "Miami (Florida)"
    convs["Miami (OH)"] = "Miami (Ohio)"
    convs["Florida Intl"] = "Florida International"
    convs["UCF"] = "Central Florida"
    convs["San José State"] = "San Jose State"
    convs["San Jos\xe9 State"] = "San Jose State"
    convs["UNLV"] = "Nevada-Las Vegas"
    convs["Kent State"] = "Kent"
    convs["BYU"] = "Brigham Young"
    convs["LSU"] = "Louisiana State"
    convs["Louisiana Monroe"] = "Louisiana-Monroe"
    convs["Louisiana Lafayette"] = "Louisiana-Lafayette"
    convs["TCU"] = "Texas Christian"
    convs["MTSU"] = "Middle Tennessee State"
    convs["Middle Tennessee"] = "Middle Tennessee State"
    convs["SMU"] = "Southern Methodist"
    convs["UTEP"] = "Texas-El Paso"
    convs["Texas San Antonio"] = "Texas-San Antonio"
    convs["BGSU"] = "Bowling Green State"
    convs["Bowling Green"] = "Bowling Green State"
    #convs["NCSU"] = "North Carolina State"
    convs["NC State"] = "North Carolina State"
    convs["USC"] = "Southern California"
    convs["Ole Miss"] = "Mississippi"
    
    convs["Presbyterian College"] = "Presbyterian"
    convs["The Citadel"] = "Citadel"
    convs["UC Davis"] = "California-Davis"
    convs["VMI"] = "Virginia Military Institute"
    convs["Stephen F Austin"] = "Stephen F. Austin"
    
    invconvs={}
    for k,v in convs.iteritems():
        invconvs[v] = k
    return convs, invconvs

def InvTeamConv(team):
    convs, invconvs = fillConv()
    if invconvs.get(team):
        return invconvs[team]
    return team
    
def TeamConv(team):
    convs, invconvs = fillConv()
    if convs.get(team):
        return convs[team]
    return team

In [ ]:
#!/usr/bin/env python2
# -*- coding: utf-8 -*-
"""
Created on Sun Dec  3 15:00:12 2017

@author: tgadfort
"""

import sys
if '/Users/tgadfort/Python' not in sys.path:
    sys.path.insert(0, '/Users/tgadfort/Python')

from fsio import setFile, isFile
from fileio import save
from path import getTeamsDBDir
from htmlParser import getHTML
from download import getURL

def getConferenceBaseURL():
    return "http://www.espn.com/college-football/standings/"

def getFBSURL():
    return getConferenceBaseURL()+"_/season/"
    
def getFCSURL():
    return getConferenceBaseURL()+"_/view/fcs/season/"
    
def getDIIURL():
    return getConferenceBaseURL()+"_/view/d2/season/"
    
def getDIIIURL():
    return getConferenceBaseURL()+"_/view/d3/season/"


def downloadConferenceData(yearID, debug = True):
    url = getFBSURL()+str(yearID)
    savename = setFile(getTeamsDBDir(), "FBS-"+str(yearID)+".p")
    if not isFile(savename):
        getURL(url, savename, debug)

    url = getFCSURL()+str(yearID)
    savename = setFile(getTeamsDBDir(), "FCS-"+str(yearID)+".p")
    if not isFile(savename):
        getURL(url, savename, debug)

    url = getDIIURL()+str(yearID)
    savename = setFile(getTeamsDBDir(), "DII-"+str(yearID)+".p")
    if not isFile(savename):
        getURL(url, savename, debug)

    url = getDIIIURL()+str(yearID)
    savename = setFile(getTeamsDBDir(), "DIII-"+str(yearID)+".p")
    if not isFile(savename):
        getURL(url, savename, debug)


def getConferenceData(yearID, confName, debug = True):
    savename = setFile(getTeamsDBDir(), confName+"-"+str(yearID)+".p")
    bsdata   = getHTML(savename)

    conferences = []
    h2s = bsdata.findAll("h2", {"class": "table-caption"})
    for h2 in h2s:
        span = h2.find("span", {"class": "long-caption"})
        if span:
            conferences.append(span.text)

    teamData = {}
    teamMap  = {}
                    
    tables = bsdata.findAll("table")
    for i,table in enumerate(tables):
        conferenceName = conferences[i]
        headers = []
        headers.append("Team")
        ths = table.findAll("th")
        for th in ths:
            span = th.find("span", {"class": "tooltip"})
            if span:
                headers.append(span.text)

        trs = table.findAll("tr", {"class": "standings-row"})
        for j,tr in enumerate(trs):
            tds = tr.findAll("td")
            
            ## Name
            try:
                ref      = tds[0].find("a").attrs['href']
                teamID   = ref.split("/")[-2]
                #teamName = ref.split("/")[-1]
                niceName = tds[0].find("span", {"class": "team-names"}).text
            except:
                #if debug:
                #print "Unknown team",tds[0]
                #print "Skipping..."
                continue

            teamMap[teamID] = {"CONF": conferenceName, "DIV": confName}
            if teamMap.get(conferenceName) == None:
                teamMap[conferenceName] = []
            teamMap[conferenceName].append(teamID)

            if teamMap.get(confName) == None:
                teamMap[confName] = []
            teamMap[confName].append(teamID)
            
            teamData[teamID] = {}

            localData = []
            localData.append(niceName)
            #print niceName,'\t',teamID
            for k in range(1,len(tds)):
                #print j,'\t',k,'\t',tds[k].text
                localData.append(tds[k].text)
            teamData[teamID] = dict(zip(headers, localData))
            teamData[teamID]["Conference"] = conferenceName
            teamData[teamID]["Division"]   = confName
                    
            

    return teamMap, teamData


def createConferenceData(yearID, debug = False):
    teamMapFBS,teamDataFBS   = getConferenceData(yearID, 'FBS', debug)
    teamMapFCS,teamDataFCS   = getConferenceData(yearID, 'FCS', debug)
    teamMapDII,teamDataDII   = getConferenceData(yearID, 'DII', debug)
    teamMapDIII,teamDataDIII = getConferenceData(yearID, 'DIII', debug)
    
    teamMap  = teamMapFBS.copy()
    teamMap.update(teamMapFCS)
    teamMap.update(teamMapDII)
    teamMap.update(teamMapDIII)

    teamData = teamDataFBS.copy()
    teamData.update(teamDataFCS)
    teamData.update(teamDataDII)
    teamData.update(teamDataDIII)
    
    savename = setFile(getTeamsDBDir(), str(yearID)+"-Map.p")
    save(savename, teamMap, debug = True)
    
    savename = setFile(getTeamsDBDir(), str(yearID)+"-Data.p")
    save(savename, teamData, debug = True)

In [ ]:
# -*- coding: utf-8 -*-
"""
Created on Wed Dec  9 17:36:45 2015

@author: tgadfort
"""

import TeamConv as tc
import teamNum as tn
import getHTML as web
import os
import glob
import random


def getURL(basepath, url, htmlid, force):
#    result = web.checkURL(url)
#    if result == False:
#        print ' --->',url,' = ',result
#        return result


    if os.path.exists(basepath):
        savehtml=basepath+"/"+str(htmlid)+".html"
    else:
        print ' ---> No save path'
        print basepath
        print htmlid
        return False
    
    if os.path.exists(savehtml) and force == False:
        print ' ---> Save path exists, but force -> FALSE'
        return False
        
    result=web.getHTML(url, savehtml)
    if result:
        print ' --->',url,'  in  ',savehtml
    else:
        print " Did not download",url



def parseHistoricalSchedule(schedule):
    vals = schedule.split("recap?id=")
    games={}
    for val in vals:
        pos    = val.find("\">")
        gameid = val[:pos]
        try:
            games[gameid] = int(gameid)
        except:
            continue
        
    return games
    
    


def parseSchedule(base, schedule):
    vals = schedule.split("<li>")
    games={}
    for val in vals:
        if val.find("gameId=") != -1:
            idval="href=\"/college-football/game?gameId="
            pos1=val.find(idval)
            pos2=val.find("\">", pos1+1)
            gamehtml=val[pos1+6:pos2]
            gameid=gamehtml.split("=")[1]
            gamehtml = base + gamehtml
            if games.get(gameid) == None:
                games[gameid] = gamehtml
    return games
    
 
def getHistoricalSchedule(basepath, teamid, force):
    years=range(2002, 2015)
    for year in years:
        yearid = str(year)
        url="http://espn.go.com/college-football/team/schedule/_/id/"+teamid+"/year/"+yearid + "/"
        htmlid = teamid + "-" + yearid
        getURL(basepath, url, htmlid, force)

    
def getTeamURL(teamnum):
    ttypes={}
    ttypes["Team"] = "team"
    urls=[]
    for k,v in ttypes.iteritems():
        url="http://espn.go.com/college-football/"+v+"/_/id/"+str(teamnum)
        urls.append([k,url])
    return urls


def getGameURLs(gameid):
    gtypes={}
    gtypes["Plays"]    = "playbyplay"
    gtypes["Matchup"]  ="matchup"
    gtypes["BoxScore"] = "boxscore"
    urls=[]
    for k,v in gtypes.iteritems():
        url="http://scores.espn.go.com/college-football/"+v+"?gameId="+str(gameid)
        urls.append([k,url])
    return urls



def getTeam(teamnum, locbase, test=False, force=False):
    urls = getTeamURL(teamnum)
    for url in urls:
        basepath = locbase + "/" + url[0]
        getURL(basepath, url[1], teamnum, force)
    
    
def getGame(gameid, locbase, test=False, force=False):
    urls = getGameURLs(gameid)
    for url in urls:
        basepath = locbase + "/" + url[0]
        getURL(basepath, url[1], gameid, force)
        


def getTeamHistoricalGames(schedulebase, teamnum):
    teamhtmls = glob.glob(schedulebase + "/" + str(teamnum) + "-*")
    teamgames={}
    for teamhtml in teamhtmls:
        teamyear  = os.path.basename(teamhtml).split(".")[0]
        team,year = teamyear.split("-")

        #print team,year
        #print teamhtml

        fdata = open(teamhtml).readlines()
        fdata = [x.strip('\r\n') for x in fdata]
        fdata = [x.strip('\t') for x in fdata]
        for line in fdata:
            if line.find("<ul class=\"game-schedule\">") != -1:
                games = parseHistoricalSchedule(line)
                teamgames.update(games)
#                for k,v in games.iteritems():
#                    teamgames[k] = getGameURLs(k)
                    
    return teamgames
    

def getTeamGames(locbase, webbase, teamnum):
    teamhtml=locbase + "/" + str(teamnum) + ".html"
    if not os.path.exists(teamhtml):
        print "No team file:",teamhtml
        return False
    fdata = open(teamhtml).readlines()
    fdata = [x.strip('\r\n') for x in fdata]
    fdata = [x.strip('\t') for x in fdata]
    for line in fdata:
        if line.find("<section class=\"club-schedule\" data-module=\"schedule\"") != -1:
            games = parseSchedule(webbase, line)
            return games
    return None


def parseTeam(base, teamhtml, fbsteams):
    fdata = open(teamhtml).readlines()
    fdata = [x.strip('\r\n') for x in fdata]
    fdata = [x.strip('\t') for x in fdata]

    
    for line in fdata:
        if line.find("<meta property=\"og:title\" content=\"") != -1:
            pos1=line.find("content=")
            pos2=line.find("College Football")
            name=line[pos1+9:pos2].strip()
            vals=name.split()
            fbsteam=False
            test1=vals[0]
            test1=tc.TeamConv(test1)
            test2=" ".join(vals[:2])
            test2=tc.TeamConv(test2)
            test3=test2+" State"
            test3=tc.TeamConv(test3)
            if fbsteams.get(test1):
                fbsteam = True
                print test1,"is an FBS team"
            if fbsteams.get(test2):
                fbsteam = True
                print test2,"is an FBS team"
            if fbsteams.get(test3):
                fbsteam = True
                print test3,"is an FBS team"
            if not fbsteam:
                print "I don't think [",name,"] is an FBS team"
                return
                
        if line.find("<section class=\"club-schedule\" data-module=\"schedule\"") != -1:
            games = parseSchedule(base, line)
            for game in games:
                idval = game.split("=")[1]
                playbyplay = game.replace("game?", "playbyplay?")
                saveval="Games/Plays/"+idval+".html"
                if os.path.exists(saveval):
                    #print "Already have",saveval
                    continue
                gamehtml = playbyplay
                print gamehtml,'--->',saveval
                getHTML(gamehtml, saveval)

                

def stripTeamNum(line):
    pos1=line.find("src=\"")
    pos2=line.find(".png", pos1+1)
    logoaddr=line[pos1+5:pos2+4]
    pos=logoaddr.rfind("/")
    try:
        teamnum=int(logoaddr[pos+1:-4])
    except:
        print "Could not get team number",logoaddr
        f()
    return teamnum,logoaddr    
    
    
def getTeamNum(line):
    logoname="class=\"logo\">"
    if line.find(logoname) != -1:
        teamnum,logoaddr=stripTeamNum(line)
        return teamnum,logoaddr    
    return -1,"NoLogoAddr"





In [ ]:
# -*- coding: utf-8 -*-
"""
Created on Mon Dec 14 15:27:02 2015

@author: tgadfort
"""


import TeamConv as tc
import teamNum as tn
import getHTML as web
import os
import json


def parseHistoricalScores(scorepath, teampath, histjsonfile):
    
    historicaldata={}
    years=range(1869, 2020)
    for year in years:
        yearid=str(year)
        key = yearid
        
        teamfile  = teampath + "/" + yearid + ".html"
        scorefile = scorepath + "/" + yearid + ".html"

        if os.path.exists(teamfile) and os.path.exists(scorefile):
            teamdata = open(teamfile).readlines()
            teamdata = [x.strip('\r\n') for x in teamdata]

            scoredata = open(scorefile).readlines()
            scoredata = [x.strip('\r\n') for x in scoredata]
        else:
            continue
        

        yearscores=[]
        yearteams={}
        
        conference=None
        for team in teamdata[1:]:
            if str.isalpha(team[0]) == True:
                continue
            if str.isalpha(team[1]) == True:
                conference=team.strip()
                continue
            if str.isalpha(team[2]) == True:
                teamname=tc.TeamConv(team.strip())
                yearteams[teamname] = conference
        
        for score in scoredata:
            vals = score.split()
            
            date = None
            team1 = None
            team2 = None
            score1 = None
            score2 = None
            
            
            ## Date
            date = vals[0]
            vals = vals[1:]

            ## Team1
            team1=[]
            j = 0
            while j < len(vals):
                try:
                    score1 = int(vals[j])
                    team1  = " ".join(team1)
                    vals   = vals[j+1:]
                    break
                except:
                    team1.append(vals[j])
                j += 1

            ## Team2
            team2=[]
            j = 0
            while j < len(vals):
                try:
                    score2 = int(vals[j])
                    team2  = " ".join(team2)
                    vals   = vals[j+1:]
                    break
                except:
                    team2.append(vals[j])
                j += 1
                
            comment = None
            if len(vals) > 0:
                comment = " ".join(vals)

            if score2 == None:
                lastval = vals[-1]
                testscore = lastval[-4:]
                try:
                    testscore = int(testscore)                    
                    team2     = lastval[:-4]
                    score2    = testscore
                    vals      = []
                except:
                    testscore = lastval[-3:]
                if not score2:
                    try:
                        testscore = int(testscore)
                        team2     = lastval[:-3]
                        score2    = testscore
                        vals      = []
                    except:
                        testscore = lastval[-2:]
                if not score2:
                    try:
                        testscore = int(testscore)
                        team2     = lastval[:-2]
                        score2    = testscore
                        vals      = []
                    except:
                        testscore = lastval[-1:]
                                        
                    
            team1 = tc.TeamConv(team1)
            team2 = tc.TeamConv(team2)
            
            sval={}
            sval['date']    = date
            sval['team1']   = team1
            try:
                sval['conf1']   = yearteams[team1]
            except:
                yearteams[team1] = "DivII"
                sval['conf1']   = yearteams[team1]
            sval['score1']  = score1
            sval['team2']   = team2
            try:
                sval['conf2']   = yearteams[team2]
            except:
                yearteams[team2] = "DivII"
                sval['conf2']   = yearteams[team2]
            sval['score2']  = score2
            sval['comment'] = comment
            yearscores.append(sval)


        historicaldata[key] = {}
        historicaldata[key]['teams']  = yearteams
        historicaldata[key]['scores'] = yearscores
        print '\t',key
        
    print '\tWrote',len(historicaldata),"scores to",histjsonfile
    json.dump(historicaldata, open(histjsonfile, "w"))

        

def getHistoricalTeams(basepath, force):
    years=range(1869, 2014)
    for year in years:
        yearid=str(year)
        url="http://wilson.engr.wisc.edu/rsfc/history/howell/cf"+yearid+"tms.txt"
        result = web.checkURL(url)
        if not result:
            continue
        
        if os.path.exists(basepath):
            savehtml=basepath+"/"+yearid+".html"
        else:
            print ' ---> No save path',basepath,'\t',yearid
            return False
        
        if os.path.exists(savehtml) and force == False:
            print ' ---> Save path exists, but force -> FALSE'
            return False
        
        result=web.getHTML(url, savehtml)
        if result:
            print ' --->',url,'  in  ',savehtml
        else:
            print " Did not download",url



def getHistoricalScores(basepath, force):
    years=range(1869, 2014)
    for year in years:
        yearid=str(year)
        url="http://wilson.engr.wisc.edu/rsfc/history/howell/cf"+yearid+"gms.txt"
        result = web.checkURL(url)
        if not result:
            continue
        
        if os.path.exists(basepath):
            savehtml=basepath+"/"+yearid+".html"
        else:
            print ' ---> No save path',basepath,'\t',yearid
            return False
        
        if os.path.exists(savehtml) and force == False:
            print ' ---> Save path exists, but force -> FALSE'
            return False
        
        result=web.getHTML(url, savehtml)
        if result:
            print ' --->',url,'  in  ',savehtml
        else:
            print " Did not download",url



def getScores(basepath, savehtml, yearid, force):
    url = 'http://www.jhowell.net/cf/scores/Sked2015.htm'
    result = web.checkURL(url)
    if result == False:
        print ' --->',url,' = ',result
        return result

    if os.path.exists(savehtml) and force == False:
        print ' ---> Save path exists, but force -> FALSE'
        return False
        
    result=web.getHTML(url, savehtml)
    if result:
        print ' --->',url,'  in  ',savehtml
    else:
        print " Did not download",url
        
    return True


def parseScores(txt):
    fdata = open(txt).readlines()
    fdata = [x.strip('\r\n') for x in fdata]

    yeardata={}

    i=0
    while i < len(fdata):
        line = fdata[i]
        tdata=[]
        if line.find("<table") != -1:
            while line.find("</table>") == -1:
                tdata.append(line)
                i += 1
                line = fdata[i]

            teamdata = parseTable(tdata)
            yeardata[teamdata['name']] = {}
            yeardata[teamdata['name']]['conf'] = teamdata['conf']
            yeardata[teamdata['name']]['games'] = teamdata['games']
        i += 1
    return yeardata



def parseTable(table):
    table = [x.replace("</tr>", "") for x in table]
    table = [x.replace("</td>", "") for x in table]

    teamdata={}
    teamdata["games"] = []
    
    table = table[1:]
    name,conf = getName(table[0])
    teamdata["name"] = name
    teamdata["conf"] = conf

    table = table[1:]

    for line in table:
        gamedata = getGame(line)
        if gamedata:
            teamdata["games"].append(gamedata)

    return teamdata
    f()

    
    
def getName(line):
    pos = line.find("<p align=\"center\">")
    if pos == -1:
        print "Could not parse:",line
        f()
    name = line[pos+18:]
    
    pos = name.rfind("(")
    conf = name[pos:]
    conf = conf.replace("(", "")
    conf = conf.replace(")", "")
    name = name[:pos-1]
    return name,conf


def getGame(line):
    line = line.replace("<td align=\"right\">", ":")
    line = line.replace("<td>", ":")
    line = line.replace("<tr>", "")
    linevals = line.split(":")
    site = None
    if len(linevals) == 8:
        try:
            dummy,date,day,home,opp,res,score,against = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    elif len(linevals) == 9:
        try:
            dummy,date,day,home,opp,res,score,against,site = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    elif len(linevals) == 10:
        try:
            dummy,date,day,home,opp,res,score,against,site,comment = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    
    opp = opp.replace("*", "")
    if home == "vs.":
        home = 1
    elif home == "@":
        home = -1
    else:
        print "ERROR with Home:",home
        f()
    if site != None:
        home = 0

    if len(res) == 0:
        return None

    try:
        game={}
        game['date'] = date
        game['day'] = day
        game['home'] = home
        game['opponent'] = opp
        game['result'] = res
        game['score'] = int(score)
        game['against'] = int(against)
    except:
        print "DICT ERROR\t",date,day,home,opp,res,score,against
        f()
        

    return game
    
    


##########################################
#
# This is the output line to the csv file
#
##########################################
def writeLine(outfile, Date, Team1, Team2, Score1, Score2, Winner):
    lout=[]
    lout.append(Date)
    lout.append(Team1)
    lout.append(Team2)
    lout.append(Score1)
    lout.append(Score2)
    lout.append(Winner)
    lout=[str(x) for x in lout]
    outfile.write(",".join(lout))
    outfile.write("\n")
    


def writeFile(fname, yeardata):
    f=open(fname, "w")
    writeLine(f, "Date", "Team1", "Team2", "Score1", "Score2", "Winner")
    nline=0
    teams=sorted(yeardata.keys())
    for team in teams:
        games = yeardata[team]["games"]
        for game in games:
            if game['result'] == 'W':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            elif game['result'] == 'L':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], game['opponent'])
            else:
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()

In [ ]:
from lxml import html
import requests
import json
import csv



def TeamConv(team):
    convs={}
    convs["Miami (FL)"] = "Miami (Florida)"
    convs["Miami (OH)"] = "Miami (Ohio)"
    convs["Florida Intl"] = "Florida International"
    convs["UCF"] = "Central Florida"
    convs["San José State"] = "San Jose State"
    convs["San Jos\xe9 State"] = "San Jose State"
    convs["UNLV"] = "Nevada-Las Vegas"
    convs["Kent State"] = "Kent"
    convs["BYU"] = "Brigham Young"
    convs["LSU"] = "Louisiana State"
    convs["Louisiana Monroe"] = "Louisiana-Monroe"
    convs["Louisiana Lafayette"] = "Louisiana-Lafayette"
    convs["TCU"] = "Texas Christian"
    convs["MTSU"] = "Middle Tennessee State"
    convs["Middle Tennessee"] = "Middle Tennessee State"
    convs["SMU"] = "Southern Methodist"
    convs["UTEP"] = "Texas-El Paso"
    convs["Texas San Antonio"] = "Texas-San Antonio"
    convs["BGSU"] = "Bowling Green State"
    convs["Bowling Green"] = "Bowling Green State"
    convs["NCSU"] = "North Carolina State"
    convs["NC State"] = "North Carolina State"
    convs["USC"] = "Southern California"
    convs["Ole Miss"] = "Mississippi"
    
    convs["Presbyterian College"] = "Presbyterian"
    convs["The Citadel"] = "Citadel"
    convs["UC Davis"] = "California-Davis"
    convs["VMI"] = "Virginia Military Institute"
    convs["Stephen F Austin"] = "Stephen F. Austin"
    if convs.get(team):
        return convs[team]
    return team


##########################################
#
# This is the output line to the csv file
#
##########################################
def writeLine(outfile, Date, Team1, Team2, Score1, Score2, Winner):
    lout=[]
    lout.append(Date)
    lout.append(Team1)
    lout.append(Team2)
    lout.append(Score1)
    lout.append(Score2)
    lout.append(Winner)
    lout=[str(x) for x in lout]
    outfile.write(",".join(lout))
    outfile.write("\n")
    


##########################################
#
# Write file based on start/end date
#
##########################################
def writeAbrvFile(fname, abrvdata):
    f=open(fname, "w")
    nline = 0
    teams = sorted(abrvdata.keys())
    for team in teams:
        abrv = abrvdata[team]["Abrv"]
        city = abrvdata[team]["City"]
        state = abrvdata[team]["State"]

        f.write(team+"\t"+city+"\t"+state+"\t"+abrv+"\n")
        nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()

def writeConfFile(fname, yeardata):
    f=open(fname, "w")
    teams=sorted(yeardata.keys())
    nline = 0
    for team in teams:
        conf = yeardata[team]["conf"]
        f.write(team+"\t"+conf+"\n")
        nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()
    

def writeGraphFile(fname, yeardata):
    f=open(fname, "w")
    teams=sorted(yeardata.keys())
    nline=0
    for team in teams:
        games = yeardata[team]["games"]
        opponents=[]
        opponents.append(team)
        for game in games:
            opponent = game['opponent']
            f.write(team+"\t"+opponent+"\n")
            nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()


def writeFile(fname, yeardata):
    f=open(fname, "w")
    writeLine(f, "Date", "Team1", "Team2", "Score1", "Score2", "Winner")
    nline=0
    teams=sorted(yeardata.keys())
    for team in teams:
        games = yeardata[team]["games"]
        for game in games:
            if game['result'] == 'W':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            elif game['result'] == 'L':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], game['opponent'])
            else:
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()




def getScores(htm, txt):
    page  = requests.get('http://www.jhowell.net/cf/scores/Sked2015.htm')
    fname = txt
    f = open(fname, "w")
    f.write(page.text)
    f.close()


def getAbrv(htm, txt):
    page  = requests.get('https://en.wikipedia.org/wiki/List_of_colloquial_names_for_universities_and_colleges_in_the_United_States')
    fname = txt
    f = open(fname, "w")
    f.write(page.text)
    f.close()


def getName(line):
    pos = line.find("<p align=\"center\">")
    if pos == -1:
        print "Could not parse:",line
        exit()
    name = line[pos+18:]
    
    pos = name.rfind("(")
    conf = name[pos:]
    conf = conf.replace("(", "")
    conf = conf.replace(")", "")
    name = name[:pos-1]
    return name,conf


def getGame(line):
    line = line.replace("<td align=\"right\">", ":")
    line = line.replace("<td>", ":")
    line = line.replace("<tr>", "")
    linevals = line.split(":")
    site = None
    if len(linevals) == 8:
        try:
            dummy,date,day,home,opp,res,score,against = linevals
        except:
            print "SPLIT ERROR:",line
            exit()
    elif len(linevals) == 9:
        try:
            dummy,date,day,home,opp,res,score,against,site = linevals
        except:
            print "SPLIT ERROR:",line
            exit()

    opp = opp.replace("*", "")
    if home == "vs.":
        home = 1
    elif home == "@":
        home = -1
    else:
        print "ERROR with Home:",home
        exit()
    if site != None:
        home = 0

    if len(res) == 0:
        return None

    try:
        game={}
        game['date'] = date
        game['day'] = day
        game['home'] = home
        game['opponent'] = opp
        game['result'] = res
        game['score'] = int(score)
        game['against'] = int(against)
    except:
        print "DICT ERROR\t",date,day,home,opp,res,score,against
        exit()
        

    return game    


def parseTable(table):
    table = [x.replace("</tr>", "") for x in table]
    table = [x.replace("</td>", "") for x in table]

    teamdata={}
    teamdata["games"] = []
    
    table = table[1:]
    name,conf = getName(table[0])
    teamdata["name"] = name
    teamdata["conf"] = conf

    table = table[1:]

    for line in table:
        gamedata = getGame(line)
        if gamedata:
            teamdata["games"].append(gamedata)

    return teamdata
    exit()

    

def parseScores(txt):
    fdata = open(txt).readlines()
    fdata = [x.strip('\r\n') for x in fdata]

    yeardata={}

    i=0
    while i < len(fdata):
        line = fdata[i]
        tdata=[]
        if line.find("<table") != -1:
            while line.find("</table>") == -1:
                tdata.append(line)
                i += 1
                line = fdata[i]

            teamdata = parseTable(tdata)
            yeardata[teamdata['name']] = {}
            yeardata[teamdata['name']]['conf'] = teamdata['conf']
            yeardata[teamdata['name']]['games'] = teamdata['games']
            print len(yeardata)
        i += 1
    return yeardata


def parseAbrv(txt):
    print txt
    fdata = open(txt).readlines()
    fdata = [x.strip('\r\n') for x in fdata]
    fdata = [x.strip('\t') for x in fdata]
    i=0
    adata={}
    while i < len(fdata):
        line = fdata[i]
        if line.find('----') != -1:
            i += 1
            continue
        vals = line.split(' = ')
        if len(vals) == 2:
            adata[vals[0]] = vals[1]
        else:
            print line,'\t',vals
            exit()
        i += 1

    return adata

def parseLocation(locdata, abrvdata):
    print locdata
    fdata = open(locdata).readlines()
    fdata = [x.strip('\r\n') for x in fdata]
    fdata = [x.strip('\t') for x in fdata]
    states={}
    missing={}
    print abrvdata.keys()
    fteam={}
    for team in abrvdata.keys():
        fteam[team] = {}
        fteam[team]["Abrv"] = abrvdata[team]
        fteam[team]["City"] = None
        fteam[team]["State"] = None
    
    for line in fdata:
        lvals = line.split('\t')
        name = lvals[0]
        mascot = lvals[1]
        city = lvals[2]
        state = lvals[3]
        if state == "Hawai'i":
            state = "Hawaii"
        conf = lvals[4]
        states[state] = 1
        
        if fteam.get(name) == None:
            print "#",name,city,state
            print "            fteam[\""+name+"\"][\"City\"] = "
            print "            fteam[\""+name+"\"][\"State\"] = "
        else:               
            fteam[name]["City"] = city
            fteam[name]["State"] = state
        
    print sorted(fteam.keys())
    
    fteam["Army"]["City"] = "West Point"
    fteam["Army"]["State"] = "New York"
    fteam["Bowling Green State"]["City"] = "Bowling Green"
    fteam["Bowling Green State"]["State"] = "Ohio"
    fteam["Brigham Young"]["City"] = "Provo"
    fteam["Brigham Young"]["State"] = "Utah"
    fteam["Central Florida"]["City"] = "Orlando"
    fteam["Central Florida"]["State"] = "Florida"
    fteam["Kent"]["City"] = "Kent"
    fteam["Kent"]["State"] = "Ohio"
    fteam["Louisiana State"]["City"] = "Baton Rouge"
    fteam["Louisiana State"]["State"] = "Louisiana"
    fteam["Miami (Florida)"]["City"] = "Coral Gables"
    fteam["Miami (Florida)"]["State"] = "Florida"
    fteam["Middle Tennessee State"]["City"] = "Murfreesboro"
    fteam["Middle Tennessee State"]["State"] = "Tennessee"
    fteam["Mississippi"]["City"] = "Oxford"
    fteam["Mississippi"]["State"] = "Mississippi"
    fteam["North Carolina State"]["City"] = "Raleigh"
    fteam["North Carolina State"]["State"] = "North Carolina"
    fteam["Northern Illinois"]["City"] = "DeKalb"
    fteam["Northern Illinois"]["State"] = "Illinois"
    fteam["Southern California"]["City"] = "Los Angeles"
    fteam["Southern California"]["State"] = "California"
    fteam["Southern Methodist"]["City"] = "University Park"
    fteam["Southern Methodist"]["State"] = "Texas"
    fteam["Southern Mississippi"]["City"] = "Hattiesburg"
    fteam["Southern Mississippi"]["State"] = "Mississippi"
    fteam["Texas Christian"]["City"] = "Fort Worth"
    fteam["Texas Christian"]["State"] = "Texas"
    fteam["Hawaii"]["City"] = "Honolulu"
    fteam["Hawaii"]["State"] = "Hawaii"
    fteam["Miami (Ohio)"]["City"] = "Oxford"
    fteam["Miami (Ohio)"]["State"] = "Ohio"
    fteam["Texas-El Paso"]["City"] = "El Paso"
    fteam["Texas-El Paso"]["State"] = "Texas"
    fteam["Texas-San Antonio"]["City"] = "San Antonio"
    fteam["Texas-San Antonio"]["State"] = "Texas"
    fteam["Nevada-Las Vegas"]["City"] = "Las Vegas"
    fteam["Nevada-Las Vegas"]["State"] = "Nevada"
    fteam["Florida International"]["City"] = "Miami"
    fteam["Florida International"]["State"] = "Florida"
            
    for k,v in fteam.iteritems():
        if v["City"] == None:
            print k

    return fteam
            
#    print sorted(states.keys())        
#    print abrvdata

#getAbrv('', 'Abvr.dat')
abrvdata = parseAbrv('Abrv.txt')
locdata = parseLocation('Location.csv', abrvdata)
json.dump(locdata, open("Teams.json", "w"))

yeardata = parseScores('2015.dat')
json.dump(yeardata, open("2015games.json", "w"))

writeAbrvFile('Teams.csv', locdata)
#writeFile('2015.csv', yeardata)
#writeConfFile('2015.conf', yeardata)
#writeGraphFile('2015.graph', yeardata)



In [ ]:

##############################################################################
#
#
# parseScoringSummary()
#
#
##############################################################################
def parseScoringSummary(gameid, scoredata, team1data, team2data, debug):
    scores=scoredata.split("<span class=\"headline\">")
    scores=scoredata.split("<div class=\"table-row\">")
    scores=scoredata.split("<img class=\"team-logo\" ")
    scores=scoredata.split("<tr><td class=\"logo\"><img class=\"team-logo\" ")

    teams={}
    teams[int(team1data[1])] = tc.TeamConv(team1data[0])
    teams[int(team2data[1])] = tc.TeamConv(team2data[0])
    teams[team1data[3]] = tc.TeamConv(team1data[0])
    teams[team2data[3]] = tc.TeamConv(team2data[0])
    summary=[]
    
    awayteam=None
    hometeam=None
    quarter=None
    for s in range(len(scores)):
        score=scores[s]
        teamnum,logoaddr=tn.stripTeamNum(score)
        
        

        ## Quarter
        flag="<th id=\"quarter-1\" class=\"quarter\" colspan=\"2\">"
        pos1=score.find(flag)
        pos2=score.find("</th>", pos1+1)
        if pos1 != -1:
            tmpquarter=score[pos1+len(flag):pos2]
        if quarter == None:
            quarter = tmpquarter            
            

        ## Score type        
        flag="<div class=\"score-type\">"
        pos1=score.find(flag)
        pos2=score.find("</div>", pos1+1)
        scoretype=score[pos1+len(flag):pos2]

        ## Drive time
        flag="<div class=\"time-stamp\">"
        pos1=score.find(flag)
        pos2=score.find("</div>", pos1+1)
        timestamp=score[pos1+len(flag):pos2]

        ## Result
        flag="<div class=\"headline\">"
        pos1=score.find(flag)
        pos2=score.find("</div>", pos1+1)
        headline=score[pos1+len(flag):pos2]
        
        ## Require timestamp and result to continue
        if len(timestamp) == 0 and len(headline) == 0:
            continue
        #print '[',timestamp,'][',headline,']'

        ## Score
        flag="<td class=\"home-score\">"
        pos1=score.find(flag)
        pos2=score.find("</td>", pos1+1)
        homescore=int(score[pos1+len(flag):pos2])

        ## Score
        flag="<td class=\"away-score\">"
        pos1=score.find(flag)
        pos2=score.find("</td>", pos1+1)
        awayscore=int(score[pos1+len(flag):pos2])

        ## Details
        flag="class=\"drive-details\">"
        details=[-1, -1, -1, -1]
        if score.find(flag) != -1 and True:
            pos1=score.find(flag)
            pos2=score.find("</div>", pos1+1)
            detail=score[pos1+len(flag):pos2]            
            dvals=detail.split(",")
            try:
                plays=dvals[0].replace("plays","")
                plays=plays.replace("play","")
                yards=dvals[1].replace("yards","")
                yards=yards.replace("yard","")
            except:
                print "Problem with drive (plays,yards) details"
                print dvals
                f()
                
            if len(dvals) == 3:
                try:
                    ptime=dvals[2].strip()
                    minutes,seconds=ptime.split(":")            
                except:
                    print "Problem with drive (time) details"
                    print dvals
                    f()
            else:
                minutes=-1
                seconds=-1
                
            try:
                details=[int(plays), int(yards), int(minutes), int(seconds)]
            except:
                print "Problem with drive details: Making ints"
                print dvals
                f()
        
        if hometeam == None:
            flag="<th class=\"home-team\">"
            pos1=score.find(flag)
            pos2=score.find("</th>", pos1+1)
            hometeam=score[pos1+len(flag):pos2]
        if awayteam == None:
            flag="<th class=\"away-team\">"
            pos1=score.find(flag)
            pos2=score.find("</th>", pos1+1)
            awayteam=score[pos1+len(flag):pos2]
        
        

        qnum=quarter.title()
        if qnum.find("First") != -1:
            qnum=1
        elif qnum.find("Second") != -1:
            qnum=2
        elif qnum.find("Third") != -1:
            qnum=3
        elif qnum.find("Fourth") != -1:
            qnum=4
        elif qnum.find("Overtime") != -1:
            qnum=5
        else:
            print "Could not extract quarter from",qnum
            f()
        summary.append([teams[teamnum], scoretype, qnum, timestamp, awayscore, homescore, headline, details])
        show=False
        if show:
            print s,'\t',teams[teamnum],'\t',scoretype,'\t',qnum,'\t',timestamp, '\t',
            print headline,'\t',awayteam,awayscore,'-',homescore,hometeam,'\t',
            print details,'\t',
            print scores[s]
        #,'\t\t',scores[s]
            
        quarter = tmpquarter
        
    scores={}
    scores[tc.TeamConv(team1data[0])] = []
    scores[tc.TeamConv(team2data[0])] = []
    summary=[]
    for i in range(len(summary)):
        teamname = tc.TeamConv(summary[i][0])
        if scores.get(teamname) == None:
            print "Key error in scores:",teamname
            print scores.keys()
            f()
        ssum = summary[i][1:]
        ssum.insert(0, i)
        scores[teamname].append(ssum)

    #print scores
    return scores

In [ ]:


def parseHistoricalScores(scorepath, teampath, histjsonfile):
    
    historicaldata={}
    years=range(1869, 2020)
    for year in years:
        yearid=str(year)
        key = yearid
        
        teamfile  = teampath + "/" + yearid + ".html"
        scorefile = scorepath + "/" + yearid + ".html"

        if os.path.exists(teamfile) and os.path.exists(scorefile):
            teamdata = open(teamfile).readlines()
            teamdata = [x.strip('\r\n') for x in teamdata]

            scoredata = open(scorefile).readlines()
            scoredata = [x.strip('\r\n') for x in scoredata]
        else:
            continue
        

        yearscores=[]
        yearteams={}
        
        conference=None
        for team in teamdata[1:]:
            if str.isalpha(team[0]) == True:
                continue
            if str.isalpha(team[1]) == True:
                conference=team.strip()
                continue
            if str.isalpha(team[2]) == True:
                teamname=tc.TeamConv(team.strip())
                yearteams[teamname] = conference
        
        for score in scoredata:
            vals = score.split()
            
            date = None
            team1 = None
            team2 = None
            score1 = None
            score2 = None
            
            
            ## Date
            date = vals[0]
            vals = vals[1:]

            ## Team1
            team1=[]
            j = 0
            while j < len(vals):
                try:
                    score1 = int(vals[j])
                    team1  = " ".join(team1)
                    vals   = vals[j+1:]
                    break
                except:
                    team1.append(vals[j])
                j += 1

            ## Team2
            team2=[]
            j = 0
            while j < len(vals):
                try:
                    score2 = int(vals[j])
                    team2  = " ".join(team2)
                    vals   = vals[j+1:]
                    break
                except:
                    team2.append(vals[j])
                j += 1
                
            comment = None
            if len(vals) > 0:
                comment = " ".join(vals)

            if score2 == None:
                lastval = vals[-1]
                testscore = lastval[-4:]
                try:
                    testscore = int(testscore)                    
                    team2     = lastval[:-4]
                    score2    = testscore
                    vals      = []
                except:
                    testscore = lastval[-3:]
                if not score2:
                    try:
                        testscore = int(testscore)
                        team2     = lastval[:-3]
                        score2    = testscore
                        vals      = []
                    except:
                        testscore = lastval[-2:]
                if not score2:
                    try:
                        testscore = int(testscore)
                        team2     = lastval[:-2]
                        score2    = testscore
                        vals      = []
                    except:
                        testscore = lastval[-1:]
                                        
                    
            team1 = tc.TeamConv(team1)
            team2 = tc.TeamConv(team2)
            
            sval={}
            sval['date']    = date
            sval['team1']   = team1
            try:
                sval['conf1']   = yearteams[team1]
            except:
                yearteams[team1] = "DivII"
                sval['conf1']   = yearteams[team1]
            sval['score1']  = score1
            sval['team2']   = team2
            try:
                sval['conf2']   = yearteams[team2]
            except:
                yearteams[team2] = "DivII"
                sval['conf2']   = yearteams[team2]
            sval['score2']  = score2
            sval['comment'] = comment
            yearscores.append(sval)


        historicaldata[key] = {}
        historicaldata[key]['teams']  = yearteams
        historicaldata[key]['scores'] = yearscores
        print '\t',key
        
    print '\tWrote',len(historicaldata),"scores to",histjsonfile
    json.dump(historicaldata, open(histjsonfile, "w"))

        

def getHistoricalTeams(basepath, force):
    years=range(1869, 2014)
    for year in years:
        yearid=str(year)
        url="http://wilson.engr.wisc.edu/rsfc/history/howell/cf"+yearid+"tms.txt"
        result = web.checkURL(url)
        if not result:
            continue
        
        if os.path.exists(basepath):
            savehtml=basepath+"/"+yearid+".html"
        else:
            print ' ---> No save path',basepath,'\t',yearid
            return False
        
        if os.path.exists(savehtml) and force == False:
            print ' ---> Save path exists, but force -> FALSE'
            return False
        
        result=web.getHTML(url, savehtml)
        if result:
            print ' --->',url,'  in  ',savehtml
        else:
            print " Did not download",url



def getHistoricalScores(basepath, force):
    years=range(1869, 2014)
    for year in years:
        yearid=str(year)
        url="http://wilson.engr.wisc.edu/rsfc/history/howell/cf"+yearid+"gms.txt"
        result = web.checkURL(url)
        if not result:
            continue
        
        if os.path.exists(basepath):
            savehtml=basepath+"/"+yearid+".html"
        else:
            print ' ---> No save path',basepath,'\t',yearid
            return False
        
        if os.path.exists(savehtml) and force == False:
            print ' ---> Save path exists, but force -> FALSE'
            return False
        
        result=web.getHTML(url, savehtml)
        if result:
            print ' --->',url,'  in  ',savehtml
        else:
            print " Did not download",url



def getScores(basepath, savehtml, yearid, force):
    url = 'http://www.jhowell.net/cf/scores/Sked2015.htm'
    result = web.checkURL(url)
    if result == False:
        print ' --->',url,' = ',result
        return result

    if os.path.exists(savehtml) and force == False:
        print ' ---> Save path exists, but force -> FALSE'
        return False
        
    result=web.getHTML(url, savehtml)
    if result:
        print ' --->',url,'  in  ',savehtml
    else:
        print " Did not download",url
        
    return True


def parseScores(txt):
    fdata = open(txt).readlines()
    fdata = [x.strip('\r\n') for x in fdata]

    yeardata={}

    i=0
    while i < len(fdata):
        line = fdata[i]
        tdata=[]
        if line.find("<table") != -1:
            while line.find("</table>") == -1:
                tdata.append(line)
                i += 1
                line = fdata[i]

            teamdata = parseTable(tdata)
            yeardata[teamdata['name']] = {}
            yeardata[teamdata['name']]['conf'] = teamdata['conf']
            yeardata[teamdata['name']]['games'] = teamdata['games']
        i += 1
    return yeardata



def parseTable(table):
    table = [x.replace("</tr>", "") for x in table]
    table = [x.replace("</td>", "") for x in table]

    teamdata={}
    teamdata["games"] = []
    
    table = table[1:]
    name,conf = getName(table[0])
    teamdata["name"] = name
    teamdata["conf"] = conf

    table = table[1:]

    for line in table:
        gamedata = getGame(line)
        if gamedata:
            teamdata["games"].append(gamedata)

    return teamdata
    f()

    
    
def getName(line):
    pos = line.find("<p align=\"center\">")
    if pos == -1:
        print "Could not parse:",line
        f()
    name = line[pos+18:]
    
    pos = name.rfind("(")
    conf = name[pos:]
    conf = conf.replace("(", "")
    conf = conf.replace(")", "")
    name = name[:pos-1]
    return name,conf


def getGame(line):
    line = line.replace("<td align=\"right\">", ":")
    line = line.replace("<td>", ":")
    line = line.replace("<tr>", "")
    linevals = line.split(":")
    site = None
    if len(linevals) == 8:
        try:
            dummy,date,day,home,opp,res,score,against = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    elif len(linevals) == 9:
        try:
            dummy,date,day,home,opp,res,score,against,site = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    elif len(linevals) == 10:
        try:
            dummy,date,day,home,opp,res,score,against,site,comment = linevals
        except:
            print "SPLIT ERROR:",line
            f()
    
    opp = opp.replace("*", "")
    if home == "vs.":
        home = 1
    elif home == "@":
        home = -1
    else:
        print "ERROR with Home:",home
        f()
    if site != None:
        home = 0

    if len(res) == 0:
        return None

    try:
        game={}
        game['date'] = date
        game['day'] = day
        game['home'] = home
        game['opponent'] = opp
        game['result'] = res
        game['score'] = int(score)
        game['against'] = int(against)
    except:
        print "DICT ERROR\t",date,day,home,opp,res,score,against
        f()
        

    return game
    
    


##########################################
#
# This is the output line to the csv file
#
##########################################
def writeLine(outfile, Date, Team1, Team2, Score1, Score2, Winner):
    lout=[]
    lout.append(Date)
    lout.append(Team1)
    lout.append(Team2)
    lout.append(Score1)
    lout.append(Score2)
    lout.append(Winner)
    lout=[str(x) for x in lout]
    outfile.write(",".join(lout))
    outfile.write("\n")
    


def writeFile(fname, yeardata):
    f=open(fname, "w")
    writeLine(f, "Date", "Team1", "Team2", "Score1", "Score2", "Winner")
    nline=0
    teams=sorted(yeardata.keys())
    for team in teams:
        games = yeardata[team]["games"]
        for game in games:
            if game['result'] == 'W':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            elif game['result'] == 'L':
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], game['opponent'])
            else:
                writeLine(f, game['date'], team, game['opponent'], game['score'], game['against'], team)
            nline += 1
    print "\tWrote",nline,"lines to",fname
    f.close()

In [ ]:


def Fix(name, size):
    newname=name
    while len(newname) < size:
        newname += " "
    return newname
    
def driveScore(result):
    res = result.title()
    if len(result) == 0:
        return 0
    if res == "Safety":
        return -2
    if res == "End Of Game Touchdown":
        return 6
    if res == "Touchdown" or res == "Touchdown Touchdown":
        return 7
    if res == "Fumble Touchdown" or res == "Fumble Return Touchdown" or res == "Punt Touchdown" or res == "Punt Return Touchdown" or res == "End Of Half Touchdown" or res == "Downs Touchdown":
        return -7
    if res == "Interception Touchdown":
        return -7
    if res == "Missed Fg Touchdown":
        return -7
    if res == "Field Goal":
        return 3
    noPoints=["Kickoff", "Interception", "Punt", "Missed Fg", "Missed Fg Touchdown", "Downs", "End Of Game", "Fumble", "End Of Half", "Possession (For Ot Drives)"]
    for nop in noPoints:
        #print res,nop
        if res == nop:
            return 0
    print '-> ['+result.title()+']'
    if any(word in noPoints for word in res):
        print "Something is here"
    f()
    return 0

def augmentScore(drives, d, team, augscore):
    drives[d]['runningscore'][team][1] += augscore
    return drives


def driveFixes(gameid, drives, teams):
    if gameid == "400756912": # Miami vs FAU
        print "Fixing drives for this game"
        drives[6]['team'] = teams['MIA']
        drives[6]['result'] = "Punt"
        print "\tDrive6 -> Punt"
        drives[7]['team'] = teams['FAU']
        drives[7]['result'] = "Fumble"        
        print "\tDrive7 -> Fumble"
        drives[8]['team'] = teams['MIA']
    if gameid == "400603869": # Texas A&M vs Ball St
        drives[20]['team'] = teams['BALL']
    if gameid == "400603936": # Texas A&M vs Ball St
        drives[9]['team'] = teams['TA&M']
    if gameid == "400756952":
        augmentScore(drives, 8, 1, 3)
    if gameid == "400787442":
#        augmentScore(drives, 2, 0, 3)
        augmentScore(drives, 2, 1, 7)
    if gameid == "400763533": # Iowa vs Wis
        drives[9]['team'] = teams['IOWA']
        drives[15]['team'] = teams['WIS']
    if gameid == "400763552": # Iowa vs MD
        drives[19]['team'] = teams['MD']
        drives[20]['team'] = teams['MD']
    if gameid == "400787296": # Iowa vs MD
        drives[9]['team'] = teams['SDSU']
    if gameid == "400763589":
        augmentScore(drives, 26, 0, 2)
    if gameid == "400763590":
        drives.pop(15)
    if gameid == "400763645":
        drives[30]['team'] = teams['MTSU']
        drives[30]['score'] = 7
        drives[32]['runningscore'] = drives[31]['runningscore']
        drives[32]['team'] = teams['MTSU']
        drives[32]['result'] = "Field Goal"
        drives[32]['score'] = 3
        drives[31] = drives[34]
        drives[31]['result'] = "Touchdown"
        drives[31]['team'] = teams['MRSH']
        drives[31]['score'] = 7
        drives[33]['runningscore'] = drives[32]['runningscore']
        drives[33]['result'] = "Missed Field Goal"
        drives[33]['team'] = teams['MRSH']
        drives[33]['score'] = 0
        drives.pop(34)
    return drives


    if gameid == "400757042":
        drives[30]['runningscore'][0][1] += 2
    if gameid == "400757061":
        drives[10]['runningscore'][0][1] += 7
        
    if gameid == "400756952":
        drives[8]['runningscore'][1][1] += 3
        drives[14]['runningscore'][0][1] += 7
        
    if gameid == "400756951":
        print "Fixing drives for this game"
        drives[19]['runningscore'][1][1] += 2
        print "\tDrive8 -> MIA ball"
    if gameid == "400756961":
        drives[21]['runningscore'][1][1] += 8
        
    if gameid == "400757064": augmentScore(drives, 7, 1, 7)
#    if gameid == "400763457": augmentScore(drives, 25, 0, 6)
#    if gameid == "400763470": augmentScore(drives, 15, 0, 7)
#    if gameid == "400763470": augmentScore(drives, 16, 1, 7)
#    if gameid == "400763472": augmentScore(drives, 19, 0, 6)
    return drives

def analyzeDriveSummary(gameid, drives, awayteam, hometeam):
    teams={}
    #print awayteam
    #print hometeam
    teams[int(awayteam[0])] = awayteam[1]
    teams[awayteam[1]] = int(awayteam[0])
    teams[int(hometeam[0])] = hometeam[1]
    teams[hometeam[1]] = int(hometeam[0])

    ## Some are just totally messed up and require hand coding:
    #print "Game ID -->",gameid
    drives=driveFixes(gameid, drives, teams)
    
    realDebug=False
    if realDebug:
        print '\t',Fix("Driving",10),'\t','# Running Score','\t\t\tResult'
        for i in range(len(drives)-1):
            drive=drives[i]
            drivingteam=teams[drive['team']]
        
            print i,'\t',Fix(drivingteam,10),'\t',drive['score'], drive['runningscore'],'\t',drive['summary'],'\t',drive['result']

    ## Check for an extra entry due to Punt Return
    extras=[]


    ## In case we need to remove a drive    
    for i in range(len(drives)-1):
        result=drives[i]['result']
        ryards=drives[i]['summary'][1]
        rscore=drives[i]['score']        
        rtime =60*drives[i]['summary'][2]+drives[i]['summary'][3]
        nextresult=drives[i+1]['result']
        nextryards=drives[i+1]['summary'][1]
        nextrscore=drives[i+1]['score']
        nextrtime =60*drives[i+1]['summary'][2]+drives[i+1]['summary'][3]
        
        if result.find("Touchdown") -1 and nextresult.find("Touchdown") != -1:
            if nextryards == 0 and rscore < 0 and nextrscore > 0 and nextrtime == 0:
                extras.append(i+1)
                print "====================================================="
                print "====================================================="
                print drives[i]
                print drives[i+1]," <--- Removing this guy."
                print "====================================================="
                print "====================================================="
    for extra in extras:
        drives.pop(extra)
        

    debugScore=False
    if debugScore: print '#\tPrev\tCurr\tDiff\tDrive\tNext\tDiffNext'
    for i in range(len(drives)-1):
        ## Offense score
        drivingteam=teams[drives[i]['team']]
        dscore=0
        teamid=-1
        
        if i == 0:
            prevscores=[ 0,0 ]
        else:
            prevscores=[ drives[i-1]['runningscore'][0][1], drives[i-1]['runningscore'][1][1] ]
        currscores=[ drives[i]['runningscore'][0][1], drives[i]['runningscore'][1][1] ]
        nextscores=[ drives[i+1]['runningscore'][0][1], drives[i+1]['runningscore'][1][1] ]
        diffscores=[0,0]
        diffscores[0]=currscores[0] - prevscores[0]
        diffscores[1]=currscores[1] - prevscores[1]
        diffnextscores=[0,0]
        diffnextscores[0]=nextscores[0] - currscores[0]
        diffnextscores[1]=nextscores[1] - currscores[1]
        
        if drivingteam == awayteam[1]:
            drivescore=[ drives[i]['score'],0 ]
        if drivingteam == hometeam[1]:
            drivescore=[ 0, drives[i]['score'] ]
        if debugScore: print i,'\t',prevscores,'\t',currscores,'\t',diffscores,'\t',drivescore,'\t',nextscores,'\t',diffnextscores,'\t',

        
        ## Away team scored
        if drivescore[0] > 0:
            teamid=0
            if diffscores[teamid] == 0:
                if debugScore: print "Away Score, but no update. Setting to",drives[i+1]['runningscore'][teamid][1],'from',drives[i]['runningscore'][teamid][1],
                drives[i]['runningscore'][teamid][1] = drives[i+1]['runningscore'][teamid][1]

        ## Home team gave up defensive points to away team
        if drivescore[1] < 0:
            teamid=0
            if diffscores[teamid] == 0:
                if debugScore: print "Away Score on defense, but no update. Setting to",drives[i+1]['runningscore'][teamid][1],"from",drives[i]['runningscore'][teamid][1]
                drives[i]['runningscore'][teamid][1] = drives[i+1]['runningscore'][teamid][1]

                
        ## Home team scored
        if drivescore[1] > 0:
            teamid=1
            if diffscores[teamid] == 0:
                if debugScore: print "Home Score, but no update. Setting to",drives[i+1]['runningscore'][teamid][1],'from',drives[i]['runningscore'][teamid][1],
                drives[i]['runningscore'][teamid][1] = drives[i+1]['runningscore'][teamid][1]

        ## Away team gave up defensive points to home team
        if drivescore[0] < 0:
            teamid=1
            if diffscores[teamid] == 0:
                if debugScore: print "Home Score on defense, but no update. Setting to",drives[i+1]['runningscore'][teamid][1],'from',drives[i]['runningscore'][teamid][1],
                drives[i]['runningscore'][teamid][1] = drives[i+1]['runningscore'][teamid][1]

        ## Strange thing that happens in OT
        if diffnextscores[0] != 0 and diffnextscores[1] != 0:
            if i == len(drives) - 2:
                if debugScore: print "Two scoring changes. Setting to",drives[i]['runningscore'],'from',drives[i+1]['runningscore']
                drives[i+1]['runningscore'] = drives[i]['runningscore']
        if debugScore: print ''


    #for i in range(len(drives)):
    #    print i,'\t',drives[i]['runningscore']

    ## Check for higher scores incorrectly given
    for t in range(2):
        i=0
        for i in range(len(drives)-1):
            currscore = drives[i]['runningscore'][t][1]
            #print i,"\tCurrent Score:",currscore
            j = i+1
            fix=False
            while j < len(drives) - 1:
                nextscore = drives[j]['runningscore'][t][1]
                if nextscore < currscore:
                    #print '\t',j,'\tNext Score:',nextscore
                    k=j-1
                    #print "\tFixing [",i,k,"] entries."
                    fix=True
                    break
                j += 1
            if fix:
                j=i
                while j <= k:
                    print '  Fixing Score on drive',j,'\t',
                    print '  ',drives[j]['runningscore'][t][1],' -> ',nextscore
                    drives[j]['runningscore'][t][1] = nextscore
                    j += 1
                
                
            #print i,'\t',drives[i]['runningscore'][t]

    nerr=0
    scores={}
    scores[awayteam[1]]=0
    scores[hometeam[1]]=0
    showResult=False
    
    if showResult: print i,'\t',Fix("Driving",10),'\t','# Running Score','\t\t','Team Score','\tResult'
    for i in range(len(drives)):
        drive=drives[i]
        drivingteam=teams[drive['team']]
        scoreval=drive['score']
        if drivingteam == awayteam[1]:
            newscore = drive['runningscore'][0][1]
            oteamscore = drive['runningscore'][1][1]
            oteam = hometeam[1]
        else:
            newscore = drive['runningscore'][1][1]
            oteamscore = drive['runningscore'][0][1]
            oteam = awayteam[1]
           

        ## Special for negative plays
        if scoreval < 0:
            if showResult: print "Turnover ->",drivingteam,' -> '
            if drivingteam == awayteam[1]:
                if showResult: print "\t home team scores",drive['runningscore'][1][1],'  ',scores[hometeam[1]]
                if drive['runningscore'][1][1] != scores[hometeam[1]]:
                    drivingteam = hometeam[1]
                newscore = drive['runningscore'][1][1]
                #oteamscore = drive['runningscore'][0][1]
                #oteam = awayteam[1]
            else:
                if showResult: print "\t home team scores",drive['runningscore'][0][1],'  ',scores[awayteam[1]]
                if drive['runningscore'][0][1] != scores[awayteam[1]]:
                    drivingteam = awayteam[1]
                newscore = drive['runningscore'][0][1]
                #oteamscore = drive['runningscore'][1][1]
                #oteam = hometeam[1]
            if showResult: print drivingteam,"Should be the one that got points."
            scoreval *= -1
            

        err=False
        diff=0
        if newscore != scores[drivingteam] + scoreval:
            err=True
            diff = scores[drivingteam] + scoreval - newscore
            result=drive['result']
            comment = ""
            ## Missed extra point or two-point conversion
            if diff < -10 and result == "Downs":
                scoreval = 0
                comment = "End of Game"
            if scoreval == 7 and diff == 1:
                scoreval = 6
                comment = "Missed Extra Point"
            if scoreval == 7 and diff == -1:
                scoreval = 8
                comment = "Two Point Conversion"
            if scoreval == 0 and diff == -3 and result == "End of Half":
                scoreval = 3
                comment = "Field Goal"
            if scoreval == 0 and diff == -3 and result == "Fumble":
                scoreval = 3
                comment = "Field Goal"
            if scoreval == 0 and diff == -3 and result == "Downs":
                scoreval = 3
                comment = "Field Goal"
            if scoreval == 0 and diff == -7 and result == "End of Half":
                scoreval = 7
                comment = "Touchdown"
            if scoreval == 0 and diff == -7 and result == "End of Game":
                scoreval = 7
                comment = "Touchdown"

            ## Check if we need to also fix the other teams score
            if scores[oteam] != oteamscore:
                oteamdiff = oteamscore - scores[oteam]
                if oteamdiff == 2:
                    comment += " Defensive PAT"
                    scores[oteam] = oteamscore
                else:
                    print "Something happened to",oteam,"so that they got",oteamdiff,"points."
                    
        
            ## Check if this fixes things
            if newscore == scores[drivingteam] + scoreval:
                err=False
                drives[i]['score'] = 6
                drives[i]['edit'] = 1
                drives[i]['result'] += " "+comment
            else:
                nerr += 1                
            
            scores[drivingteam] = scores[drivingteam] + scoreval
        else:
            err=False
            scores[drivingteam] = scores[drivingteam] + scoreval
        
        if showResult:
            print i,'\t',Fix(drivingteam,10),'\t',drive['score'], drive['runningscore'],'\t',scores[drivingteam],'\t',drive['summary'],'\t',drive['result'],
            if err:
                print '\t\t',err,'\t(',diff,')'
            else:
                print ''

    if nerr > 3:
        print "There were",nerr,"remaining errors in the drive summary"
        f()
    return drives
    

def parseDriveSummary(drive, debug):
    vals=drive.split("<span")
    res={}
    res['summary'] = None
    res['team'] = None
    res['result'] = None
    res['score'] = None
    res['runningscore']=[]
    
    for val in vals:        
        ## Headline
        hline="class=\"headline\">"
        if val.find(hline) != -1:
            #print val
            pos=val.find(hline)
            dresult=val[pos+17:-7]
            res['result'] = dresult
            res['score'] = driveScore(dresult)

            
        ## Get Score Info
        tname="class=\"team-name\">"
        if val.find(tname) != -1:
            pos1=val.find(tname)
            if pos1 == -1:
                print "Could not find current team name when parsing..."
            pos2=val.find("</span>", pos1+1)
            teamname=val[pos1+len(tname):pos2]
            
        ## Get Score Info
        tscore="class=\"team-score\">"
        if val.find(tscore) != -1:
            pos1=val.find(tscore)
            if pos1 == -1:
                print "Could not find current team score when parsing..."
            pos2=val.find("</span>", pos1+1)
            teamscore=int(val[pos1+len(tscore):pos2])
            res['runningscore'].append([teamname, teamscore])


        ## Details
        details="class=\"drive-details\">"
        if val.find(details) != -1:
            pos1=val.find(details)
            pos2=val.find("</span>")
            detail=val[pos1+len(details):pos2]
            dvals=detail.split(",")
            try:
                plays=dvals[0].replace("plays","")
                plays=plays.replace("play","")
                yards=dvals[1].replace("yards","")
                yards=yards.replace("yard","")
            except:
                print "Problem with drive (plays,yards) details"
                print dvals
                f()
                
            if len(dvals) == 3:
                try:
                    ptime=dvals[2].strip()
                    m,s=ptime.split(":")            
                except:
                    print "Problem with drive (time) details"
                    print dvals
                    f()
            else:
                m=0
                s=0                
                
            try:
                details=[int(plays), int(yards), int(m), int(s)]
            except:
                print "Problem with drive details: Making ints"
                print dvals
                f()
            res['summary'] = details

            
        ## Game title
        logo="class=\"home-logo\">"
        if val.find(logo) != -1:
            pos2=val.find(".png")
            pos1=val.find("/", pos2-5)
            if pos1 == -1 or pos2 == -1:
                continue
                print "Problem parsing logo in drive summary:",val
                f()
            teamnum = val[pos1+1:pos2]
            try:
                teamnum=int(teamnum)
            except:
                print "Problem parsing team number:",teamnum
                print "Original value:",val[pos1+1:pos2]
                print pos1
                print pos2
                f()
            res['team'] = teamnum

    for k,v in res.iteritems():
        if v == None:
            continue
            print "Could not parse drive"
            print 'drive -->',drive
            print '==============================='
            print res
            f()

    #analyzeDriveSummary(res)

    if res['team'] == None:
        return None
        
    
    return res


def updateTime(ptime, newval):
    minval=ptime[0]
    secval=ptime[1]

    minval += newval[0]
    secval += newval[1]
    if secval > 60:
        minval += 1
        secval -= 60
    return [minval,secval]

def getDown(down):
    if down == "1st":
        down=1
    elif down == "2nd":
        down=2
    elif down == "3rd":
        down=3
    elif down == "4th":
        down=4
    else:
        print "Unknown down",down
        f()
    return down

def parsePlays(gameid, teams, allplays, dsum):
    plays=[]
    currstate=None
    quarter=1

    showPlay=False
    try:
        teamnum,addr=tn.stripTeamNum(allplays[0])
    except:
        print "Problem with getting driving team!",allplays[0]
        return None,plays
        print dsum
        f()
    drivingteam = teams[teams[teamnum]]
    teamname = teams[teamnum]
    for p in range(len(allplays)-2):
        play = allplays[p]
        if allplays[p] == "<span class=\"post-play\">" and allplays[p+2] == "</span>":
            playresult = allplays[p+1]
            if playresult.find("NO PLAY") != -1:
                continue
            if showPlay: print '--->',playresult
            if currstate:
                currplay = [currstate, playresult]
                plays.append(currplay)
                currstate = None
            else:
                print "No information about the drive state!"
                f()

        if (allplays[p] == "<li class=\"end-quarter\">" or allplays[p] == "<li class=\"half-time\">") and allplays[p+2] == "<p>":
            driveinfo=[0,0,0]
            if showPlay: print '--->',driveinfo
            currstate=driveinfo


        if (allplays[p] == "<li class=\"\">" or allplays[p] == "<li class=\"video\">") and allplays[p+2] == "<p>":
            drivestate = allplays[p+1]
            drivestate = drivestate.replace("<h3>", "")
            drivestate = drivestate.replace("</h3>", "")
            if drivestate == "":
                drivestate = "Kickoff"
            vals=drivestate.split()
            driveinfo=[]
            if len(vals) == 1:
                driveinfo=[0,0,0]
            elif len(vals) == 6:
                down=getDown(vals[0])
                if vals[2] == "Goal":
                    togo="Goal"
                else:
                    togo=int(vals[2])
                if vals[4] == drivingteam:
                    dist=100 - int(vals[5])
                else:
                    dist=int(vals[5])
                driveinfo=[down,togo,dist]
            elif len(vals) == 5:
                if vals[0] == "and":
                    driveinfo=[0,"2 PT",int(vals[4])]
                elif vals[4] == "50":
                    down=getDown(vals[0])
                    if vals[2] == "Goal":
                        togo="Goal"
                    else:
                        togo=int(vals[2])
                    dist=50
                    driveinfo=[down,togo,dist]
                else:
                    print "Can not parse drive state!",drivestate
                    f()                        
            else:
                print "Can not parse drive state!",drivestate
                f()
            if showPlay: print '--->',drivestate,'\t\t',driveinfo
            currstate=driveinfo
                
    return teamname,plays

def parsePlayByPlay(gameid, pbp, team1data, team2data, debug):
    j=0
    ndrives=0
    drives=[]
    driveplays=[]
    awayteam=[team1data[1], team1data[3]]
    hometeam=[team2data[1], team2data[3]]
        
    teams={}
    teams[int(team1data[1])] = tc.TeamConv(team1data[0])
    teams[int(team2data[1])] = tc.TeamConv(team2data[0])
    teams[team1data[3]] = tc.TeamConv(team1data[0])
    teams[team2data[3]] = tc.TeamConv(team2data[0])
    teams[tc.TeamConv(team1data[0])] = team1data[3]
    teams[tc.TeamConv(team2data[0])] = team2data[3]
    while j < len(pbp):
        line = pbp[j]
        
               
        ## Game title
        drive="<span class=\"drive-details\">"
        dsum = None
        if line.find(drive) != -1 and False:
            continue
        
            dsum = parseDriveSummary(line, debug)
            if debug:
                print "Drive[",ndrives,'] -->',dsum
            if dsum == None:
                j += 1
                continue
            drives.append(dsum)
            ndrives += 1
            
        flag="<ul class=\"drive-list\">"
        if line.find(flag) != -1:
            k=j+1
            try:
                while pbp[k].find("</ul>") == -1:
                    k += 1
            except:
                k=len(pbp)
            teamname,plays=parsePlays(gameid, teams, pbp[j:k], dsum)
            if teamname == None or len(plays) == 0:
                j += 1
                continue
            plays.insert(0, teamname)
            driveplays.append(plays)
            if debug: print len(plays),'\t',plays                

        j += 1

#    if len(drives) != len(driveplays):
#        print "Found",len(drives),"drive summaries and",len(driveplays),"drive plays."
#        f()
        
    #drives = analyzeDriveSummary(gameid, drives, awayteam, hometeam)

    if len(driveplays) == 0:
        print "No drives found for this game."
        return None
        

    summary={}
    summary[tc.TeamConv(team1data[0])] = []
    summary[tc.TeamConv(team2data[0])] = []
    
    for i in range(len(driveplays)):
        team=driveplays[i][0]
        if summary.get(team) == None:
            print "Error paring drive plays for",team
            print summary.keys()
            f()
        plays = driveplays[i][1:]
        plays.insert(0, i)
        
        summary[team].append(plays)
        
    return summary

In [ ]:

##############################################################################
#
#
# parseMatchup()
#
#
##############################################################################

def getAttr(mdata, key, i):
    j=i
    attrs=[]
    while j < len(mdata):
        #print j,'\t',mdata[j]
        if j > i + 20:
            f()
        value=None
        if mdata[j].find("</tr>") != -1:
            break
        if mdata[j].find("td>") == -1:
            value=mdata[j].strip()
            #print '--->',j,value
            attrs.append(value)            
        j += 1

    if len(attrs) == 4:
        attrs.pop(0)
    name=attrs[0]
    val1=attrs[1]
    val2=attrs[2]
    itype=int    
    if val1.find("-") != -1 and val2.find("-") != -1: itype = str
    if val1.find(".") != -1 and val2.find(".") != -1: itype = float
    if val1.find(":") != -1 and val2.find(":") != -1: itype = complex
    
    if itype == int:
        val1=int(val1)
        val2=int(val2)
    if itype == float:
        val1=float(val1)
        val2=float(val2)
    if itype == str:
        vals=val1.split('-')
        if len(vals[0]) == 0:
            val1 = int(val1)
        else:
            vals=[int(x) for x in val1.split("-")]
            val1 = [vals[0], vals[1]]
            
        vals=val2.split('-')
        if len(vals[0]) == 0:
            val2 = int(val2)
        else:
            vals=[int(x) for x in val2.split("-")]
            val2 = [vals[0], vals[1]]
    if itype == complex:
        vals=[int(x) for x in val1.split(":")]
        val1 = [vals[0], vals[1]]
        vals=[int(x) for x in val2.split(":")]
        val2 = [vals[0], vals[1]]
        
    #print 'attrs->',attrs
    #print val1,val2    
    retval=[name, val1, val2]    
    
    return retval


def parseMatchup(mdata, team1data, team2data, debug):
    teams={}
    teams[int(team1data[1])] = tc.TeamConv(team1data[0])
    teams[int(team2data[1])] = tc.TeamConv(team2data[0])
    teams[team1data[3]] = tc.TeamConv(team1data[0])
    teams[team2data[3]] = tc.TeamConv(team2data[0])
    summary=[]
    #print len(mdata)

    teamorder=[None,None]
    keys=["firstDowns", "thirdDownEff", "fourthDownEff", 
          "totalYards", "netPassingYards",
          "yardsPerPass", "completionAttempts", "interceptions",
          "rushingYards", "rushingAttempts", "yardsPerRushAttempt",
          "totalPenaltiesYards", "turnovers", "fumblesLost",
          "interceptions", "possessionTime"]
    values={}
    for key in keys:
        values[key] = None



    for i in range(len(mdata)):
        line=mdata[i]
        if line == "<th>Matchup</th>":
            j=i+1
            while j < len(mdata):
                if mdata[j].find("<img src=") != -1:
                    teamnum,addr=tn.stripTeamNum(mdata[j])
                    if teamorder[0] == None:
                        teamorder[0] = teams[teamnum]
                        j+=1
                        continue
                    if teamorder[1] == None:
                        teamorder[1] = teams[teamnum]
                        break
                j +=1 

        for key in keys:
            if line.find("data-stat-attr=\""+key+"\"") != -1:
                attr=getAttr(mdata, key, i)
                values[key] = attr
                #print key,'\t',attr
                break

    if teamorder[0] == None or teamorder[1] == None:
        return None

    retvals={}
    retvals[teamorder[0]] = {}
    retvals[teamorder[1]] = {}
    for k,v in values.iteritems():
        if v == None:
            retvals[teamorder[0]][k] = None
            retvals[teamorder[1]][k] = None
        else:
            retvals[teamorder[0]][v[0]] = v[1]
            retvals[teamorder[1]][v[0]] = v[2]
    return retvals

In [ ]:


    
##############################################################################
#
#
# parseTeamData()
#
#
##############################################################################    
def parseTeamData(line, teams, showData):
    pos=line.find("<thead><tr>")
    if pos == -1:
        print "Problem parseing team data",line
        f()
        
    ## Get name
    info=line[:pos]
    info=info.replace("</caption>", "")
    ipos=info.rfind(">")
    info=info[ipos+1:]
    dataname=info
    teamname=None
    for team,tconv in teams.iteritems():
        if dataname.find(team) != -1:
            teamname = tconv
            break
    
    if teamname == None:
        print "Could not find team in",dataname
        print "Expected:",teams
        f()
    #print 'Data ->',dataname
    
    ## Get info
    line=line[pos:]
    line=line.replace("<thead>", "")
    #print 'Full line --->',line
    #print ''
    
    lines=line.split("<tr")
    if len(lines[0]) == 0:
        lines.pop(0)
        
    for l in range(len(lines)):
        if lines[l][0] == '>':
            lines[l] = lines[l][1:]
        lines[l] = lines[l].strip()
        #print '\t',l,'\t',lines[l]
    #print ''
        
    keys=[]
    headers=lines[0].split("<th")
    headers=[x.replace("class=\"", "") for x in headers]
    headers=[x.replace("</th>", "") for x in headers]
    headers=[x.strip() for x in headers]
    headers=[x for x in headers if x != ""]
    for h in range(len(headers)):
        pos=headers[h].find("\">")
        if pos != -1:
            headers[h] = headers[h][:pos]
        keys.append(headers[h])
        #print '\t',h,'\t',headers[h]
    #print ''

    values={}
    if showData: print 'keys --->',keys
    lines.pop(0)
    if showData: print lines
    if showData: print ''
    teamvals={}
    noInfo=False
    
    for lne in lines:
        lvals=lne.split("</td")

        vals=[]        
        for k in range(len(keys)):
            if lvals[k].find("class=\""+keys[k]+"\"") == -1:
                if lvals[k].find("No") == -1:
                    print "Problem parsing box score"
                    print keys[k]
                    print keys
                    print lvals
                    f()
                else:
                    noInfo=True
                    break
            
            lvals[k] = lvals[k].replace("</a>", "")
            lvals[k] = lvals[k].strip()
            pos = lvals[k].rfind(">")
            val = lvals[k][pos+1:]
            vals.append(val)
            #print keys[k],'\t',val

        if not noInfo:         
            teamvals[vals[0]] = vals[1:]
            if showData: print '\t',vals[0], teamvals[vals[0]]


    if noInfo:
        teamvals["None"] = []
        for i in range(len(keys)-1): teamvals["None"].append('0')
            

    keys=keys[1:]        
    for name in teamvals.keys():
        val = teamvals[name]
        data={}
        for i in range(len(keys)):
            if val[i].find(".") != -1: data[keys[i]] = float(val[i])
            elif val[i].find("/") != -1: data[keys[i]] = [int(x) for x in val[i].split("/")]
            else: 
                try:
                    data[keys[i]] = int(val[i])
                except:
                    data[keys[i]] = str(val[i])
        teamvals[name] = data
        
    try:
        field = dataname.replace(teamname, "").strip()
    except:
        print "Problem parsing data field name",dataname
        f()
        

    if showData: print teamname,'\t',field,'\t',teamvals
    return teamname,field,teamvals


    
    
##############################################################################
#
#
# parseBoxScore()
#
#
##############################################################################
def parseBoxScore(bdata, team1data, team2data, debug):
    teams={}
    teams[int(team1data[1])] = tc.TeamConv(team1data[0])
    teams[int(team2data[1])] = tc.TeamConv(team2data[0])
    teams[team1data[3]] = tc.TeamConv(team1data[0])
    teams[team2data[3]] = tc.TeamConv(team2data[0])

    values={}
    values[tc.TeamConv(team1data[0])] = {}
    values[tc.TeamConv(team2data[0])] = {}
    
    tconvs={}
    for team in values.keys():
        tconvs[team] = team
        invconv = tc.InvTeamConv(team)
        if invconv == team:
            continue
        tconvs[invconv] = team
        
    for team in values.keys():
        if team.find("State") != -1:
            tstate = team.replace("State", "").strip()
            if tconvs.get(tstate) == None:
                tconvs[tstate]= team
    
    showData=debug
    
    for i in range(len(bdata)):
        line=bdata[i]
        if line.find("class=\"boxscore-tabs game-package-box-score ") != -1:
            vals=line.split("<div class=\"col column-")
            for val in vals:
                if val.find(".png") != -1:
                    teamnum,addr = tn.stripTeamNum(val)
                else:
                    continue
#                try:
#                    print val
#                    teamnum,addr = tn.stripTeamNum(val)
#                except:
#                    print val
#                    continue
                if showData: print ''
                if showData: print teamnum
                teamname,field,teamdata=parseTeamData(val, tconvs, showData)
                if values.get(teamname) == None:
                    print "Did not recognize team",teamname
                    print "Should be",values.keys()
                    f()
                values[teamname][field] = teamdata
                if showData: print teamname,'\t',field,'\t',teamdata
                if showData: print ''

    if showData: print values
        
    return values

In [ ]:
# This Python file uses the following encoding: utf-8
import argparse

import os, sys
import glob
import requests
from collections import Counter
import json
import datetime

import parsePlayByPlay
import parseScoringSummary
import parseMatchup
import parseBoxScore
import parseTeam
import parseScores
import parseSFref

import TeamConv as tc
import teamNum as tn

reload(sys)
sys.setdefaultencoding('utf8')


def f(): raise Exception("Found exit()")
    
def Fix(name, size):
    newname=name
    while len(newname) < size:
        newname += " "
    return newname



def TestTime(time1, time2):
    #print time1 - time2
    oneday=datetime.timedelta(days=1)
    if time1 == time2 or time1 == time2 + oneday or time1 == time2 - oneday:
        return True
    return False

def getdTimeYear(date, year):
    m,d = date.split('/')
    if int(m) < 10:
        dateyear="0"+m
    else:
        dateyear=m
    if int(d) < 10:
        dateyear+="/0"+d
    else:
        dateyear="/"+d
    dateyear = date + "/"+str(year)
    try:
        tformat = "%m/%d/%Y"
        gametime   = datetime.datetime.strptime(dateyear, tformat)
    except:
        print "Could not convert date:",dateyear
        f()
    return gametime

def getdTime(date):
    try:
        tformat = "%B %d, %Y"
        gametime   = datetime.datetime.strptime(date, tformat)
    except:
        print "Could not convert date:",date
        f()
    return gametime


    




##############################################################################
#
#
# parseTitle()
#
#
##############################################################################
def parseTitle(game, debug):
    print game
    vals=game.split(" - ")
    if len(vals) != 4:
        print "Can not parse title:",game
        f()

    try:
        team1,team2=vals[0].split(" vs. ")
        date=vals[2]
    except:
        print "Problem with parsing title:",vals
        f()

    return team1,team2,date






##############################################################################
#
#
# parseLogo()
#
#
##############################################################################
def parseLogo(logo, debug):
    team1=None
    team2=None
    teamnum=-1
    if debug: print "=============== logo ==============="
    for div in logo.split("<div"):
        if debug: print "\t->  ",div
        
        if teamnum == -1:
            teamnum,logoaddr=tn.getTeamNum(div)
        if teamnum != -1:
            if debug: print '--->',logoaddr,'<---'
        
        teamname="class=\"team-name\""
        if div.find(teamname) != -1:
            pos1=div.find("<span class=\"long-name\">")
            pos2=div.find("</span>", pos1+1)
            team=div[pos1+24:pos2]
            if debug: print '---> Team Long:  ',team,'<---'
            
            abrvtxt="<span class=\"abbrev\" title=\""+team+"\">"
            pos1=div.find(abrvtxt)
            pos2=div.find("</span>", pos1+1)
            abrv=div[pos1+len(abrvtxt):pos2]
            if debug: print '---> Team Short: ',abrv,'<---'
            

            if team1 == None:
                team1=[team, teamnum, logoaddr, abrv]
            else:
                team2=[team, teamnum, logoaddr, abrv]
            teamnum=-1

    if debug: print team1
    if debug: print team2

    if team1 == None or team2 == None:
        print "Could not find teams:",team1,team2
        f()

    return team1, team2
    f()






##############################################################################
#
#
# compareGames()
#
#
##############################################################################
def compareGames(fbsgames, fbsscores, teamnums):
    ks=fbsscores.keys()
    for k in ks:
        v = fbsscores[k]
        team1=k
        print "=====",Fix(k,25),"====="


        test=False
        if test:
            vals=["Buffalo"]
            for val in vals:
                for k2,v2 in fbsgames.iteritems():                
                    teams=v2.keys()
                    for team in teams:
                        if team.find(val) != -1:
                            print k2," vs ".join(teams)
            f()
                        #exit()

        testgames={}
        for k2,v2 in fbsgames.iteritems():                
            teams=v2.keys()
            for team in teams:
                if team1 == tc.TeamConv(team):
                    testgames[k2]=v2
                    break


        ngames = len(testgames)
        games=v['games']
        if ngames < 1:
            print ""
            print ""
            print "=====",k,"=====",
            print "  ---> FBS Games:",ngames
            f()
        

        for i in range(len(games)):
            game=games[i]
            fbsscore = game

            dtime = getdTimeYear(game['date'], 2015)
            team2 = game['opponent']

            gamekey = None
            fbsgame = None
            for key,v2 in testgames.iteritems():
                side = v2.keys()[0]
                dtime2 = getdTime(v2[side]['date'])
                if TestTime(dtime, dtime2):
                    gamekey = key
                    if fbsgames.get(gamekey):
                        fbsgame = fbsgames[gamekey]
                    else:
                        print "Error in key!",gamekey
                        f()
                    break
                
            if gamekey == None or fbsgame == None:
                print "  --->",team1,'vs.',team2,' \t on',game['date'],'\t',
                print "Could not find fbs game key."
                for key,v2 in testgames.iteritems():
                    sides = v2.keys()
                    dtime2 = getdTime(v2[sides[0]]['date'])
                    print key,'\t',sides[0],sides[1],dtime2
                f()

            fbsscores[k]['games'][i]['teamdata'] = fbsgame
            print '\t',Fix(game['date'], 5),'\t',Fix(team2,25),'\t',gamekey

    return fbsscores
    


def testStats(fullgames):
    for k,v in fullgames.iteritems():
        print ''        
        print "=============================================================="
        team=k
        games=v['games']
        for game in games:
            date=game['date']
            opp = game['opponent']
            score=game['score']
            oppscore=game['against']
            print '\t',date,'\t',score,'\t',oppscore,'\t --> ',team,' vs.',opp,
            details=game['play-by-play']
            try:
                teamdetails=details[team]
                oppdetails=details[opp]
            except:
                print "Error with key in fullgames{} in testStats()"
                print opp,details
                f()

            if teamdetails['summary']['score'] != score or oppdetails['summary']['score'] != oppscore:
                print "ERROR"
                print '\t\t',teamdetails['summary']['score'],'\t',oppdetails['summary']['score']
                print teamdetails
                print oppdetails
                f()
            else:
                print ""
        print ''        
        print "=============================================================="
        
    f()



def parseGame(gameid, gamehtml, fbsteams, debug, checkformissing):
    fdata = open(gamehtml).readlines()
    fdata = [x.strip('\r\n') for x in fdata]
    fdata = [x.strip('\t') for x in fdata]
    
    matchuphtml=gamehtml.replace("Plays", "Matchup")
    if matchuphtml == gamehtml:
        print "Problem parsing matchup html",gamehtml
        f()
    mdata=[]
    if os.path.exists(matchuphtml):
        mdata = open(matchuphtml).readlines()
        mdata = [x.strip('\r\n') for x in mdata]
        mdata = [x.strip('\t') for x in mdata]
    else:
        return "NoScore", None
    
    boxscorehtml=matchuphtml.replace("Matchup", "BoxScore")
    if boxscorehtml == matchuphtml:
        print "Problem parsing box score html",matchuphtml
        f()
    bdata=[]
    if os.path.exists(boxscorehtml):
        bdata = open(boxscorehtml).readlines()
        bdata = [x.strip('\r\n') for x in bdata]
        bdata = [x.strip('\t') for x in bdata]
    else:
        return "NoScore", None
    i=0
    
    gdata={}
    gdata["title"] = None
    gdata["logo"] = None
    gdata["plays"] = []
    while i < len(fdata):
        line=fdata[i]
        
        ## Game title
        gametitle="<meta name=\"title\" content=\""
        if line.find(gametitle) != -1 and gdata["title"] == None:
            gdata["title"] = line[len(gametitle):-3]

            

        ## Team logo
        logo="<img class=\"team-logo\""
        if line.find(logo) != -1 and gdata["logo"] == None:
            gdata["logo"] = line



        ## Game play-by-play
        pbp="<div id=\"gamepackage-play-by-play\" data-module=\"playbyplay\">"
        if line.find(pbp) != -1:
            while line.find("<div id=\"gamepackage-scoring-wrap\"") == -1:
                gdata["plays"].append(line)
                i += 1
                try:
                    line=fdata[i]
                except:
                    break



        ## Scoring summary
        scoresum="<div class=\"scoring-summary\">"
        if line.find(scoresum) != -1:
            gdata["scores"] = line

        i += 1

    if checkformissing:
        if gdata.get('scores') == None:
            return "NoScore",None
        else:            
            return "Good",None


    team1A,team2A,date=parseTitle(gdata["title"], debug)    
    if fbsteams.get(tc.TeamConv(team1A)) == None and fbsteams.get(tc.TeamConv(team2A)) == None:
        if debug: print "No FBS team here. Moving on."
        return "NoFBSTeam",None
    
    #print '--->',date,'<---'
    gametime = getdTime(date)
    if gametime > datetime.datetime.today():
        if debug: print "Game has not happened yet"
        return "NotPlayedYet",None


    team1Data,team2Data=parseLogo(gdata["logo"], debug)
    if team1Data[0] != team1A or team2Data[0] != team2A:
        print "Problem with teams"
        print team1Data[0],'<-->',team1A
        print team2Data[0],'<-->',team2A
        f()
        
    #print "---> Plays Info",len(gdata["plays"]),"<---"
    drives = parsePlayByPlay.parsePlayByPlay(gameid, gdata["plays"], team1Data, team2Data, debug)

    scores=[]
    if gdata.get('scores'):
        scores=parseScoringSummary.parseScoringSummary(gameid, gdata['scores'], team1Data, team2Data, debug)
    else:
        scores=None
    
    ##  Check for matchup information
    matchup=parseMatchup.parseMatchup(mdata, team1Data, team2Data, debug)
    #print matchup
    

    ##  Check for boxscore information
    boxscore=parseBoxScore.parseBoxScore(bdata, team1Data, team2Data, debug)
    #print boxscore

    gamedetails = {}
    team1Data[0] = tc.TeamConv(team1Data[0])
    team2Data[0] = tc.TeamConv(team2Data[0])
    gamedetails[team1Data[0]] = {}
    gamedetails[team2Data[0]] = {}
    print '\t'," vs. ".join(gamedetails.keys())

    gamedetails[team1Data[0]]['logo'] = team1Data[1:]
    gamedetails[team1Data[0]]["date"] = date
    gamedetails[team2Data[0]]['logo'] = team2Data[1:]
    gamedetails[team2Data[0]]["date"] = date
    
    gamedetails[team1Data[0]]['drives'] = None
    gamedetails[team1Data[0]]['scores'] = None
    gamedetails[team1Data[0]]["teamstats"] = None
    gamedetails[team1Data[0]]["indivstats"] = None
    
    gamedetails[team2Data[0]]['drives'] = None
    gamedetails[team2Data[0]]['scores'] = None
    gamedetails[team2Data[0]]["teamstats"] = None
    gamedetails[team2Data[0]]["indivstats"] = None
    
    
    if matchup != None:       
        if matchup.get(team1Data[0]) == None:
            print "Could not find",team1Data[0],"in matchup",matchup.keys()
            f()
        if matchup.get(team2Data[0]) == None:
            print "Could not find",team2Data[0],"in matchup",matchup.keys()
            f()
        gamedetails[team1Data[0]]["teamstats"] = matchup[team1Data[0]]
        gamedetails[team2Data[0]]["teamstats"] = matchup[team2Data[0]]
        
    if boxscore != None:
        if boxscore.get(team1Data[0]) == None:
            print "Could not find",team1Data[0],"in matchup",boxscore.keys()
            f()
        if boxscore.get(team2Data[0]) == None:
            print "Could not find",team2Data[0],"in matchup",boxscore.keys()
            f()
        gamedetails[team1Data[0]]["indivstats"] = boxscore[team1Data[0]]
        gamedetails[team2Data[0]]["indivstats"] = boxscore[team2Data[0]]

    if scores:
        if scores.get(team1Data[0]) == None:
            print "Could not find",team1Data[0],"in score",scores.keys()
            f()
        if scores.get(team2Data[0]) == None:
            print "Could not find",team2Data[0],"in score",scores.keys()
            f()
        gamedetails[team1Data[0]]['scores'] = scores[team1Data[0]]
        gamedetails[team2Data[0]]['scores'] = scores[team2Data[0]]
    
    if drives:
        if drives.get(team1Data[0]) == None:
            print "Could not find",team1Data[0],"in drives",drives.keys()
            f()
        if drives.get(team2Data[0]) == None:
            print "Could not find",team2Data[0],"in drives",drives.keys()
            f()
        gamedetails[team1Data[0]]['drives'] = drives[team1Data[0]]
        gamedetails[team2Data[0]]['drives'] = drives[team2Data[0]]
        


    return "Good",gamedetails



############################################################
##
##  Main()
##
############################################################
def main(args):
    yearid="2015"
    webbase="http://scores.espn.go.com"
    
    basepath     = os.path.abspath("/Users/tgadfort/Dropbox/Football")
    gamebase     = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games")
    teambase     = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games/Teams")
    schedulebase = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games/Teams/Schedule")
    spteampath   = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games/Teams/SFref")
    spyearpath   = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games/Teams/SFref/Historical")
    scorebase    = os.path.abspath("/Users/tgadfort/Dropbox/Football/Scores")
    gamesdir     = os.path.relpath("Games/Plays")
    datadir      = os.path.abspath("/Users/tgadfort/Dropbox/Football/Data")
    sprefdir     = os.path.abspath("/Users/tgadfort/Dropbox/Football/SPref")


    historicalscorebase = scorebase
    historicalteambase  = os.path.abspath("/Users/tgadfort/Dropbox/Football/Games/Teams/Historical")
    historicaljsonfile  = os.path.abspath(datadir + "/" + "HistoricalTeamScores.json")
    
    
    fbsgamesfile   = os.path.abspath(datadir + "/" + yearid+"Data.json")
    teamdbfile     = os.path.abspath(datadir + "/" + "TeamDB.json")
    

    scorehtmlfile  = os.path.abspath(scorebase + "/" + yearid + ".html")
    scorejsonfile  = os.path.abspath(datadir + "/" + yearid + "Scores.json")
    scorecsvfile   = os.path.abspath(datadir + "/" + yearid + "Scores.csv")
    

    fullgamefile   = os.path.abspath(datadir + "/" + "Merged" + yearid + ".json")
    teamdb=json.load(open(teamdbfile))
    fbsteams=teamdb['names']
    

    sprefhtml             = os.path.abspath(sprefdir + "/" + "index.html")
    sprefteamsjsonfile    = os.path.abspath(datadir + "/" + "SPrefTeams.json")
    sprefgamelogsjsonfile = os.path.abspath(datadir + "/" + "SPrefGameLogs.json")
    sprefteamyearjsonfile = os.path.abspath(datadir + "/" + "SPrefTeamYear.json")


    if args.spref:
        parseSFref.getSFref(sprefhtml, args.force)
        parseSFref.parseSFref(sprefhtml, sprefteamsjsonfile)
        parseSFref.getSFrefTeams(spteampath, sprefteamsjsonfile, args.force)
        parseSFref.parseSFrefTeams(spteampath, sprefteamsjsonfile, args.force)
        parseSFref.getSFrefTeamYears(spyearpath, sprefteamsjsonfile, args.force)
        parseSFref.parseSFrefTeamYears(spyearpath, sprefteamyearjsonfile, args.force)
        parseSFref.parseSFrefTeamGameLog(spyearpath, sprefgamelogsjsonfile, args.force)
        return

    #################################
    # If we need to get historical scores
    #################################
    if args.gethistoricalscores:
#        parseScores.getHistoricalScores(historicalscorebase, args.force)
#        parseScores.getHistoricalTeams(historicalteambase, args.force)
        parseScores.parseHistoricalScores(historicalscorebase, 
                                          historicalteambase,
                                          historicaljsonfile)
        return

    #################################
    # If we need to merge scores and data
    #################################
    if args.merge:
        fbsgames  = json.load(open(fbsgamesfile))
        fbsscores = json.load(open(scorejsonfile))
        fullgames = compareGames(fbsgames, fbsscores, teamdb)
        print "Writing",len(fullgames),"full games to",fullgamefile
        json.dump(fullgames, open(fullgamefile, "w"))
        return



    #################################
    # If we need to download scores
    #################################
    if args.getscores:
        scoreid = yearid
        parseScores.getScores(scorebase, scorehtmlfile, scoreid, args.force)
        scores = parseScores.parseScores(scorehtmlfile)
        if scores:
            parseScores.writeFile(scorecsvfile, scores)
            json.dump(scores, open(scorejsonfile, "w"))
            print "\tWrote",len(scores),"lines to",scorejsonfile
        return



    #################################
    # If we need to redownload teams
    #################################
    if args.getgame:
        gameid = args.getgame[0]
        parseTeam.getGame(gameid, gamebase, test=False, force=True)
        return



    #################################
    # If we need to redownload teams
    #################################
    if args.getteams:
        for k in teamdb['nums'].keys():
            result = parseTeam.getTeam(k, teambase, test=False, force=args.force)
            parseTeam.getHistoricalSchedule(schedulebase, k, args.force)
        return



    #################################
    # If we need to redownload games
    #################################
    if args.getgames:
        for k in teamdb['nums'].keys():
            result = parseTeam.getTeamHistoricalGames(schedulebase, k)
            for gameid, gamenum in result.iteritems():
                gameresult = parseTeam.getGame(gameid, gamebase, test=False, force=args.force)
            continue
            
            result = parseTeam.getTeamGames(gamebase, webbase, k)
            for gameid, gamehtml in result.iteritems():
                result = parseTeam.getGame(gameid, gamehtml, gamebase, test=False, force=args.force)

        return



    debug=False
    games=glob.glob(gamesdir+"/*.html")
    gamedb={}
    fbsgames={}
    missing=[]
    for g in range(len(games)):
        print "==================="
        print "Game",g+1,'/',len(games),'\t',
        game=games[g]
        key = os.path.basename(game)
        key = key.split(".")[0]
        print key,'  ',
        gamestatus,gameresults = parseGame(key, game, fbsteams, debug, args.missing)
        if args.missing:
            if gamestatus != "Good":
                missing.append([gamestatus, key])
            continue
        if gamestatus != "Good":
            print "\t-->",gamestatus
            missing.append([gamestatus, key])
            continue
        if gameresults == None:
            print "\t-->",gamestatus
            continue
    
        #print gameresults
        if gamedb.get(key):
            print "Already parsed this game [",key,"]!"
            continue
        fbsgames[key] = gameresults
        #print gameresults
        teams=gameresults.keys()
        if fbsteams.get(tc.TeamConv(teams[0])) and fbsteams.get(tc.TeamConv(teams[1])):
            gamedb[key] = gameresults
        else:   
            print "Not keeping game for later downloads by gameDB because one team is not FBS"
            
    print "Done parsing",len(games),"games."
    print "FBS Games:",len(fbsgames)
    print "Writing",len(fbsgames),"games to",fbsgamesfile
    json.dump(fbsgames, open(fbsgamesfile, "w"))



    

    #################################
    # If we need to get missing games
    #################################
    print '----- Missing -----'
    for game in missing:        
        print '\t--->',game
    print '-------------------'
    
    if args.missing:
        for game in missing:
            gamestatus = game[0]
            gameid = game[1]
            if gamestatus == "NoScore":
                result = parseTeam.getGame(gameid, gamebase, test=False, force=args.force)
        return
    
    
 

##################################################################
##
## main
##
##################################################################
if __name__ == "__main__":
    parser = argparse.ArgumentParser()
    #parser.add_argument('-get-games', dest='getgames', nargs=1, help='Base directory name.')
    parser.add_argument('-spref', action="store_true", dest='spref', help='Get SFrefence data.')
    parser.add_argument('-merge', action="store_true", dest='merge', help='Merge scores and game data.')
    parser.add_argument('-get-game', nargs=1, dest='getgame', help='Get missing games.')
    parser.add_argument('-get-games', action="store_true", dest='getgames', default=False, help='Get missing games.')
    parser.add_argument('-get-teams', action="store_true", dest='getteams', default=False, help='Get missing games.')
    parser.add_argument('-missing', action="store_true", dest='missing', default=False, help='Look for missing games.')
    parser.add_argument('-force', action="store_true", dest='force', default=False, help='Force downloads.')
    parser.add_argument('-get-scores', action="store_true", dest='getscores', default=False, help='Get only scores.')
    parser.add_argument('-get-historical-scores', action="store_true", dest='gethistoricalscores', default=False, help='Get historical scores.')
    args = parser.parse_args()

    main(args)
    